In [418]:
import numpy as np
import os
import pandas as pd
import arcpy

# Import the required ArcGIS API for Python modules
import arcgis
from arcgis.gis import GIS
gis = arcgis.GIS()
from arcgis.geoanalytics import manage_data

from IPython.display import display, Markdown

In [419]:
dirWork         = os.getcwd()
year            = '2019'
dirInput        = os.path.join(dirWork, r'data\data' + year                    )
dirIntermediate = os.path.join(dirWork, r'intermediate\intermediate' + year    )
dirResults      = os.path.join(dirWork, r'results\results' + year              )

print("Working Directory: "      + dirWork        )
print("Input Directory: "        + dirInput       )
print("Intermediate Directory: " + dirIntermediate)
print("Results Directory: "      + dirResults     )

Working Directory: c:\Users\cday\Documents\projects\Census-LEHD-Commute-Patterns
Input Directory: c:\Users\cday\Documents\projects\Census-LEHD-Commute-Patterns\data\data2019
Intermediate Directory: c:\Users\cday\Documents\projects\Census-LEHD-Commute-Patterns\intermediate\intermediate2019
Results Directory: c:\Users\cday\Documents\projects\Census-LEHD-Commute-Patterns\results\results2019


In [420]:
dirIntermediate

'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\intermediate\\intermediate2019'

In [421]:
#input filenames
fname_CityTownship_csv        = os.path.join(dirInput, 'citytownship.csv'                                         )
fname_CityTownship_shp        = os.path.join(dirInput, 'Municipalities_Township' + r'\Municipalities_Township.shp') 
fname_LEHDCommutePatterns_csv = os.path.join(dirInput, 'lehd_at_blockgroup_level' + year + '.csv'                 )
fname_UofUManualAllocation_csv= os.path.join(dirInput, '490351108004_Manual_Allocation.csv'                       )
fname_BlockGroups_shp         = os.path.join(dirInput, 'tl_2020_49_bg' + r'\tl_2020_49_sd_bg.shp'                    )
fname_Counties_AGRC_shp       = os.path.join(dirInput, 'Utah_County_Boundaries-shp' + r'\Counties.shp'            )
fname_LEHDCommutePatterns_csv

#intermediate
fname_CityTownshipCounty_BlockGroups_shp = os.path.join(dirIntermediate, 'citytownshipcounty_blockgroup_intersect.shp')
fname_CityTownshipWCodes_shp             = os.path.join(dirIntermediate, 'Municipalities_Townships_withCodes.shp')
fname_CountyWCodes_shp                   = os.path.join(dirIntermediate, 'Counties_withCodes.shp')
fname_CityTownshipWCodesUnionCounty_shp  = os.path.join(dirIntermediate, 'Municipalities_Townships_withCodes_Counties.shp')
fname_CityTownshipCountyWCodes_shp       = os.path.join(dirIntermediate, 'Municipalities_Townships_Counties_withCodes.shp')

#display(dirIntermediate)

#results geodatabase

fname_CityTownshipJSON = os.path.join(dirResults, "citytownshipdata.json")

gdb_LEHDCommutePatterns = "LEHDCommutePatterns.gdb"
fname_LEHDCommutePatterns_gdb = os.path.join(dirResults, gdb_LEHDCommutePatterns)

fname_CityTownshipWCodes = os.path.join(fname_LEHDCommutePatterns_gdb, 'Municipalities_and_Townships')
#fname_CityTownshipCounty = os.path.join(fname_LEHDCommutePatterns_gdb, 'Municipalities_Townships_Counties')

fname_BlockGroupsWCommutePatterns_Number = os.path.join(fname_LEHDCommutePatterns_gdb, 'LEHD_BlockGroup_CommutePatterns_Number')
fname_BlockGroupsWCommutePatterns_Percent_SA = os.path.join(fname_LEHDCommutePatterns_gdb, 'LEHD_BlockGroup_CommutePatterns_Percent_SelectedArea')
fname_BlockGroupsWCommutePatterns_Percent_MU = os.path.join(fname_LEHDCommutePatterns_gdb, 'LEHD_BlockGroup_CommutePatterns_Percent_MapUnit')

fname_TractsWCommutePatterns_Number = os.path.join(fname_LEHDCommutePatterns_gdb, 'LEHD_Tract_CommutePatterns_Number')
fname_TractsWCommutePatterns_Percent_SA = os.path.join(fname_LEHDCommutePatterns_gdb, 'LEHD_Tract_CommutePatterns_Percent_SelectedArea')
fname_TractsWCommutePatterns_Percent_MU = os.path.join(fname_LEHDCommutePatterns_gdb, 'LEHD_Tract_CommutePatterns_Percent_MapUnit')

fname_SDWCommutePatterns_Number = os.path.join(fname_LEHDCommutePatterns_gdb, 'LEHD_SD_CommutePatterns_Number')
fname_SDWCommutePatterns_Percent_SA = os.path.join(fname_LEHDCommutePatterns_gdb, 'LEHD_SD_CommutePatterns_Percent_SelectedArea')
fname_SDWCommutePatterns_Percent_MU = os.path.join(fname_LEHDCommutePatterns_gdb, 'LEHD_SD_CommutePatterns_Percent_MapUnit')

fname_CitiesWCommutePatterns_Number = os.path.join(fname_LEHDCommutePatterns_gdb, 'LEHD_City_CommutePatterns_Number')
fname_CitiesWCommutePatterns_Percent_SA = os.path.join(fname_LEHDCommutePatterns_gdb, 'LEHD_City_CommutePatterns_Percent_SelectedArea')
fname_CitiesWCommutePatterns_Percent_MU = os.path.join(fname_LEHDCommutePatterns_gdb, 'LEHD_City_CommutePatterns_Percent_MapUnit')

fname_Counties = os.path.join(fname_LEHDCommutePatterns_gdb, 'Counties')

def deleteIfExists(obj):
    if arcpy.Exists(obj): arcpy.Delete_management(obj)

#if results geodatabase doesn't exist, create it
print("Checking if " + fname_LEHDCommutePatterns_gdb + " exists...")
if not arcpy.Exists(os.path.join(dirResults, gdb_LEHDCommutePatterns)):
    print("Creating " + fname_LEHDCommutePatterns_gdb + "...")
    arcpy.management.CreateFileGDB(dirResults, gdb_LEHDCommutePatterns)
else:
    print(gdb_LEHDCommutePatterns + " exists...")

#print(AnalysisAreasInput)

Checking if c:\Users\cday\Documents\projects\Census-LEHD-Commute-Patterns\results\results2019\LEHDCommutePatterns.gdb exists...
LEHDCommutePatterns.gdb exists...


# Create Cities/Townships Feature Class with 3-Digit Code and County FIPS

In [422]:
#read in city/township shapefile, SHORTDESC is common field between this and CODE3 dataset
sdf_CityTownship = pd.DataFrame.spatial.from_featureclass(fname_CityTownship_shp)
display(sdf_CityTownship)

FID COUNTYNBR                              NAME  COUNTYSEAT  \
0      0        03                            Newton           0   
1      1        12                            Eureka           0   
2      2        29                        Huntsville           0   
3      3        27                        Springdale           0   
4      4        23                       Grantsville           0   
..   ...       ...                               ...         ...   
253  253        18          COPPERTON METRO TOWNSHIP           0   
254  254        18             KEARNS METRO TOWNSHIP           0   
255  255        18              MAGNA METRO TOWNSHIP           0   
256  256        18  EMIGRATION CANYON METRO TOWNSHIP           0   
257  257        18         WHITE CITY METRO TOWNSHIP           0   

             SHORTDESC    UPDATED   FIPS  ENTITYNBR SALESTAXID  IMSCOLOR  \
0               NEWTON 2018-09-19  54550     3100.0        047         2   
1               EUREKA 2018-09-19  24080     3010.0        009         2   
2           HUNTSVILLE 2014-10-15  37060     3030.0        019         4   
3           SPRINGDALE 2014-10-15  71840     3100.0        023         2   
4          GRANTSVILLE 2020-06-05  31120     3010.0        023         2   
..                 ...        ...    ...        ...        ...       ...   
253          Copperton 2016-12-27  15720        0.0                    0   
254             Kearns 2016-12-27  40470        0.0                    0   
255              Magna 2018-11-14  47290        0.0                    0   
256  Emigration Canyon 2016-12-27  22875        0.0                    0   
257         White City 2016-12-27  84050        0.0                    0   

               MINNAME  POPLASTCEN  POPLASTEST     GNIS  \
0                              801         813  1430705   
1                              693         695  1437974   
2           Huntsville         602         638  1428949   
3           Springdale         569         609  1432867   
4                             9152       11568  1428338   
..                 ...         ...         ...      ...   
253          Copperton         822         835            
254             Kearns       35769       36330            
255              Magna       26513       26949            
256  Emigration Canyon        1568        1592            
257         White City        5686        5768            

                                   GlobalID  SHAPE_Leng  SHAPE_Area  \
0    {1C320704-F3E4-4D4F-A542-F6FFE3C36900}    0.071275    0.000240   
1    {E1F6AAAD-E49E-4820-A270-D3E7C2131A80}    0.100706    0.000395   
2    {E9A934D8-FE13-4A6D-925E-73A9988E3F17}    0.126158    0.000246   
3    {E6E76C45-D141-47DF-9C96-D3D46F15A2B9}    0.193621    0.001208   
4    {5F5B6417-7EF9-49B5-A689-CBF42953DC9D}    0.772545    0.010742   
..                                      ...         ...         ...   
253  {B3F64B90-565B-44B4-8C7B-87000672B734}    0.067294    0.000086   
254  {75A0B23A-775B-44DC-BCCA-4E504BF9E548}    0.185692    0.001277   
255  {28F85E1F-72D3-43E5-BBF4-F85CC28898D5}    0.756349    0.010342   
256  {29B91C07-4DE5-4395-8337-6E13304256BB}    0.350202    0.005034   
257  {2C41A42F-87EE-4D97-AED2-6619D82F72AF}    0.147366    0.000241   

                                                 SHAPE  
0    {"rings": [[[-112.00138477499996, 41.855487523...  
1    {"rings": [[[-112.09987515199998, 39.957670251...  
2    {"rings": [[[-111.76117535999998, 41.253396941...  
3    {"rings": [[[-112.97934207899999, 37.197581387...  
4    {"rings": [[[-112.37537669199997, 40.593511564...  
..                                                 ...  
253  {"rings": [[[-112.09934129299995, 40.562296682...  
254  {"rings": [[[-111.98660579699998, 40.667567316...  
255  {"rings": [[[-112.10619664199999, 40.691640141...  
256  {"rings": [[[-111.74338063899995, 40.818777216...  
257  {"rings": [[[-111.86273107599999, 40.581548957...  

[258 rows x 18 columns]

In [423]:
#rename METRO TOWNSHIPs to match CODE3 dataset
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'WHITE CITY METRO TOWNSHIP'       , 'SHORTDESC'] = "WHITE CITY METRO TOWNSHIP"
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'EMIGRATION CANYON METRO TOWNSHIP', 'SHORTDESC'] = "EMIGRATION CANYON METRO TOWNSHIP"
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'COPPERTON METRO TOWNSHIP'        , 'SHORTDESC'] = "COPPERTON METRO TOWNSHIP"
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'MAGNA METRO TOWNSHIP'            , 'SHORTDESC'] = "MAGNA METRO TOWNSHIP"
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'KEARNS METRO TOWNSHIP'           , 'SHORTDESC'] = "KEARNS METRO TOWNSHIP"

#give townships a better name
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'WHITE CITY METRO TOWNSHIP'       , 'NAME'] = "White City"
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'EMIGRATION CANYON METRO TOWNSHIP', 'NAME'] = "Emigration Canyon"
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'COPPERTON METRO TOWNSHIP'        , 'NAME'] = "Copperton"
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'MAGNA METRO TOWNSHIP'            , 'NAME'] = "Magna"
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'KEARNS METRO TOWNSHIP'           , 'NAME'] = "Kearns"

In [424]:
#read in township codes data
df_CityTownshipCodes = pd.read_csv(fname_CityTownship_csv)

#consolidate Hideout
df_CityTownshipCodes = df_CityTownshipCodes.loc[df_CityTownshipCodes.SHORTDESC != 'HIDEOUT (WASATCH)']
df_CityTownshipCodes = df_CityTownshipCodes.loc[df_CityTownshipCodes.SHORTDESC != 'HIDEOUT (SUMMIT)']

# get wfrc city/townships only
wfrc_towns  = ["AFK","ALA","ALP","BDL","BGM","BNT","BRT","CDF","CEN","CHA","CHL","CLF","CLI","CMT","COA","CWH","DAN","DRA","EAG","ELK","EMT","FAR","FCS","FFD","FRR","FTH","GLA","GOS","GRL","HAR","HDT","HDT","HEB","HER","HGH","HNF","HOL","HOO","HVL","IND","INT","KAY","KMS","KMT","LAY","LEH","LIN","MAP","MID","MLC","MMT","MRG","MSL","MUR","MWY","NOG","NSL","OGD","OKL","ORM","PAY","PGR","PLN","PRK","PRY","PVO","PVW","ROY","RVD","RVT","SAN","SAQ","SAR","SFK","SJC","SLC","SLM","SOG","SPV","SSL","SUN","SWE","SYR","TAY","TOO","UIN","VIN","WAT","WBG","WDL","WEB","WHT","WHV","WIL","WJC","WPT","WVC","WXC"]
df_CityTownshipCodes = df_CityTownshipCodes[df_CityTownshipCodes['CODE3'].isin(wfrc_towns)].reset_index(drop=True)

df_CityTownshipCodes

SHORTDESC CODE3
0          AMERICAN FORK   AFK
1                   ALTA   ALA
2                 ALPINE   ALP
3      BLUFFDALE (SL CO)   BDL
4    BLUFFDALE (UTAH CO)   BDL
..                   ...   ...
96          WILLARD CITY   WIL
97      WEST JORDAN CITY   WJC
98            WEST POINT   WPT
99      WEST VALLEY CITY   WVC
100     WOODS CROSS CITY   WXC

[101 rows x 2 columns]

In [425]:
#join spatial data frame to data frame with codes using SHORTDESC field as key between two
sdf_CityTownshipWCodes = pd.DataFrame.merge(sdf_CityTownship, df_CityTownshipCodes, on='SHORTDESC')

#export to intermediate location so that it can be used in dissolve function later (to remove cities that span counties)
sdf_CityTownshipWCodes.spatial.to_featureclass(fname_CityTownshipWCodes_shp, sanitize_columns=False)

display(sdf_CityTownshipWCodes)

FID COUNTYNBR               NAME  COUNTYSEAT  \
0      2        29         Huntsville           0   
1      4        23        Grantsville           0   
2      5        18          Bluffdale           0   
3      7        18           Herriman           0   
4     13        18       Taylorsville           0   
..   ...       ...                ...         ...   
96   253        18          Copperton           0   
97   254        18             Kearns           0   
98   255        18              Magna           0   
99   256        18  Emigration Canyon           0   
100  257        18         White City           0   

                            SHORTDESC    UPDATED   FIPS  ENTITYNBR SALESTAXID  \
0                          HUNTSVILLE 2014-10-15  37060     3030.0        019   
1                         GRANTSVILLE 2020-06-05  31120     3010.0        023   
2                   BLUFFDALE (SL CO) 2018-11-15  06810     3020.0        019   
3                       HERRIMAN TOWN 2019-11-22  34970     3035.0        060   
4                   TAYLORSVILLE CITY 2014-09-15  75360     3105.0        142   
..                                ...        ...    ...        ...        ...   
96           COPPERTON METRO TOWNSHIP 2016-12-27  15720        0.0              
97              KEARNS METRO TOWNSHIP 2016-12-27  40470        0.0              
98               MAGNA METRO TOWNSHIP 2018-11-14  47290        0.0              
99   EMIGRATION CANYON METRO TOWNSHIP 2016-12-27  22875        0.0              
100         WHITE CITY METRO TOWNSHIP 2016-12-27  84050        0.0              

     IMSCOLOR            MINNAME  POPLASTCEN  POPLASTEST     GNIS  \
0           4         Huntsville         602         638  1428949   
1           2                           9152       11568  1428338   
2           4                           7693       14699  1425844   
3           1                          22018       44877  1428675   
4           4       Taylorsville       59989       60192  1433206   
..        ...                ...         ...         ...      ...   
96          0          Copperton         822         835            
97          0             Kearns       35769       36330            
98          0              Magna       26513       26949            
99          0  Emigration Canyon        1568        1592            
100         0         White City        5686        5768            

                                   GlobalID  SHAPE_Leng  SHAPE_Area  \
0    {E9A934D8-FE13-4A6D-925E-73A9988E3F17}    0.126158    0.000246   
1    {5F5B6417-7EF9-49B5-A689-CBF42953DC9D}    0.772545    0.010742   
2    {E52CE320-1532-4A57-8DB9-DFA819FBB85B}    0.303290    0.002868   
3    {3E78F48D-80B9-44DA-AC9F-836A7B4F1B8E}    0.617524    0.005943   
4    {3ADD19D5-EF23-4257-8048-E355AE283BC6}    0.303444    0.002991   
..                                      ...         ...         ...   
96   {B3F64B90-565B-44B4-8C7B-87000672B734}    0.067294    0.000086   
97   {75A0B23A-775B-44DC-BCCA-4E504BF9E548}    0.185692    0.001277   
98   {28F85E1F-72D3-43E5-BBF4-F85CC28898D5}    0.756349    0.010342   
99   {29B91C07-4DE5-4395-8337-6E13304256BB}    0.350202    0.005034   
100  {2C41A42F-87EE-4D97-AED2-6619D82F72AF}    0.147366    0.000241   

                                                 SHAPE CODE3  
0    {"rings": [[[-111.76117535999998, 41.253396941...   HVL  
1    {"rings": [[[-112.37537669199997, 40.593511564...   GRL  
2    {"rings": [[[-111.94473146099995, 40.497759794...   BDL  
3    {"rings": [[[-112.06032590299998, 40.481954434...   HER  
4    {"rings": [[[-111.92081851599994, 40.685958404...   TAY  
..                                                 ...   ...  
96   {"rings": [[[-112.09934129299995, 40.562296682...   CMT  
97   {"rings": [[[-111.98660579699998, 40.667567316...   KMT  
98   {"rings": [[[-112.10619664199999, 40.691640141...   MMT  
99   {"rings": [[[-111.74338063899995, 40.818777216...   EMT  
100  {"rings": [[[-1

In [426]:
#dissolve by code, due to some cities spanning counties and having multiple records in codes and/or munis/townships
deleteIfExists(fname_CityTownshipWCodes)
arcpy.management.Dissolve(fname_CityTownshipWCodes_shp, fname_CityTownshipWCodes, ['CODE3'], [['NAME','FIRST'], ['COUNTYNBR','FIRST']])

sdf_CityTownshipWCodes = pd.DataFrame.spatial.from_featureclass(fname_CityTownshipWCodes)
sdf_CityTownshipWCodes = sdf_CityTownshipWCodes.rename(columns={"code3":"CODE3", "FIRST_name":"FIRST_NAME", "FIRST_countynbr":"FIRST_COUNTYNBR"})

display(sdf_CityTownshipWCodes)

OBJECTID CODE3        FIRST_NAME FIRST_COUNTYNBR  \
0          1   AFK     American Fork              25   
1          2   ALA              Alta              18   
2          3   ALP            Alpine              25   
3          4   BDL         Bluffdale              18   
4          5   BGM      Brigham City              02   
..       ...   ...               ...             ...   
92        93   WIL           Willard              02   
93        94   WJC       West Jordan              18   
94        95   WPT        West Point              06   
95        96   WVC  West Valley City              18   
96        97   WXC       Woods Cross              06   

                                                SHAPE  
0   {"rings": [[[-111.77435121873373, 40.353624868...  
1   {"rings": [[[-111.59946851855727, 40.577431980...  
2   {"rings": [[[-111.75455302160464, 40.479513910...  
3   {"rings": [[[-111.9704071902396, 40.5008379065...  
4   {"rings": [[[-112.01898409573937, 41.535781784...  
..                                                ...  
92  {"rings": [[[-112.02999503963935, 41.391465965...  
93  {"rings": [[[-112.00475852158849, 40.638664299...  
94  {"rings": [[[-112.10779328273378, 41.143687479...  
95  {"rings": [[[-111.9626132723846, 40.7260972067...  
96  {"rings": [[[-111.89260269236036, 40.866220107...  

[97 rows x 5 columns]

In [427]:
df_CityTownship_NameCode = sdf_CityTownshipWCodes[['FIRST_NAME','CODE3','FIRST_COUNTYNBR']].copy()
df_CityTownship_NameCode = df_CityTownship_NameCode.sort_values(by=['FIRST_NAME'])

df_CityTownship_NameCode.columns = ('NAME','CODE3','COUNTYNBR')

display(df_CityTownship_NameCode)

#df_CityTownship_NameCode.to_json(os.path.join(dirResults, "citytownshipdata.json"),orient='records')
#export after adding workers and residents columns from data

NAME CODE3 COUNTYNBR
2             Alpine   ALP        25
1               Alta   ALA        18
0      American Fork   AFK        25
3          Bluffdale   BDL        18
5          Bountiful   BNT        06
..               ...   ...       ...
95  West Valley City   WVC        18
90        White City   WHT        18
92           Willard   WIL        02
88    Woodland Hills   WDL        25
96       Woods Cross   WXC        06

[97 rows x 3 columns]

In [428]:
#explicit definition of county for cross-county cities
df_CityTownship_NameCode.loc[((df_CityTownship_NameCode['CODE3'] == 'BDL')), 'COUNTYNBR'] = '18'
df_CityTownship_NameCode.loc[((df_CityTownship_NameCode['CODE3'] == 'DRA')), 'COUNTYNBR'] = '18'
df_CityTownship_NameCode.loc[((df_CityTownship_NameCode['CODE3'] == 'HDT')), 'COUNTYNBR'] = '26'
df_CityTownship_NameCode.loc[((df_CityTownship_NameCode['CODE3'] == 'PRK')), 'COUNTYNBR'] = '22'

#read in county dataset
sdf_CountiesAGRC = pd.DataFrame.spatial.from_featureclass(fname_Counties_AGRC_shp)
sdf_CountiesAGRC['FIPS'   ] = sdf_CountiesAGRC['FIPS'].astype(int)
sdf_CountiesAGRC['zCOFIPS'] = 'z' + sdf_CountiesAGRC['FIPS'].astype(str).str.zfill(2) #add 'z' instead of 0, so that columns names won't start with number, and so sorts at end
sdf_CountiesAGRC['CO_NAME'] = sdf_CountiesAGRC['NAME'].str.title() + ' County'
display(sdf_CountiesAGRC)

#join by COUNTYNBR to get CO_FIPS
df_CityTownship_NameCode_wCOFIPS = pd.DataFrame.merge(df_CityTownship_NameCode,sdf_CountiesAGRC,on='COUNTYNBR')
display(df_CityTownship_NameCode_wCOFIPS)


df_CityTownship_NameCode = df_CityTownship_NameCode_wCOFIPS[['NAME_x','CODE3','zCOFIPS']]
df_CityTownship_NameCode.columns = ('NAME','CODE3','zCOFIPS')

display(df_CityTownship_NameCode)

FID  OBJECTID COUNTYNBR     ENTITYNBR  ENTITYYR        NAME  FIPS  \
0     0         1        03  2.010031e+09    2010.0       CACHE     5   
1     1         2        07  2.010071e+09    2010.0    DUCHESNE    13   
2     2         3        06  2.010061e+09    2010.0       DAVIS    11   
3     3         4        14  2.010141e+09    2010.0     MILLARD    27   
4     4         5        26  2.010261e+09    2010.0     WASATCH    51   
5     5         6        02  2.010021e+09    2010.0   BOX ELDER     3   
6     6         7        29  2.010291e+09    2010.0       WEBER    57   
7     7         8        12  2.010121e+09    2010.0        JUAB    23   
8     8         9        20  2.010201e+09    2010.0     SANPETE    39   
9     9        10        27  2.010271e+09    2010.0  WASHINGTON    53   
10   10        11        10  2.010101e+09    2010.0       GRAND    19   
11   11        12        17  2.010171e+09    2010.0        RICH    33   
12   12        13        04  2.010041e+09    2010.0      CARBON     7   
13   13        14        05  2.010051e+09    2010.0     DAGGETT     9   
14   14        15        01  2.010011e+09    2010.0      BEAVER     1   
15   15        16        21  2.010211e+09    2010.0      SEVIER    41   
16   16        17        09  2.010091e+09    2010.0    GARFIELD    17   
17   17        18        23  2.010231e+09    2010.0      TOOELE    45   
18   18        19        22  2.010221e+09    2010.0      SUMMIT    43   
19   19        20        16  2.010161e+09    2010.0       PIUTE    31   
20   20        21        24  2.010241e+09    2010.0      UINTAH    47   
21   21        22        11  2.010111e+09    2010.0        IRON    21   
22   22        23        08  2.010081e+09    2010.0       EMERY    15   
23   23        24        28  2.010281e+09    2010.0       WAYNE    55   
24   24        25        19  2.006191e+09    2006.0    SAN JUAN    37   
25   25        26        15  2.010151e+09    2010.0      MORGAN    29   
26   26        27        13  2.010131e+09    2010.0        KANE    25   
27   27        28        18  2.010181e+09    2010.0   SALT LAKE    35   
28   28        29        25  2.010251e+09    2010.0        UTAH    49   

   STATEPLANE  POP_LASTCE  POP_CURRES                                GlobalID  \
0       North      112656      128289  {59BEE5FF-00D6-414A-8CD9-3B9CF5FA25FB}   
1     Central       18607       19938  {AAE112BD-8D24-46EE-98CD-6689B87A14D1}   
2       North      306479      355481  {66DDE457-AF53-4B6D-9A7D-25F29FCCF626}   
3     Central       12503       13188  {DE7E933D-7233-4FBE-8D0C-5E0826EF05D7}   
4     Central       23530       34091  {1BAA04F5-D976-4917-BBF2-BE9C0F868C55}   
5       North       49975       56046  {2F4FBEBE-32DB-4A2D-A6D1-277679BDF193}   
6       North      231236      260213  {7F2E8776-C886-4F23-9D40-B861B1FB5391}   
7     Central       10246       12017  {7A6D2476-AE18-48E8-820B-CE97B805879F}   
8     Central       27822       30939  {323210BE-8E14-49FE-96FE-1C571E744993}   
9       South      138115      177556  {A13328EF-DD99-45B8-897C-A9FE2418E7CA}   
10    Central        9225        9754  {6246AFC5-101A-4D5B-8355-1910ED7CF71D}   
11      North        2264        2483  {0362BF2D-2424-4C0C-AF74-7FC49DDAF467}   
12    Central       21403       20463  {F9F3A18C-023D-42E3-AB18-3168BA3C9446}   
13      North        1059         950  {A1C114E4-6F14-452C-8157-F199752416CE}   
14      South        6629        6710  {14543D4C-CB01-4B05-AB19-DA399ABFD0ED}   
15    Central       20802       21620  {C9ECC2C2-7282-4B4E-9B47-D53CBB880820}   
16      South        5172        5051  {579769A4-4616-4A9B-92F0-9CFB2AEFD176}   
17    Central       58218       72259  {197FEA12-E2B4-4514-9A3C-963D8244A1E3}   
18      North       36324       42145  {EE2B9872-701C-470A-A300-1DB609C67F24}   
19      South        1556        1479  {E4A8F0F6-AE75-4DAA-AF72-298AC8274F7D}   
20    Central       32588       35734  {8FAEFFAA-95C1-404A-8862-3CCC91A0C412}   
21      South       46163      

NAME_x CODE3 COUNTYNBR  FID  OBJECTID     ENTITYNBR  ENTITYYR  \
0           Alpine   ALP        25   28        29  2.010251e+09    2010.0   
1    American Fork   AFK        25   28        29  2.010251e+09    2010.0   
2       Cedar Fort   CDF        25   28        29  2.010251e+09    2010.0   
3      Cedar Hills   CHL        25   28        29  2.010251e+09    2010.0   
4   Eagle Mountain   EAG        25   28        29  2.010251e+09    2010.0   
..             ...   ...       ...  ...       ...           ...       ...   
92      West Haven   WHV        29    6         7  2.010291e+09    2010.0   
93     Grantsville   GRL        23   17        18  2.010231e+09    2010.0   
94          Tooele   TOO        23   17        18  2.010231e+09    2010.0   
95          Morgan   MRG        15   25        26  2.010151e+09    2010.0   
96       Santaquin   SAQ        12    7         8  2.010121e+09    2010.0   

    NAME_y  FIPS STATEPLANE  POP_LASTCE  POP_CURRES  \
0     UTAH    49    Central      516564      636235   
1     UTAH    49    Central      516564      636235   
2     UTAH    49    Central      516564      636235   
3     UTAH    49    Central      516564      636235   
4     UTAH    49    Central      516564      636235   
..     ...   ...        ...         ...         ...   
92   WEBER    57      North      231236      260213   
93  TOOELE    45    Central       58218       72259   
94  TOOELE    45    Central       58218       72259   
95  MORGAN    29      North        9469       12124   
96    JUAB    23    Central       10246       12017   

                                  GlobalID FIPS_STR  COLOR4  SHAPE_Leng  \
0   {33E4105B-187C-4C0B-8F1C-D091F44BEFB1}    49049       3    5.073804   
1   {33E4105B-187C-4C0B-8F1C-D091F44BEFB1}    49049       3    5.073804   
2   {33E4105B-187C-4C0B-8F1C-D091F44BEFB1}    49049       3    5.073804   
3   {33E4105B-187C-4C0B-8F1C-D091F44BEFB1}    49049       3    5.073804   
4   {33E4105B-187C-4C0B-8F1C-D091F44BEFB1}    49049       3    5.073804   
..                                     ...      ...     ...         ...   
92  {7F2E8776-C886-4F23-9D40-B861B1FB5391}    49057       1    2.973528   
93  {197FEA12-E2B4-4514-9A3C-963D8244A1E3}    49045       2    6.105650   
94  {197FEA12-E2B4-4514-9A3C-963D8244A1E3}    49045       2    6.105650   
95  {08CCA506-439E-4F9E-8302-50A6B9468EF5}    49029       2    2.862360   
96  {7A6D2476-AE18-48E8-820B-CE97B805879F}    49023       4    6.802360   

    SHAPE_Area                                              SHAPE zCOFIPS  \
0     0.586227  {'rings': [[[-111.59404929699997, 40.577075300...     z49   
1     0.586227  {'rings': [[[-111.59404929699997, 40.577075300...     z49   
2     0.586227  {'rings': [[[-111.59404929699997, 40.577075300...     z49   
3     0.586227  {'rings': [[[-111.59404929699997, 40.577075300...     z49   
4     0.586227  {'rings': [[[-111.59404929699997, 40.577075300...     z49   
..         ...                                                ...     ...   
92    0.183659  {'rings': [[[-111.92092166399999, 41.138676415...     z57   
93    2.003307  {'rings': [[[-112.44788691599996, 41.017030151...     z45   
94    2.003307  {'rings': [[[-112.44788691599996, 41.017030151...     z45   
95    0.169567  {'rings': [[[-111.51438719299995, 40.803633660...     z29   
96    0.926379  {'rings': [[[-112.17814760399995, 40.011304953...     z23   

          CO_NAME  
0     Utah County  
1     Utah County  
2     Utah County  
3     Utah County  
4     Utah County  
..            ...  
92   Weber County  
93  Tooele County  
94  Tooele County  
95  Morgan County  
96    Juab County  

[97 rows x 20 columns]

NAME CODE3 zCOFIPS
0           Alpine   ALP     z49
1    American Fork   AFK     z49
2       Cedar Fort   CDF     z49
3      Cedar Hills   CHL     z49
4   Eagle Mountain   EAG     z49
..             ...   ...     ...
92      West Haven   WHV     z57
93     Grantsville   GRL     z45
94          Tooele   TOO     z45
95          Morgan   MRG     z29
96       Santaquin   SAQ     z23

[97 rows x 3 columns]

# Add Rows for County Level Totals

In [429]:
#read in csv with commute pattern data
df_LEHDCommutePatterns = pd.read_csv(fname_LEHDCommutePatterns_csv)

In [430]:
#get all column codes for summing
dfColCodes = df_LEHDCommutePatterns.loc[1:1,'AFK_h':'TTL_w'].T #get all columns from AFK_x through TTL_y
dfColCodes = dfColCodes.reset_index()

#convert to list for ease of calcs in future steps
dColCodes = dfColCodes['index'].values.tolist()
dColCodes

['AFK_h',
 'ALA_h',
 'ALP_h',
 'BDL_h',
 'BGM_h',
 'BNT_h',
 'BRT_h',
 'CDF_h',
 'CEN_h',
 'CHA_h',
 'CHL_h',
 'CLF_h',
 'CLI_h',
 'CMT_h',
 'COA_h',
 'CWH_h',
 'DAN_h',
 'DRA_h',
 'EAG_h',
 'ELK_h',
 'EMT_h',
 'FAR_h',
 'FCS_h',
 'FFD_h',
 'FRR_h',
 'FTH_h',
 'GLA_h',
 'GOS_h',
 'GRL_h',
 'HAR_h',
 'HDT_h',
 'HEB_h',
 'HER_h',
 'HGH_h',
 'HNF_h',
 'HOL_h',
 'HOO_h',
 'HVL_h',
 'IND_h',
 'INT_h',
 'KAY_h',
 'KMS_h',
 'KMT_h',
 'LAY_h',
 'LEH_h',
 'LIN_h',
 'MAP_h',
 'MID_h',
 'MLC_h',
 'MMT_h',
 'MRG_h',
 'MSL_h',
 'MUR_h',
 'MWY_h',
 'NOG_h',
 'NSL_h',
 'OGD_h',
 'OKL_h',
 'ORM_h',
 'PAY_h',
 'PGR_h',
 'PLN_h',
 'PRK_h',
 'PRY_h',
 'PVO_h',
 'PVW_h',
 'ROY_h',
 'RVD_h',
 'RVT_h',
 'SAN_h',
 'SAQ_h',
 'SAR_h',
 'SFK_h',
 'SJC_h',
 'SLC_h',
 'SLM_h',
 'SOG_h',
 'SPV_h',
 'SSL_h',
 'SUN_h',
 'SWE_h',
 'SYR_h',
 'TAY_h',
 'TOO_h',
 'UIN_h',
 'VIN_h',
 'WAT_h',
 'WBG_h',
 'WDL_h',
 'WEB_h',
 'WHT_h',
 'WHV_h',
 'WIL_h',
 'WJC_h',
 'WPT_h',
 'WVC_h',
 'WXC_h',
 'TTL_h',
 'AFK_w',
 'ALA_w',


In [431]:
#normalize (melt) commute data so that columns become rows
df_LEHDCommutePatterns_Normalized = pd.melt(df_LEHDCommutePatterns, id_vars=['fakeid','GEOID'], value_vars=dColCodes)

#populate new fields with data from previous column names (ABC_x/y): CODE3 and Category (_x/_y)
df_LEHDCommutePatterns_Normalized['CODE3'   ] = df_LEHDCommutePatterns_Normalized['variable'].str[0:3]
df_LEHDCommutePatterns_Normalized['CATEGORY'] = df_LEHDCommutePatterns_Normalized['variable'].str[3:5]

#join with City/Township data using CODE3
df_LEHDCommutePatterns_Normalized_wCOFIPS = pd.DataFrame.merge(df_CityTownship_NameCode, df_LEHDCommutePatterns_Normalized, on='CODE3')
display(df_LEHDCommutePatterns_Normalized_wCOFIPS)

#get county totals for each GEOID by aggregating (groupby)
df_LEHDCommutePatterns_CountyTotals_Normalized = df_LEHDCommutePatterns_Normalized_wCOFIPS.groupby(['zCOFIPS','GEOID','CATEGORY'],as_index=False).agg({'value':np.sum})

#create column names for county level totals
df_LEHDCommutePatterns_CountyTotals_Normalized['zCOFIPS_wCat'] = df_LEHDCommutePatterns_CountyTotals_Normalized['zCOFIPS'] + df_LEHDCommutePatterns_CountyTotals_Normalized['CATEGORY']

#create pivot table to reverse normalization, returning structure to original format, but this time with county columns
df_LEHDCommutePatterns_CountyTotals = df_LEHDCommutePatterns_CountyTotals_Normalized.pivot(index='GEOID', columns='zCOFIPS_wCat')['value']

display(df_LEHDCommutePatterns_CountyTotals)

NAME CODE3 zCOFIPS  fakeid         GEOID variable  value CATEGORY
0          Alpine   ALP     z49       0        colSUM    ALP_h   4722       _h
1          Alpine   ALP     z49       0  490011001001    ALP_h      0       _h
2          Alpine   ALP     z49       1  490011001002    ALP_h      0       _h
3          Alpine   ALP     z49       2  490011001003    ALP_h      1       _h
4          Alpine   ALP     z49       3  490011002001    ALP_h      0       _h
...           ...   ...     ...     ...           ...      ...    ...      ...
391875  Santaquin   SAQ     z23    2014  490572112021    SAQ_w      0       _w
391876  Santaquin   SAQ     z23    2015  490572112022    SAQ_w      0       _w
391877  Santaquin   SAQ     z23    2016  490572112023    SAQ_w      0       _w
391878  Santaquin   SAQ     z23    2017  490572112024    SAQ_w      0       _w
391879  Santaquin   SAQ     z23    2018  490572112025    SAQ_w      0       _w

[391880 rows x 8 columns]

zCOFIPS_wCat  z03_h  z03_w   z11_h   z11_w  z23_h  z23_w  z29_h  z29_w  \
GEOID                                                                    
490011001001      0      0       5       5      0      0      0      0   
490011001002      3      2       4       5      1      1      0      0   
490011001003      3      0      19      12      0      0      1      0   
490011002001      0      0       0       3      0      0      0      0   
490011002002      0      0       0       1      0      0      0      0   
...             ...    ...     ...     ...    ...    ...    ...    ...   
490572112022      4      3     192     263      1      0     18      6   
490572112023      5      7      42     114      1      0      0      0   
490572112024      4      1      39      72      0      0      2      3   
490572112025      7      1     323      44      0      0     14      0   
colSUM        13819  10213  148861  112209   5649   1041   1987   1300   

zCOFIPS_wCat   z35_h   z35_w  z43_h  z43_w  z45_h  z45_w   z49_h   z49_w  \
GEOID                                                                      
490011001001      14      21      1      1      1      0      19       7   
490011001002       8      53      0      2      0      0       4       9   
490011001003      58      48      1      0      1      1      24       8   
490011002001      13      13      0      1      0      1       9       2   
490011002002       4      26      0      0      0      0       2      16   
...              ...     ...    ...    ...    ...    ...     ...     ...   
490572112022      49     292      0      9      2      2      26      57   
490572112023      17     114      0      1      0      1       2      24   
490572112024       6     115      2      1      1      1       7      17   
490572112025      73      67      3      2     13      0      35       6   
colSUM        552510  701443   7690  16466  23034  10346  260001  240735   

zCOFIPS_wCat  z51_h  z51_w   z57_h   z57_w  
GEOID                                       
490011001001      1      0       2       1  
490011001002      0      0       0       4  
490011001003      0      2      14       5  
490011002001      1      0       0       0  
490011002002      0      1       0       2  
...             ...    ...     ...     ...  
490572112022      0      1     364     665  
490572112023      1      0      73     278  
490572112024      0      1      75     180  
490572112025      3      0     524     126  
colSUM        12428   8044  110179  101860  

[2020 rows x 20 columns]

In [432]:
#add county columns to original dataset
df_LEHDCommutePatternsWCounty = pd.DataFrame.merge(df_LEHDCommutePatterns, df_LEHDCommutePatterns_CountyTotals, on='GEOID')
df_LEHDCommutePatterns = df_LEHDCommutePatternsWCounty

df_LEHDCommutePatterns

fakeid         GEOID  AFK_h  ALA_h  ALP_h  BDL_h  BGM_h  BNT_h  BRT_h  \
0          0        colSUM  13264    192   4722   6984   9967  20045     73   
1          0  490011001001      2      0      0      0      0      1      0   
2          1  490011001002      0      0      0      0      1      2      0   
3          2  490011001003      1      0      1      1      1      2      0   
4          3  490011002001      1      0      0      0      0      0      0   
...      ...           ...    ...    ...    ...    ...    ...    ...    ...   
2015    2014  490572112021      0      0      1      1      4      2      0   
2016    2015  490572112022      4      0      1      1      3     13      0   
2017    2016  490572112023      0      0      0      0      2      2      0   
2018    2017  490572112024      0      0      1      0      1      2      0   
2019    2018  490572112025      1      0      1      1      5     17      0   

      CDF_h  CEN_h  CHA_h  CHL_h  CLF_h  CLI_h  CMT_h  COA_h  CWH_h  DAN_h  \
0       328   7546    272   4589  13825  10353    524    830  16726    669   
1         0      0      0      0      0      1      0      0      1      1   
2         0      0      0      0      1      0      0      0      0      0   
3         0      1      0      1      1      2      0      0      2      0   
4         0      0      0      0      0      0      0      0      1      0   
...     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
2015      0      2      0      0     10     11      0      0      0      0   
2016      0      4      0      0     24     27      0      0      2      0   
2017      0      0      0      0     11      5      0      0      1      0   
2018      1      1      0      0      4      0      0      1      1      0   
2019      0     14      0      1     26     34      0      1      2      0   

      DRA_h  EAG_h  ELK_h  EMT_h  FAR_h  FCS_h  FFD_h  FRR_h  FTH_h  GLA_h  \
0     22892  15382   1791    713   9218    525     97   3228   2290    876   
1         0      1      0      0      0      0      0      0      0      0   
2         0      0      0      0      0      0      0      0      0      0   
3         4      0      0      0      3      0      0      0      1      0   
4         1      0      0      0      0      0      0      0      0      0   
...     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
2015      0      1      0      0      6      0      0      5      1      0   
2016      2      0      1      0      7      0      0      7      3      0   
2017      1      0      0      0      1      0      0      0      3      0   
2018      0      0      0      0      3      0      0      0      2      0   
2019      4      1      0      0      9      0      0     10      5      0   

      GOS_h  GRL_h  HAR_h  HDT_h  HEB_h  HER_h  HGH_h  HNF_h  HOL_h  HOO_h  \
0       508   5629   3157    366   8414  18856   8182    390  14465   3782   
1         0      0      0      0      0      0      0      0      1      0   
2         0      0      0      0      0      1      0      0      0      0   
3         0      0      0      0      0      1      0      0      0      0   
4         0      0      0      0      1      0      0      0      0      0   
...     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
2015      0      1      6      0      0      2      1      0      1      3   
2016      0      1      7      0      0      0      1      0      1      9   
2017      0      0      2      0      1      1      0      0      1      3   
2018      0      1      2      0      0      0      0      0      0      2   
2019      0      3      9      1      2      0      1      0      1     18   

      HVL_h  IND_h  INT_h  KAY_h  KMS_h  KMT_h  LAY_h  LEH_h  LIN_h  MAP_h  \
0       295    128     34  12698   1064  18589  32514  31126   5007   4963   
1         0      0      0      0      0      1      1      1      0      1   
2         0 

In [433]:
#remove UofU displaced block group
#superceeded by manual reallocation prior to data input prep
#
display(df_LEHDCommutePatterns[df_LEHDCommutePatterns['GEOID']=='490351108004'])

#
#df_LEHDCommutePatterns = df_LEHDCommutePatterns[df_LEHDCommutePatterns['GEOID'] != '490351108004']

#display(df_LEHDCommutePatterns[df_LEHDCommutePatterns['GEOID']=='490351108004'])

fakeid         GEOID  AFK_h  ALA_h  ALP_h  BDL_h  BGM_h  BNT_h  BRT_h  \
631     630  490351108004      0      0      2      1      2      5      0   

     CDF_h  CEN_h  CHA_h  CHL_h  CLF_h  CLI_h  CMT_h  COA_h  CWH_h  DAN_h  \
631      0      1      0      1      8      1      0      0     26      0   

     DRA_h  EAG_h  ELK_h  EMT_h  FAR_h  FCS_h  FFD_h  FRR_h  FTH_h  GLA_h  \
631      6      3      1      0      1      0      0      0      0      0   

     GOS_h  GRL_h  HAR_h  HDT_h  HEB_h  HER_h  HGH_h  HNF_h  HOL_h  HOO_h  \
631      0      2      0      0      1      7      2      0     35      0   

     HVL_h  IND_h  INT_h  KAY_h  KMS_h  KMT_h  LAY_h  LEH_h  LIN_h  MAP_h  \
631      0      1      0      3      0      7      5      8      2      1   

     MID_h  MLC_h  MMT_h  MRG_h  MSL_h  MUR_h  MWY_h  NOG_h  NSL_h  OGD_h  \
631     18     46      3      0      0     24      1      1      2      8   

     OKL_h  ORM_h  PAY_h  PGR_h  PLN_h  PRK_h  PRY_h  PVO_h  PVW_h  ROY_h  \
631      0     10      1      3      0      1      0      6      0      1   

     RVD_h  RVT_h  SAN_h  SAQ_h  SAR_h  SFK_h  SJC_h  SLC_h  SLM_h  SOG_h  \
631      1      7     35      0      3      4     13     61      1      3   

     SPV_h  SSL_h  SUN_h  SWE_h  SYR_h  TAY_h  TOO_h  UIN_h  VIN_h  WAT_h  \
631      2     16      2      1      1     20      9      0      0      0   

     WBG_h  WDL_h  WEB_h  WHT_h  WHV_h  WIL_h  WJC_h  WPT_h  WVC_h  WXC_h  \
631      0      0      0      2      0      0     26      1     32      1   

     TTL_h  AFK_w  ALA_w  ALP_w  BDL_w  BGM_w  BNT_w  BRT_w  CDF_w  CEN_w  \
631    529      5      2      0      3      1      4      0      0      1   

     CHA_w  CHL_w  CLF_w  CLI_w  CMT_w  COA_w  CWH_w  DAN_w  DRA_w  EAG_w  \
631      0      0      1      2      0      0     21      0     33      1   

     ELK_w  EMT_w  FAR_w  FCS_w  FFD_w  FRR_w  FTH_w  GLA_w  GOS_w  GRL_w  \
631      0      1      4      0      1      0      0      0      0      0   

     HAR_w  HDT_w  HEB_w  HER_w  HGH_w  HNF_w  HOL_w  HOO_w  HVL_w  IND_w  \
631      0      0      1      4      0      0     38      0      0      0   

     INT_w  KAY_w  KMS_w  KMT_w  LAY_w  LEH_w  LIN_w  MAP_w  MID_w  MLC_w  \
631      0      1      0      5      7     18      3      0     18     53   

     MMT_w  MRG_w  MSL_w  MUR_w  MWY_w  NOG_w  NSL_w  OGD_w  OKL_w  ORM_w  \
631      1      1      0     53      1      0      6     10      0     10   

     PAY_w  PGR_w  PLN_w  PRK_w  PRY_w  PVO_w  PVW_w  ROY_w  RVD_w  RVT_w  \
631      0      1      0      8      0     10      0      0      0      4   

     SAN_w  SAQ_w  SAR_w  SFK_w  SJC_w  SLC_w  SLM_w  SOG_w  SPV_w  SSL_w  \
631     18      0      2      1     23    287      0      2      1     33   

     SUN_w  SWE_w  SYR_w  TAY_w  TOO_w  UIN_w  VIN_w  WAT_w  WBG_w  WDL_w  \
631      0      0      0     30      2      0      0      0      0      0   

     WEB_w  WHT_w  WHV_w  WIL_w  WJC_w  WPT_w  WVC_w  WXC_w  TTL_w  z03_h  \
631      2      1      0      0     21      0     51      2    843      2   

     z03_w  z11_h  z11_w  z23_h  z23_w  z29_h  z29_w  z35_h  z35_w  z43_h  \
631      1     32     30      0      0      0      1    385    700      1   

     z43_w  z45_h  z45_w  z49_h  z49_w  z51_h  z51_w  z57_h  z57_w  
631      8     11      2     50     53      3      2     14     12

# Quick JSON export with some summary stats

In [434]:
#use row with "colSUM" as GEOID as total
df_LEHDCommutePatterns_ColSum = df_LEHDCommutePatterns[df_LEHDCommutePatterns['GEOID'] == 'colSUM']
df_LEHDCommutePatterns_ColSum

fakeid   GEOID  AFK_h  ALA_h  ALP_h  BDL_h  BGM_h  BNT_h  BRT_h  CDF_h  \
0       0  colSUM  13264    192   4722   6984   9967  20045     73    328   

   CEN_h  CHA_h  CHL_h  CLF_h  CLI_h  CMT_h  COA_h  CWH_h  DAN_h  DRA_h  \
0   7546    272   4589  13825  10353    524    830  16726    669  22892   

   EAG_h  ELK_h  EMT_h  FAR_h  FCS_h  FFD_h  FRR_h  FTH_h  GLA_h  GOS_h  \
0  15382   1791    713   9218    525     97   3228   2290    876    508   

   GRL_h  HAR_h  HDT_h  HEB_h  HER_h  HGH_h  HNF_h  HOL_h  HOO_h  HVL_h  \
0   5629   3157    366   8414  18856   8182    390  14465   3782    295   

   IND_h  INT_h  KAY_h  KMS_h  KMT_h  LAY_h  LEH_h  LIN_h  MAP_h  MID_h  \
0    128     34  12698   1064  18589  32514  31126   5007   4963  17404   

   MLC_h  MMT_h  MRG_h  MSL_h  MUR_h  MWY_h  NOG_h  NSL_h  OGD_h  OKL_h  \
0  30097  14884   1987   1014  25120   2374   9134   8696  39786    617   

   ORM_h  PAY_h  PGR_h  PLN_h  PRK_h  PRY_h  PVO_h  PVW_h  ROY_h  RVD_h  \
0  45810   9632  16766   3261   4264   2778  38893   4487  18915   4055   

   RVT_h  SAN_h  SAQ_h  SAR_h  SFK_h  SJC_h  SLC_h  SLM_h  SOG_h  SPV_h  \
0  23996  47957   5649  15409  20518  33206  90355   4071   7814  16954   

   SSL_h  SUN_h  SWE_h  SYR_h  TAY_h  TOO_h  UIN_h  VIN_h  WAT_h  WBG_h  \
0  12174   2659   3179  12484  31289  17405    651    148   4565    171   

   WDL_h  WEB_h  WHT_h  WHV_h  WIL_h  WJC_h  WPT_h  WVC_h  WXC_h    TTL_h  \
0    965   3280   2973   6035   1074  59636   4899  63405   5175  1431409   

   AFK_w  ALA_w  ALP_w  BDL_w  BGM_w  BNT_w  BRT_w  CDF_w  CEN_w  CHA_w  \
0  22811   1838   2558   4478   9085  11940     79     58   5781    202   

   CHL_w  CLF_w  CLI_w  CMT_w  COA_w  CWH_w  DAN_w  DRA_w  EAG_w  ELK_w  \
0    876  17022   2624     90    763  20765    225  40016   2336    285   

   EMT_w  FAR_w  FCS_w  FFD_w  FRR_w  FTH_w  GLA_w  GOS_w  GRL_w  HAR_w  \
0     93   8785     74     95   3251    394    208     67   2330   1702   

   HDT_w  HEB_w  HER_w  HGH_w  HNF_w  HOL_w  HOO_w  HVL_w  IND_w  INT_w  \
0      9   6162   4842   3148     57  10927    634     94     12      0   

   KAY_w  KMS_w  KMT_w  LAY_w  LEH_w  LIN_w  MAP_w  MID_w  MLC_w  MMT_w  \
0   8415   1306   4215  27632  36565  13160   2123  18414  47873   2904   

   MRG_w  MSL_w  MUR_w  MWY_w  NOG_w  NSL_w  OGD_w  OKL_w  ORM_w  PAY_w  \
0   1300   1742  46705   1383   2954  14920  58666    265  48060   5821   

   PGR_w  PLN_w  PRK_w  PRY_w  PVO_w  PVW_w  ROY_w  RVD_w  RVT_w  SAN_w  \
0  12021    815  14001    946  57332   2230   7600   7992  10783  49663   

   SAQ_w  SAR_w  SFK_w  SJC_w   SLC_w  SLM_w  SOG_w  SPV_w  SSL_w  SUN_w  \
0   1041   3795  13180  31997  247011   1891   6994  13088  33211   1092   

   SWE_w  SYR_w  TAY_w  TOO_w  UIN_w  VIN_w  WAT_w  WBG_w  WDL_w  WEB_w  \
0    791   4176  21228   8016    253   1084   3299     51    173   2145   

   WHT_w  WHV_w  WIL_w  WJC_w  WPT_w  WVC_w  WXC_w    TTL_w  z03_h  z03_w  \
0    350   3634    182  35072   1137  68889   5355  1452647  13819  10213   

    z11_h   z11_w  z23_h  z23_w  z29_h  z29_w   z35_h   z35_w  z43_h  z43_w  \
0  148861  112209   5649   1041   1987   1300  552510  701443   7690  16466   

   z45_h  z45_w   z49_h   z49_w  z51_h  z51_w   z57_h   z57_w  
0  23034  10346  260001  240735  12428   8044  110179  101860

In [435]:
#prepare area columns for json
df_people = df_LEHDCommutePatterns_ColSum.loc[:,'AFK_h':'z57_w'].T #transpose
df_people = df_people.reset_index()
df_people['CATEGORY'] = df_people['index'].str[3:5]
df_people['index']    = df_people['index'].str[:3]
df_people

index       0 CATEGORY
0     AFK   13264       _h
1     ALA     192       _h
2     ALP    4722       _h
3     BDL    6984       _h
4     BGM    9967       _h
..    ...     ...      ...
211   z49  240735       _w
212   z51   12428       _h
213   z51    8044       _w
214   z57  110179       _h
215   z57  101860       _w

[216 rows x 3 columns]

In [436]:
#prepare x columns
df_people_x = df_people[df_people['CATEGORY'] == '_h']
df_people_x.columns = ('CODE3','people_h','CATEGORY')

df_people_x['CODE3'] = df_people_x['CODE3'].str[:3]

df_people_x = df_people_x.drop_duplicates() #some duplicate columns in dataset
display(df_people_x)

#prepare y columns
df_people_y = df_people[df_people['CATEGORY'] == '_w']
df_people_y.columns = ('CODE3','people_w','CATEGORY')

df_people_y['CODE3'] = df_people_y['CODE3'].str[:3]

df_people_y = df_people_y.drop_duplicates() #some duplicate columns in dataset
display(df_people_y)

df_people_x = df_people_x.drop(['CATEGORY'], axis=1)
df_people_y = df_people_y.drop(['CATEGORY'], axis=1)

#combine city/township data with x and y
df_CityTownship_People = pd.DataFrame.merge(df_CityTownship_NameCode,df_people_x, on='CODE3', how='right')
df_CityTownship_People = pd.DataFrame.merge(df_CityTownship_People  ,df_people_y, on='CODE3', how='right')                                           


C:\Users\cday\AppData\Local\ESRI\conda\envs\arcgispro-py3-clone\lib\site-packages\ipykernel_launcher.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """


CODE3  people_h CATEGORY
0     AFK     13264       _h
1     ALA       192       _h
2     ALP      4722       _h
3     BDL      6984       _h
4     BGM      9967       _h
..    ...       ...      ...
206   z43      7690       _h
208   z45     23034       _h
210   z49    260001       _h
212   z51     12428       _h
214   z57    110179       _h

[108 rows x 3 columns]

C:\Users\cday\AppData\Local\ESRI\conda\envs\arcgispro-py3-clone\lib\site-packages\ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


CODE3  people_w CATEGORY
98    AFK     22811       _w
99    ALA      1838       _w
100   ALP      2558       _w
101   BDL      4478       _w
102   BGM      9085       _w
..    ...       ...      ...
207   z43     16466       _w
209   z45     10346       _w
211   z49    240735       _w
213   z51      8044       _w
215   z57    101860       _w

[108 rows x 3 columns]

In [437]:
#define county dataframe
df_CoNames = sdf_CountiesAGRC[['zCOFIPS','CO_NAME']]

#prepare dataframe for export to JSON, combining city/township
df_CityTownship_Export = pd.DataFrame.merge(df_CityTownship_People, df_CoNames, left_on='CODE3', right_on='zCOFIPS', how='left')

#for any null values, replace with zero(0)
df_CityTownship_Export = df_CityTownship_Export.fillna(0)

#Get city/township name and county name into one field
df_CityTownship_Export.loc[df_CityTownship_Export.CO_NAME != 0, 'NAME'] = df_CityTownship_Export['CO_NAME']

#filter by only 4 columns for export
df_CityTownship_Export = df_CityTownship_Export[['NAME','CODE3','people_h','people_w']]

#change TTL (total) row to Counties subhead for correct positioning in dropdown

#don't include total row
df_CityTownship_Export = df_CityTownship_Export[df_CityTownship_Export['CODE3'] != 'TTL']

#df_CityTownship_Export.loc[((df_CityTownship_Export['CODE3'] == 'TTL')), 'NAME' ] = '---COUNTIES---'
#df_CityTownship_Export.loc[((df_CityTownship_Export['CODE3'] == 'TTL')), 'CODE3'] = 'y000'

#create a first letter field for sorting, to preserve COUNTIES with (z..) at bottom of sort, so can't use name as first sort
#df_CityTownship_Export['firstletter'] = df_CityTownship_Export['CODE3'].str[0:1]
#df_CityTownship_Export = df_CityTownship_Export.sort_values(by=['firstletter','NAME'])
df_CityTownship_Export = df_CityTownship_Export.sort_values(by=['NAME'])

#filter again by only 4 columns for export
df_CityTownship_Export = df_CityTownship_Export[['NAME','CODE3','people_h','people_w']]

#rename columns with 'label' and 'value' to work better in javascript dojo convention
df_CityTownship_Export.columns = ('label','value','people_h','people_w')

#let's see what we got!!
display(df_CityTownship_Export)
    
#export to JSON
df_CityTownship_Export.to_json(fname_CityTownshipJSON,orient='records')

label value  people_h  people_w
2             Alpine   ALP      4722      2558
1               Alta   ALA       192      1838
0      American Fork   AFK     13264     22811
3          Bluffdale   BDL      6984      4478
5          Bountiful   BNT     20045     11940
..               ...   ...       ...       ...
95  West Valley City   WVC     63405     68889
90        White City   WHT      2973       350
92           Willard   WIL      1074       182
88    Woodland Hills   WDL       965       173
96       Woods Cross   WXC      5175      5355

[107 rows x 4 columns]

# Update ColCodes with Counties for summing

In [438]:
#get all column codes for summing
dfColCodesWCounty = df_LEHDCommutePatterns.loc[1:1,'AFK_h':'z57_w'].T
dfColCodesWCounty = dfColCodesWCounty.reset_index()
dColCodesWCounty = dfColCodesWCounty['index'].values.tolist()
dColCodesWCounty

['AFK_h',
 'ALA_h',
 'ALP_h',
 'BDL_h',
 'BGM_h',
 'BNT_h',
 'BRT_h',
 'CDF_h',
 'CEN_h',
 'CHA_h',
 'CHL_h',
 'CLF_h',
 'CLI_h',
 'CMT_h',
 'COA_h',
 'CWH_h',
 'DAN_h',
 'DRA_h',
 'EAG_h',
 'ELK_h',
 'EMT_h',
 'FAR_h',
 'FCS_h',
 'FFD_h',
 'FRR_h',
 'FTH_h',
 'GLA_h',
 'GOS_h',
 'GRL_h',
 'HAR_h',
 'HDT_h',
 'HEB_h',
 'HER_h',
 'HGH_h',
 'HNF_h',
 'HOL_h',
 'HOO_h',
 'HVL_h',
 'IND_h',
 'INT_h',
 'KAY_h',
 'KMS_h',
 'KMT_h',
 'LAY_h',
 'LEH_h',
 'LIN_h',
 'MAP_h',
 'MID_h',
 'MLC_h',
 'MMT_h',
 'MRG_h',
 'MSL_h',
 'MUR_h',
 'MWY_h',
 'NOG_h',
 'NSL_h',
 'OGD_h',
 'OKL_h',
 'ORM_h',
 'PAY_h',
 'PGR_h',
 'PLN_h',
 'PRK_h',
 'PRY_h',
 'PVO_h',
 'PVW_h',
 'ROY_h',
 'RVD_h',
 'RVT_h',
 'SAN_h',
 'SAQ_h',
 'SAR_h',
 'SFK_h',
 'SJC_h',
 'SLC_h',
 'SLM_h',
 'SOG_h',
 'SPV_h',
 'SSL_h',
 'SUN_h',
 'SWE_h',
 'SYR_h',
 'TAY_h',
 'TOO_h',
 'UIN_h',
 'VIN_h',
 'WAT_h',
 'WBG_h',
 'WDL_h',
 'WEB_h',
 'WHT_h',
 'WHV_h',
 'WIL_h',
 'WJC_h',
 'WPT_h',
 'WVC_h',
 'WXC_h',
 'TTL_h',
 'AFK_w',
 'ALA_w',


# Add Unincorporated County Areas to Cities/Townships

In [439]:
#filter county dataset with only what we want
sdf_CountiesWCodes = sdf_CountiesAGRC[['zCOFIPS','CO_NAME','SHAPE']]
sdf_CountiesWCodes.columns = ('CODE3','FIRST_NAME','SHAPE')
display(sdf_CountiesWCodes)

#export a couple county spatial dataframes
sdf_CountiesWCodes.spatial.to_featureclass(fname_CountyWCodes_shp, sanitize_columns=False) #as shapefile for future use
sdf_CountiesWCodes.spatial.to_featureclass(fname_Counties, sanitize_columns=False) #for gdb for use in web app

CODE3         FIRST_NAME                                              SHAPE
0    z05       Cache County  {"rings": [[[-112.15617197899996, 41.997725941...
1    z13    Duchesne County  {"rings": [[[-110.25173670299995, 40.832347463...
2    z11       Davis County  {"rings": [[[-111.92092166399999, 41.138676415...
3    z27     Millard County  {"rings": [[[-112.23854898599996, 39.553633436...
4    z51     Wasatch County  {"rings": [[[-111.39572506599995, 40.690187842...
5    z03   Box Elder County  {"rings": [[[-113.47488592699995, 41.993309448...
6    z57       Weber County  {"rings": [[[-111.92092166399999, 41.138676415...
7    z23        Juab County  {"rings": [[[-112.17814760399995, 40.011304953...
8    z39     Sanpete County  {"rings": [[[-111.60347983999998, 39.812889279...
9    z53  Washington County  {"rings": [[[-113.47458777999998, 37.607168207...
10   z19       Grand County  {"rings": [[[-109.05510868899995, 39.498702060...
11   z33        Rich County  {"rings": [[[-111.04672602399995, 42.001708362...
12   z07      Carbon County  {"rings": [[[-111.05121454599998, 39.814071497...
13   z09     Daggett County  {"rings": [[[-109.05002513499994, 40.999895250...
14   z01      Beaver County  {"rings": [[[-112.51540546399997, 38.572850827...
15   z41      Sevier County  {"rings": [[[-111.84900514399999, 39.044355246...
16   z17    Garfield County  {"rings": [[[-112.26560199199997, 38.149879660...
17   z45      Tooele County  {"rings": [[[-112.44788691599996, 41.017030151...
18   z43      Summit County  {"rings": [[[-109.99967939799996, 40.997456621...
19   z31       Piute County  {"rings": [[[-112.33023683099998, 38.510834361...
20   z47      Uintah County  {"rings": [[[-109.04897471299995, 40.662656164...
21   z21        Iron County  {"rings": [[[-113.36588561299999, 38.148691452...
22   z15       Emery County  {"rings": [[[-111.24394073999997, 39.703588004...
23   z55       Wayne County  {"rings": [[[-111.70753983999998, 38.510152783...
24   z37    San Juan County  {"rings": [[[-109.77115733799997, 36.998238968...
25   z29      Morgan County  {"rings": [[[-111.51438719299995, 40.803633660...
26   z25        Kane County  {"rings": [[[-111.84536734499994, 37.535799155...
27   z35   Salt Lake County  {"rings": [[[-111.96851544299994, 40.871938834...
28   z49        Utah County  {"rings": [[[-111.59404929699997, 40.577075300...

C:\Users\cday\AppData\Local\ESRI\conda\envs\arcgispro-py3-clone\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)


'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2019\\LEHDCommutePatterns.gdb\\Counties'

In [440]:
deleteIfExists(fname_CityTownshipWCodesUnionCounty_shp)

print ("Unioning city/township with county...")

#intersection parcels with analysis area types
arcpy.analysis.Union([fname_CityTownshipWCodes,fname_CountyWCodes_shp], fname_CityTownshipWCodesUnionCounty_shp)

sdf_CityTownshipWCodesCounty = pd.DataFrame.spatial.from_featureclass(fname_CityTownshipWCodesUnionCounty_shp)
sdf_CityTownshipWCodesCounty = sdf_CityTownshipWCodesCounty.rename(columns={"code3":"CODE3", "FIRST_name":"FIRST_NAME", "FIRST_coun":"FIRST_COUN", "first_na_1":"FIRST_NA_1", "code3_1":"CODE3_1"})
sdf_CityTownshipWCodesCounty

Unioning city/township with county...


FID  FID_Munici CODE3        FIRST_NAME FIRST_COUN  Shape_Leng  \
0      0          -1                                       0.000000   
1      1          -1                                       0.000000   
2      2          -1                                       0.000000   
3      3          -1                                       0.000000   
4      4          -1                                       0.000000   
..   ...         ...   ...               ...        ...         ...   
154  154          75   SLC    Salt Lake City         18    1.346029   
155  155          50   MMT             Magna         18    0.756349   
156  156          96   WVC  West Valley City         18    0.614523   
157  157          70   SAN             Sandy         18    1.239008   
158  158          91   WHT        White City         18    0.147366   

     Shape_Area  FID_Counti  Id CODE3_1        FIRST_NA_1  \
0      0.000000           0   0     z05      Cache County   
1      0.000000           1   0     z13   Duchesne County   
2      0.000000           2   0     z11      Davis County   
3      0.000000           3   0     z27    Millard County   
4      0.000000           4   0     z51    Wasatch County   
..          ...         ...  ..     ...               ...   
154    0.030613          27   0     z35  Salt Lake County   
155    0.010342          27   0     z35  Salt Lake County   
156    0.009884          27   0     z35  Salt Lake County   
157    0.006653          27   0     z35  Salt Lake County   
158    0.000241          27   0     z35  Salt Lake County   

                                                 SHAPE  
0    {"rings": [[[-111.50779761699998, 41.999560240...  
1    {"rings": [[[-109.99900220099995, 40.813577918...  
2    {"rings": [[[-112.10299823793908, 41.152736052...  
3    {"rings": [[[-112.01601400799998, 39.314566632...  
4    {"rings": [[[-111.38703771390648, 40.657177632...  
..                                                 ...  
154  {"rings": [[[-112.10123724564913, 40.775409823...  
155  {"rings": [[[-112.06310238736523, 40.703812554...  
156  {"rings": [[[-112.06310238736523, 40.703812554...  
157  {"rings": [[[-111.86188875086515, 40.580804996...  
158  {"rings": [[[-111.86188875086515, 40.580804996...  

[159 rows x 12 columns]

In [441]:
sdf_CityTownshipWCodesCounty.loc[((sdf_CityTownshipWCodesCounty['FID_Munici'] == -1)), 'CODE3'     ] = sdf_CityTownshipWCodesCounty['CODE3_1'   ]
sdf_CityTownshipWCodesCounty.loc[((sdf_CityTownshipWCodesCounty['FID_Munici'] == -1)), 'FIRST_NAME'] = sdf_CityTownshipWCodesCounty['FIRST_NA_1'] + ' Unincorporated'

sdf_CityTownshipWCodesCounty = sdf_CityTownshipWCodesCounty[['FID_Munici','CODE3','FIRST_NAME','SHAPE']]

sdf_CityTownshipWCodesCounty.spatial.to_featureclass(fname_CityTownshipCountyWCodes_shp, sanitize_columns=False)
sdf_CityTownshipWCodesCounty

C:\Users\cday\AppData\Local\ESRI\conda\envs\arcgispro-py3-clone\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)


FID_Munici CODE3                      FIRST_NAME  \
0            -1   z05     Cache County Unincorporated   
1            -1   z13  Duchesne County Unincorporated   
2            -1   z11     Davis County Unincorporated   
3            -1   z27   Millard County Unincorporated   
4            -1   z51   Wasatch County Unincorporated   
..          ...   ...                             ...   
154          75   SLC                  Salt Lake City   
155          50   MMT                           Magna   
156          96   WVC                West Valley City   
157          70   SAN                           Sandy   
158          91   WHT                      White City   

                                                 SHAPE  
0    {"rings": [[[-111.50779761699998, 41.999560240...  
1    {"rings": [[[-109.99900220099995, 40.813577918...  
2    {"rings": [[[-112.10299823793908, 41.152736052...  
3    {"rings": [[[-112.01601400799998, 39.314566632...  
4    {"rings": [[[-111.38703771390648, 40.657177632...  
..                                                 ...  
154  {"rings": [[[-112.10123724564913, 40.775409823...  
155  {"rings": [[[-112.06310238736523, 40.703812554...  
156  {"rings": [[[-112.06310238736523, 40.703812554...  
157  {"rings": [[[-111.86188875086515, 40.580804996...  
158  {"rings": [[[-111.86188875086515, 40.580804996...  

[159 rows x 4 columns]

# Calculate Percent

In [442]:
#read block group shapefile
sdf_BlockGroups = pd.DataFrame.spatial.from_featureclass(fname_BlockGroups_shp)
sdf_LEHDCommutePatterns = pd.DataFrame.merge(sdf_BlockGroups, df_LEHDCommutePatterns, on='GEOID')
display(sdf_BlockGroups)

FID STATEFP COUNTYFP TRACTCE  DISTSML BLKGRPCE         GEOID  \
0        0      49      035  111306     75.0        1  490351113061   
1        1      49      035  111306     75.0        2  490351113062   
2        2      49      035  111400     47.0        1  490351114001   
3        3      49      035  111400     56.0        2  490351114002   
4        4      49      035  111400     56.0        3  490351114003   
...    ...     ...      ...     ...      ...      ...           ...   
2015  2015      49      057  200900     16.0        2  490572009002   
2016  2016      49      057  201200     15.0        1  490572012001   
2017  2017      49      057  201200     15.0        2  490572012002   
2018  2018      49      057  201301     16.0        2  490572013012   
2019  2019      49      057  201301     16.0        1  490572013011   

           NAMELSAD  MTFCC FUNCSTAT     ALAND  AWATER     INTPTLAT  \
0     Block Group 1  G5030        S  877837.0     0.0  +40.6094422   
1     Block Group 2  G5030        S  653262.0     0.0  +40.6068923   
2     Block Group 1  G5030        S  381555.0     0.0  +40.7219003   
3     Block Group 2  G5030        S  308108.0     0.0  +40.7155063   
4     Block Group 3  G5030        S  422651.0     0.0  +40.7087113   
...             ...    ...      ...       ...     ...          ...   
2015  Block Group 2  G5030        S  347700.0     0.0  +41.2248269   
2016  Block Group 1  G5030        S  752190.0     0.0  +41.2121869   
2017  Block Group 2  G5030        S  437903.0     0.0  +41.2123035   
2018  Block Group 2  G5030        S  326205.0     0.0  +41.2163706   
2019  Block Group 1  G5030        S  432925.0     0.0  +41.2162428   

          INTPTLON  CENTROID_X  CENTROID_Y     BGAcres  \
0     -111.8259365 -111.825937   40.609442  216.771411   
1     -111.8144187 -111.814419   40.606892  161.314487   
2     -111.8796932 -111.879693   40.721900   94.222093   
3     -111.8797286 -111.879729   40.715506   76.084072   
4     -111.8797335 -111.879733   40.708711  104.369581   
...            ...         ...         ...         ...   
2015  -111.9636889 -111.963689   41.224827   85.863927   
2016  -111.9783667 -111.978367   41.212187  185.752109   
2017  -111.9706612 -111.970661   41.212304  108.139051   
2018  -111.9635764 -111.963576   41.216371   80.555404   
2019  -111.9538634 -111.953863   41.216243  106.909485   

                                                  SHAPE  
0     {"rings": [[[429468.0213051503, 4496405.233871...  
1     {"rings": [[[430494.91099986027, 4495540.43917...  
2     {"rings": [[[425457.5579433697, 4507873.987348...  
3     {"rings": [[[425448.36375707807, 4507253.27157...  
4     {"rings": [[[425435.2029181655, 4506380.698648...  
...                                                 ...  
2015  {"rings": [[[418807.4658959587, 4564213.682993...  
2016  {"rings": [[[417490.98019006505, 4562356.17136...  
2017  {"rings": [[[418380.1807087121, 4562347.716705...  
2018  {"rings": [[[418871.13447070273, 4563020.29370...  
2019  {"rings": [[[419571.11778565514, 4563028.08038...  

[2020 rows x 18 columns]

In [443]:
pd.set_option('display.max_columns', None)
df_LEHDCommutePatterns.loc[1:,'AFK_h':]

AFK_h  ALA_h  ALP_h  BDL_h  BGM_h  BNT_h  BRT_h  CDF_h  CEN_h  CHA_h  \
1         2      0      0      0      0      1      0      0      0      0   
2         0      0      0      0      1      2      0      0      0      0   
3         1      0      1      1      1      2      0      0      1      0   
4         1      0      0      0      0      0      0      0      0      0   
5         0      0      1      0      0      0      0      0      0      0   
...     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
2015      0      0      1      1      4      2      0      0      2      0   
2016      4      0      1      1      3     13      0      0      4      0   
2017      0      0      0      0      2      2      0      0      0      0   
2018      0      0      1      0      1      2      0      1      1      0   
2019      1      0      1      1      5     17      0      0     14      0   

      CHL_h  CLF_h  CLI_h  CMT_h  COA_h  CWH_h  DAN_h  DRA_h  EAG_h  ELK_h  \
1         0      0      1      0      0      1      1      0      1      0   
2         0      1      0      0      0      0      0      0      0      0   
3         1      1      2      0      0      2      0      4      0      0   
4         0      0      0      0      0      1      0      1      0      0   
5         0      0      0      0      0      0      0      1      0      0   
...     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
2015      0     10     11      0      0      0      0      0      1      0   
2016      0     24     27      0      0      2      0      2      0      1   
2017      0     11      5      0      0      1      0      1      0      0   
2018      0      4      0      0      1      1      0      0      0      0   
2019      1     26     34      0      1      2      0      4      1      0   

      EMT_h  FAR_h  FCS_h  FFD_h  FRR_h  FTH_h  GLA_h  GOS_h  GRL_h  HAR_h  \
1         0      0      0      0      0      0      0      0      0      0   
2         0      0      0      0      0      0      0      0      0      0   
3         0      3      0      0      0      1      0      0      0      0   
4         0      0      0      0      0      0      0      0      0      0   
5         0      0      0      0      0      0      0      0      0      0   
...     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
2015      0      6      0      0      5      1      0      0      1      6   
2016      0      7      0      0      7      3      0      0      1      7   
2017      0      1      0      0      0      3      0      0      0      2   
2018      0      3      0      0      0      2      0      0      1      2   
2019      0      9      0      0     10      5      0      0      3      9   

      HDT_h  HEB_h  HER_h  HGH_h  HNF_h  HOL_h  HOO_h  HVL_h  IND_h  INT_h  \
1         0      0      0      0      0      1      0      0      0      0   
2         0      0      1      0      0      0      0      0      0      0   
3         0      0      1      0      0      0      0      0      0      0   
4         0      1      0      0      0      0      0      0      0      0   
5         0      0      0      1      0      0      0      0      0      0   
...     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
2015      0      0      2      1      0      1      3      1      0      0   
2016      0      0      0      1      0      1      9      0      0      0   
2017      0      1      1      0      0      1      3      0      0      0   
2018      0      0      0      0      0      0      2      1      0      0   
2019      1      2      0      1      0      1     18      1      0      0   

      KAY_h  KMS_h  KMT_h  LAY_h  LEH_h  LIN_h  MAP_h  MID_h  MLC_h  MMT_h  \
1         0      0      1      1      1      0      1      2      0      0   
2         1      0      1      0      0      0      0      0      1      0   
3         1      0      

In [444]:
sdf_LEHDCommutePatterns

FID STATEFP COUNTYFP TRACTCE  DISTSML BLKGRPCE         GEOID  \
0        0      49      035  111306     75.0        1  490351113061   
1        1      49      035  111306     75.0        2  490351113062   
2        2      49      035  111400     47.0        1  490351114001   
3        3      49      035  111400     56.0        2  490351114002   
4        4      49      035  111400     56.0        3  490351114003   
...    ...     ...      ...     ...      ...      ...           ...   
2014  2015      49      057  200900     16.0        2  490572009002   
2015  2016      49      057  201200     15.0        1  490572012001   
2016  2017      49      057  201200     15.0        2  490572012002   
2017  2018      49      057  201301     16.0        2  490572013012   
2018  2019      49      057  201301     16.0        1  490572013011   

           NAMELSAD  MTFCC FUNCSTAT     ALAND  AWATER     INTPTLAT  \
0     Block Group 1  G5030        S  877837.0     0.0  +40.6094422   
1     Block Group 2  G5030        S  653262.0     0.0  +40.6068923   
2     Block Group 1  G5030        S  381555.0     0.0  +40.7219003   
3     Block Group 2  G5030        S  308108.0     0.0  +40.7155063   
4     Block Group 3  G5030        S  422651.0     0.0  +40.7087113   
...             ...    ...      ...       ...     ...          ...   
2014  Block Group 2  G5030        S  347700.0     0.0  +41.2248269   
2015  Block Group 1  G5030        S  752190.0     0.0  +41.2121869   
2016  Block Group 2  G5030        S  437903.0     0.0  +41.2123035   
2017  Block Group 2  G5030        S  326205.0     0.0  +41.2163706   
2018  Block Group 1  G5030        S  432925.0     0.0  +41.2162428   

          INTPTLON  CENTROID_X  CENTROID_Y     BGAcres  \
0     -111.8259365 -111.825937   40.609442  216.771411   
1     -111.8144187 -111.814419   40.606892  161.314487   
2     -111.8796932 -111.879693   40.721900   94.222093   
3     -111.8797286 -111.879729   40.715506   76.084072   
4     -111.8797335 -111.879733   40.708711  104.369581   
...            ...         ...         ...         ...   
2014  -111.9636889 -111.963689   41.224827   85.863927   
2015  -111.9783667 -111.978367   41.212187  185.752109   
2016  -111.9706612 -111.970661   41.212304  108.139051   
2017  -111.9635764 -111.963576   41.216371   80.555404   
2018  -111.9538634 -111.953863   41.216243  106.909485   

                                                  SHAPE  fakeid  AFK_h  ALA_h  \
0     {'rings': [[[429468.0213051503, 4496405.233871...     668      4      0   
1     {'rings': [[[430494.91099986027, 4495540.43917...     669      0      0   
2     {'rings': [[[425457.5579433697, 4507873.987348...     670      0      0   
3     {'rings': [[[425448.36375707807, 4507253.27157...     671      1      0   
4     {'rings': [[[425435.2029181655, 4506380.698648...     672      0      0   
...                                                 ...     ...    ...    ...   
2014  {'rings': [[[418807.4658959587, 4564213.682993...    1887      0      0   
2015  {'rings': [[[417490.98019006505, 4562356.17136...    1891      0      0   
2016  {'rings': [[[418380.1807087121, 4562347.716705...    1892      3      0   
2017  {'rings': [[[418871.13447070273, 4563020.29370...    1894      0      0   
2018  {'rings': [[[419571.11778565514, 4563028.08038...    1893      1      0   

      ALP_h  BDL_h  BGM_h  BNT_h  BRT_h  CDF_h  CEN_h  CHA_h  CHL_h  CLF_h  \
0         2     16      3     37      0      0     12      0      3      9   
1         1      1      0      4      0      0      0      0      0      0   
2         0      0      1      1      0      0      2      0      0      0   
3         0      0      0      0      0      0      1      0      0      1   
4         0      0      0      0      0      0      0      0      0      0   
...     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
2014      0      0      2      4      0      0      1      0      0      3   
2015      0      0 

In [445]:
df_LEHDCommutePatterns.iloc[0,2:218]

AFK_h     13264
ALA_h       192
ALP_h      4722
BDL_h      6984
BGM_h      9967
          ...  
z49_w    240735
z51_h     12428
z51_w      8044
z57_h    110179
z57_w    101860
Name: 0, Length: 216, dtype: object

In [446]:
#initialize Percent_SA distribution dataframe
df_LEHDCommutePatterns_Percent_SA = df_LEHDCommutePatterns

#divide columns AFK_x and after by first row (totals) and columns 2:218
df_LEHDCommutePatterns_Percent_SA.loc[1:,'AFK_h':] = df_LEHDCommutePatterns.loc[1:,'AFK_h':].div(df_LEHDCommutePatterns.iloc[0,2:218])
df_LEHDCommutePatterns_Percent_SA.loc[1:,'AFK_h':] = df_LEHDCommutePatterns.loc[1:,'AFK_h':] * 100
df_LEHDCommutePatterns_Percent_SA

fakeid         GEOID     AFK_h ALA_h     ALP_h     BDL_h     BGM_h  \
0          0        colSUM     13264   192      4722      6984      9967   
1          0  490011001001  0.015078   0.0       0.0       0.0       0.0   
2          1  490011001002       0.0   0.0       0.0       0.0  0.010033   
3          2  490011001003  0.007539   0.0  0.021177  0.014318  0.010033   
4          3  490011002001  0.007539   0.0       0.0       0.0       0.0   
...      ...           ...       ...   ...       ...       ...       ...   
2015    2014  490572112021       0.0   0.0  0.021177  0.014318  0.040132   
2016    2015  490572112022  0.030157   0.0  0.021177  0.014318  0.030099   
2017    2016  490572112023       0.0   0.0       0.0       0.0  0.020066   
2018    2017  490572112024       0.0   0.0  0.021177       0.0  0.010033   
2019    2018  490572112025  0.007539   0.0  0.021177  0.014318  0.050166   

         BNT_h BRT_h     CDF_h     CEN_h CHA_h     CHL_h     CLF_h     CLI_h  \
0        20045    73       328      7546   272      4589     13825     10353   
1     0.004989   0.0       0.0       0.0   0.0       0.0       0.0  0.009659   
2     0.009978   0.0       0.0       0.0   0.0       0.0  0.007233       0.0   
3     0.009978   0.0       0.0  0.013252   0.0  0.021791  0.007233  0.019318   
4          0.0   0.0       0.0       0.0   0.0       0.0       0.0       0.0   
...        ...   ...       ...       ...   ...       ...       ...       ...   
2015  0.009978   0.0       0.0  0.026504   0.0       0.0  0.072333  0.106249   
2016  0.064854   0.0       0.0  0.053008   0.0       0.0  0.173599  0.260794   
2017  0.009978   0.0       0.0       0.0   0.0       0.0  0.079566  0.048295   
2018  0.009978   0.0  0.304878  0.013252   0.0       0.0  0.028933       0.0   
2019  0.084809   0.0       0.0  0.185529   0.0  0.021791  0.188065  0.328407   

     CMT_h     COA_h     CWH_h     DAN_h     DRA_h     EAG_h     ELK_h EMT_h  \
0      524       830     16726       669     22892     15382      1791   713   
1      0.0       0.0  0.005979  0.149477       0.0  0.006501       0.0   0.0   
2      0.0       0.0       0.0       0.0       0.0       0.0       0.0   0.0   
3      0.0       0.0  0.011957       0.0  0.017473       0.0       0.0   0.0   
4      0.0       0.0  0.005979       0.0  0.004368       0.0       0.0   0.0   
...    ...       ...       ...       ...       ...       ...       ...   ...   
2015   0.0       0.0       0.0       0.0       0.0  0.006501       0.0   0.0   
2016   0.0       0.0  0.011957       0.0  0.008737       0.0  0.055835   0.0   
2017   0.0       0.0  0.005979       0.0  0.004368       0.0       0.0   0.0   
2018   0.0  0.120482  0.005979       0.0       0.0       0.0       0.0   0.0   
2019   0.0  0.120482  0.011957       0.0  0.017473  0.006501       0.0   0.0   

         FAR_h FCS_h FFD_h     FRR_h     FTH_h GLA_h GOS_h     GRL_h  \
0         9218   525    97      3228      2290   876   508      5629   
1          0.0   0.0   0.0       0.0       0.0   0.0   0.0       0.0   
2          0.0   0.0   0.0       0.0       0.0   0.0   0.0       0.0   
3     0.032545   0.0   0.0       0.0  0.043668   0.0   0.0       0.0   
4          0.0   0.0   0.0       0.0       0.0   0.0   0.0       0.0   
...        ...   ...   ...       ...       ...   ...   ...       ...   
2015   0.06509   0.0   0.0  0.154895  0.043668   0.0   0.0  0.017765   
2016  0.075938   0.0   0.0  0.216853  0.131004   0.0   0.0  0.017765   
2017  0.010848   0.0   0.0       0.0  0.131004   0.0   0.0       0.0   
2018  0.032545   0.0   0.0       0.0  0.087336   0.0   0.0  0.017765   
2019  0.097635   0.0   0.0  0.309789  0.218341   0.0   0.0  0.053295   

         HAR_h     HDT_h     HEB_h     HER_h     HGH_h HNF_h     HOL_h  \
0         3157       366      8414     18856      8182   390     14465   
1          0.0       0.0       0.0       0.0       0.0   0.0  0.006913   
2          0.0       0.0       0.0  0.005303       0.0   0.0       0.0   
3         

In [447]:
sdf_BlockGroups = pd.DataFrame.spatial.from_featureclass(fname_BlockGroups_shp)
sdf_LEHDCommutePatterns_Percent_SA = pd.DataFrame.merge(sdf_BlockGroups, df_LEHDCommutePatterns_Percent_SA, on='GEOID')
sdf_LEHDCommutePatterns_Percent_SA

FID STATEFP COUNTYFP TRACTCE  DISTSML BLKGRPCE         GEOID  \
0        0      49      035  111306     75.0        1  490351113061   
1        1      49      035  111306     75.0        2  490351113062   
2        2      49      035  111400     47.0        1  490351114001   
3        3      49      035  111400     56.0        2  490351114002   
4        4      49      035  111400     56.0        3  490351114003   
...    ...     ...      ...     ...      ...      ...           ...   
2014  2015      49      057  200900     16.0        2  490572009002   
2015  2016      49      057  201200     15.0        1  490572012001   
2016  2017      49      057  201200     15.0        2  490572012002   
2017  2018      49      057  201301     16.0        2  490572013012   
2018  2019      49      057  201301     16.0        1  490572013011   

           NAMELSAD  MTFCC FUNCSTAT     ALAND  AWATER     INTPTLAT  \
0     Block Group 1  G5030        S  877837.0     0.0  +40.6094422   
1     Block Group 2  G5030        S  653262.0     0.0  +40.6068923   
2     Block Group 1  G5030        S  381555.0     0.0  +40.7219003   
3     Block Group 2  G5030        S  308108.0     0.0  +40.7155063   
4     Block Group 3  G5030        S  422651.0     0.0  +40.7087113   
...             ...    ...      ...       ...     ...          ...   
2014  Block Group 2  G5030        S  347700.0     0.0  +41.2248269   
2015  Block Group 1  G5030        S  752190.0     0.0  +41.2121869   
2016  Block Group 2  G5030        S  437903.0     0.0  +41.2123035   
2017  Block Group 2  G5030        S  326205.0     0.0  +41.2163706   
2018  Block Group 1  G5030        S  432925.0     0.0  +41.2162428   

          INTPTLON  CENTROID_X  CENTROID_Y     BGAcres  \
0     -111.8259365 -111.825937   40.609442  216.771411   
1     -111.8144187 -111.814419   40.606892  161.314487   
2     -111.8796932 -111.879693   40.721900   94.222093   
3     -111.8797286 -111.879729   40.715506   76.084072   
4     -111.8797335 -111.879733   40.708711  104.369581   
...            ...         ...         ...         ...   
2014  -111.9636889 -111.963689   41.224827   85.863927   
2015  -111.9783667 -111.978367   41.212187  185.752109   
2016  -111.9706612 -111.970661   41.212304  108.139051   
2017  -111.9635764 -111.963576   41.216371   80.555404   
2018  -111.9538634 -111.953863   41.216243  106.909485   

                                                  SHAPE  fakeid     AFK_h  \
0     {'rings': [[[429468.0213051503, 4496405.233871...     668  0.030157   
1     {'rings': [[[430494.91099986027, 4495540.43917...     669       0.0   
2     {'rings': [[[425457.5579433697, 4507873.987348...     670       0.0   
3     {'rings': [[[425448.36375707807, 4507253.27157...     671  0.007539   
4     {'rings': [[[425435.2029181655, 4506380.698648...     672       0.0   
...                                                 ...     ...       ...   
2014  {'rings': [[[418807.4658959587, 4564213.682993...    1887       0.0   
2015  {'rings': [[[417490.98019006505, 4562356.17136...    1891       0.0   
2016  {'rings': [[[418380.1807087121, 4562347.716705...    1892  0.022618   
2017  {'rings': [[[418871.13447070273, 4563020.29370...    1894       0.0   
2018  {'rings': [[[419571.11778565514, 4563028.08038...    1893  0.007539   

     ALA_h     ALP_h     BDL_h     BGM_h     BNT_h BRT_h CDF_h     CEN_h  \
0      0.0  0.042355  0.229095  0.030099  0.184585   0.0   0.0  0.159025   
1      0.0  0.021177  0.014318       0.0  0.019955   0.0   0.0       0.0   
2      0.0       0.0       0.0  0.010033  0.004989   0.0   0.0  0.026504   
3      0.0       0.0       0.0       0.0       0.0   0.0   0.0  0.013252   
4      0.0       0.0       0.0       0.0       0.0   0.0   0.0       0.0   
...    ...       ...       ...       ...       ...   ...   ...       ...   
2014   0.0       0.0       0.0  0.020066  0.019955   0.0   0.0  0.013252   
2015   0.0       0.0       0.0  0.070232  0.009978   0.0   0.0  0.013252   
2016   

In [448]:
sdf_LEHDCommutePatterns_Percent_SA.sum()

FID                                                   2037947
STATEFP     4949494949494949494949494949494949494949494949...
COUNTYFP    0350350350350350350350570350350350350570570570...
TRACTCE     1113061113061114001114001114001114001114002002...
DISTSML                                              163121.0
                                  ...                        
z49_w                                                   100.0
z51_h                                                   100.0
z51_w                                                   100.0
z57_h                                                   100.0
z57_w                                                   100.0
Length: 234, dtype: object

In [449]:
##create map centered on Salt Lake
##map_areas = gis.map('Salt Lake')
#
##define sdf layer
##sdf_LEHDCommutePatterns_Percent_SA.spatial.plot(map_widget = map_areas,
#                            renderer_type='s',
#                            cmap = 'RdPu',  # use a red to purple color map
#                            symbol_type='simple',
#                            outline_style='s',
#                            outline_color=[0,0,0,255],
#                            line_width=1.0)
#
##display map
#map_areas

In [450]:
#export to GDB
deleteIfExists(fname_BlockGroupsWCommutePatterns_Number)
sdf_LEHDCommutePatterns.spatial.to_featureclass(fname_BlockGroupsWCommutePatterns_Number, sanitize_columns=False)


'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2019\\LEHDCommutePatterns.gdb\\BlockGroup_CommutePatterns_Number'

In [451]:
deleteIfExists(fname_BlockGroupsWCommutePatterns_Percent_SA)
sdf_LEHDCommutePatterns_Percent_SA.spatial.to_featureclass(fname_BlockGroupsWCommutePatterns_Percent_SA, sanitize_columns=False)

'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2019\\LEHDCommutePatterns.gdb\\BlockGroup_CommutePatterns_Percent_SelectedArea'

# Group by Tract

In [452]:
#input filenames
fname_Tracts_shp = os.path.join(dirInput, 'Utah_Census_Tracts_2020' + r'\CensusTracts2020.shp')

In [453]:
#read tract shapefile
sdf_Tracts = pd.DataFrame.spatial.from_featureclass(fname_Tracts_shp)
sdf_Tracts

FID  OBJECTID STATEFP20 COUNTYFP20 TRACTCE20      GEOID20   NAME20  \
0      0         1        49        049    000901  49049000901     9.01   
1      1         2        49        049    002500  49049002500       25   
2      2         3        49        049    003401  49049003401    34.01   
3      3         4        49        049    010210  49049010210   102.10   
4      4         5        49        049    000505  49049000505     5.05   
..   ...       ...       ...        ...       ...          ...      ...   
711  711       712        49        035    111701  49035111701  1117.01   
712  712       713        49        035    111903  49035111903  1119.03   
713  713       714        49        035    111905  49035111905  1119.05   
714  714       715        49        035    113309  49035113309  1133.09   
715  715       716        49        015    976500  49015976500     9765   

       NAMELSAD20 MTFCC20 FUNCSTAT20       ALAND20    AWATER20   INTPTLAT20  \
0    Census Tract   G5020          S  1.686016e+06         0.0  +40.3051285   
1    Census Tract   G5020          S  1.034541e+06         0.0  +40.2296149   
2    Census Tract   G5020          S  9.085765e+06     23788.0  +40.0560227   
3    Census Tract   G5020          S  1.581048e+07         0.0  +40.4005884   
4    Census Tract   G5020          S  3.919712e+06         0.0  +40.3700595   
..            ...     ...        ...           ...         ...          ...   
711  Census Tract   G5020          S  1.358256e+06         0.0  +40.6934670   
712  Census Tract   G5020          S  2.072253e+06         0.0  +40.6806830   
713  Census Tract   G5020          S  1.167718e+06         0.0  +40.6765749   
714  Census Tract   G5020          S  1.867612e+06         0.0  +40.6881369   
715  Census Tract   G5020          S  8.782568e+09  14165655.0  +38.9311083   

       INTPTLON20     SHAPE_Leng    SHAPE_Area  \
0    -111.6922978    7129.054778  2.902253e+06   
1    -111.6497278    5588.845931  1.776891e+06   
2    -111.7122570   18878.825275  1.556674e+07   
3    -111.7306856   26101.425584  2.729233e+07   
4    -111.7070846   12562.893900  6.760193e+06   
..            ...            ...           ...   
711  -111.8826082    6277.757800  2.365082e+06   
712  -111.8627470    7592.371898  3.606962e+06   
713  -111.8744366    8615.733516  2.032283e+06   
714  -111.9693980    8501.284969  3.251486e+06   
715  -110.6644589  917894.696612  1.454313e+10   

                                                 SHAPE  
0    {"rings": [[[-12434548.4857, 4911361.749799997...  
1    {"rings": [[[-12429589.868, 4898990.177699998]...  
2    {"rings": [[[-12439397.559799999, 4872289.2984...  
3    {"rings": [[[-12442557.703499999, 4926512.4487...  
4    {"rings": [[[-12437368.7665, 4920654.352499999...  
..                                                 ...  
711  {"rings": [[[-12455347.0952, 4966754.840000004...  
712  {"rings": [[[-12453471.3611, 4964642.738300003...  
713  {"rings": [[[-12454528.1172, 4964343.751500003...  
714  {"rings": [[[-12465233.158599999, 4967696.3889...  
715  {"rings": [[[-12390649.8356, 4669994.337099999...  

[716 rows x 17 columns]

In [454]:
#calculate tract stats
df_LEHDCommutePatterns_tract = sdf_LEHDCommutePatterns.groupby(['STATEFP','COUNTYFP','TRACTCE'])[dColCodesWCounty].apply(lambda x : x.astype(int).sum())
df_LEHDCommutePatterns_tract = df_LEHDCommutePatterns_tract.reset_index()
display(df_LEHDCommutePatterns_tract)

#caclulate tract Percent_SA stats
df_LEHDCommutePatterns_Percent_SA_tract = sdf_LEHDCommutePatterns_Percent_SA.groupby(['STATEFP','COUNTYFP','TRACTCE'])[dColCodesWCounty].apply(lambda x : x.astype(float).sum())
df_LEHDCommutePatterns_Percent_SA_tract = df_LEHDCommutePatterns_Percent_SA_tract.reset_index()
display(df_LEHDCommutePatterns_Percent_SA_tract)


#df_test = df_LEHDCommutePatterns / df_LEHDCommutePatterns_ColSum

STATEFP COUNTYFP TRACTCE  AFK_h  ALA_h  ALP_h  BDL_h  BGM_h  BNT_h  BRT_h  \
0        49      001  100100      3      0      1      1      2      5      0   
1        49      001  100200      1      0      2      0      0      0      0   
2        49      003  960100      1      0      0      0     62      2      0   
3        49      003  960200      0      0      0      0    197      4      0   
4        49      003  960301      1      0      0      0     76      3      0   
..      ...      ...     ...    ...    ...    ...    ...    ...    ...    ...   
711      49      057  210900      5      0      0      2     17     37      0   
712      49      057  211000      0      0      0      0      8      2      0   
713      49      057  211100      6      0      2      2     48     44      0   
714      49      057  211201      0      0      0      1     16      9      0   
715      49      057  211202      5      0      4      3     15     36      0   

     CDF_h  CEN_h  CHA_h  CHL_h  CLF_h  CLI_h  CMT_h  COA_h  CWH_h  DAN_h  \
0        0      1      0      1      2      3      0      0      3      1   
1        0      0      0      0      0      0      0      0      2      0   
2        0      0      0      0      7      5      0      0      1      0   
3        0      1      0      0      4      5      0      0      2      0   
4        0      0      0      0      4      2      0      0      3      0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
711      1     12      0      1     50     40      0      2      7      0   
712      0      2      0      0     12     11      0      0      1      0   
713      0     10      0      1     71    102      0      2      1      0   
714      0      2      0      1     23     24      0      0      4      0   
715      1     21      0      1     75     77      0      2      6      0   

     DRA_h  EAG_h  ELK_h  EMT_h  FAR_h  FCS_h  FFD_h  FRR_h  FTH_h  GLA_h  \
0        4      1      0      0      3      0      0      0      1      0   
1        3      0      0      0      0      0      0      0      0      0   
2        5      2      0      0      0      0      0      1      1      0   
3        2      1      0      0      0      1      0      6      1      0   
4        3      1      1      0      1      0      0      2      0      0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
711      8      3      0      1     26      0      0     34     10      1   
712      0      0      0      0      0      0      0      9      1      0   
713      4      4      0      1     11      0      0     68     14      1   
714      2      2      0      1     12      0      0     19      4      0   
715      7      2      1      0     26      0      0     22     14      0   

     GOS_h  GRL_h  HAR_h  HDT_h  HEB_h  HER_h  HGH_h  HNF_h  HOL_h  HOO_h  \
0        0      0      0      0      0      2      0      0      1      0   
1        0      0      0      0      1      2      4      0      0      0   
2        0      2      4      0      0      0      0      0      0      3   
3        0      4      2      0      0      2      2      0      2      2   
4        0      2      1      0      1      1      0      0      0      2   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
711      0      5     19      0      1      6      4      1     11     25   
712      0      1      5      0      0      0      0      0      0      4   
713      0      0     60      0      0      2      1      1      4     53   
714      0      2     15      0      0      2      1      0      1     20   
715      0      6     26      1      3      3      3      0      4     35   

     HVL_h  IND_h  INT_h  KAY_h  KMS_h  KMT_h  LAY_h  LEH_h  LIN_h  MAP_h  \
0        0      0      0      2      0      4      4      2      1      2   
1        0      0      0      0      0      0      0      4      2      0   
2        0      0      0 

STATEFP COUNTYFP TRACTCE     AFK_h  ALA_h     ALP_h     BDL_h     BGM_h  \
0        49      001  100100  0.022618    0.0  0.021177  0.014318  0.020066   
1        49      001  100200  0.007539    0.0  0.042355  0.000000  0.000000   
2        49      003  960100  0.007539    0.0  0.000000  0.000000  0.622053   
3        49      003  960200  0.000000    0.0  0.000000  0.000000  1.976523   
4        49      003  960301  0.007539    0.0  0.000000  0.000000  0.762516   
..      ...      ...     ...       ...    ...       ...       ...       ...   
711      49      057  210900  0.037696    0.0  0.000000  0.028637  0.170563   
712      49      057  211000  0.000000    0.0  0.000000  0.000000  0.080265   
713      49      057  211100  0.045235    0.0  0.042355  0.028637  0.481589   
714      49      057  211201  0.000000    0.0  0.000000  0.014318  0.160530   
715      49      057  211202  0.037696    0.0  0.084710  0.042955  0.150497   

        BNT_h  BRT_h     CDF_h     CEN_h  CHA_h     CHL_h     CLF_h     CLI_h  \
0    0.024944    0.0  0.000000  0.013252    0.0  0.021791  0.014467  0.028977   
1    0.000000    0.0  0.000000  0.000000    0.0  0.000000  0.000000  0.000000   
2    0.009978    0.0  0.000000  0.000000    0.0  0.000000  0.050633  0.048295   
3    0.019955    0.0  0.000000  0.013252    0.0  0.000000  0.028933  0.048295   
4    0.014966    0.0  0.000000  0.000000    0.0  0.000000  0.028933  0.019318   
..        ...    ...       ...       ...    ...       ...       ...       ...   
711  0.184585    0.0  0.304878  0.159025    0.0  0.021791  0.361664  0.386361   
712  0.009978    0.0  0.000000  0.026504    0.0  0.000000  0.086799  0.106249   
713  0.219506    0.0  0.000000  0.132521    0.0  0.021791  0.513562  0.985222   
714  0.044899    0.0  0.000000  0.026504    0.0  0.021791  0.166365  0.231817   
715  0.179596    0.0  0.304878  0.278293    0.0  0.021791  0.542495  0.743746   

     CMT_h     COA_h     CWH_h     DAN_h     DRA_h     EAG_h     ELK_h  \
0      0.0  0.000000  0.017936  0.149477  0.017473  0.006501  0.000000   
1      0.0  0.000000  0.011957  0.000000  0.013105  0.000000  0.000000   
2      0.0  0.000000  0.005979  0.000000  0.021842  0.013002  0.000000   
3      0.0  0.000000  0.011957  0.000000  0.008737  0.006501  0.000000   
4      0.0  0.000000  0.017936  0.000000  0.013105  0.006501  0.055835   
..     ...       ...       ...       ...       ...       ...       ...   
711    0.0  0.240964  0.041851  0.000000  0.034947  0.019503  0.000000   
712    0.0  0.000000  0.005979  0.000000  0.000000  0.000000  0.000000   
713    0.0  0.240964  0.005979  0.000000  0.017473  0.026004  0.000000   
714    0.0  0.000000  0.023915  0.000000  0.008737  0.013002  0.000000   
715    0.0  0.240964  0.035872  0.000000  0.030578  0.013002  0.055835   

        EMT_h     FAR_h     FCS_h  FFD_h     FRR_h     FTH_h     GLA_h  GOS_h  \
0    0.000000  0.032545  0.000000    0.0  0.000000  0.043668  0.000000    0.0   
1    0.000000  0.000000  0.000000    0.0  0.000000  0.000000  0.000000    0.0   
2    0.000000  0.000000  0.000000    0.0  0.030979  0.043668  0.000000    0.0   
3    0.000000  0.000000  0.190476    0.0  0.185874  0.043668  0.000000    0.0   
4    0.000000  0.010848  0.000000    0.0  0.061958  0.000000  0.000000    0.0   
..        ...       ...       ...    ...       ...       ...       ...    ...   
711  0.140252  0.282057  0.000000    0.0  1.053284  0.436681  0.114155    0.0   
712  0.000000  0.000000  0.000000    0.0  0.278810  0.043668  0.000000    0.0   
713  0.140252  0.119332  0.000000    0.0  2.106568  0.611354  0.114155    0.0   
714  0.140252  0.130180  0.000000    0.0  0.588600  0.174672  0.000000    0.0   
715  0.000000  0.282057  0.000000    0.0  0.681537  0.611354  0.000000    0.0   

        GRL_h     HAR_h     HDT_h     HEB_h     HER_h     HGH_h    HNF_h  \
0    0.000000  0.000000  0.000000  0.000000  0.010607  0.000000  0.00000   
1    0.000000  0.000000  0.000000  0.011885  0.010607  0.048888  0.0

In [455]:
df_LEHDCommutePatterns_Percent_SA_tract.sum()

STATEFP     4949494949494949494949494949494949494949494949...
COUNTYFP    0010010030030030030030030030030030030030030050...
TRACTCE     1001001002009601009602009603019603029604009605...
AFK_h                                                   100.0
ALA_h                                                   100.0
                                  ...                        
z49_w                                                   100.0
z51_h                                                   100.0
z51_w                                                   100.0
z57_h                                                   100.0
z57_w                                                   100.0
Length: 219, dtype: object

In [456]:
sdf_LEHDCommutePatterns_tract = pd.DataFrame.merge(sdf_Tracts, df_LEHDCommutePatterns_tract, left_on=['STATEFP20','COUNTYFP20','TRACTCE20'], right_on=['STATEFP','COUNTYFP',"TRACTCE"])
display(sdf_LEHDCommutePatterns_tract)

sdf_LEHDCommutePatterns_Percent_SA_tract = pd.DataFrame.merge(sdf_Tracts, df_LEHDCommutePatterns_Percent_SA_tract, left_on=['STATEFP20','COUNTYFP20','TRACTCE20'], right_on=['STATEFP','COUNTYFP',"TRACTCE"])
display(sdf_LEHDCommutePatterns_Percent_SA_tract)

FID  OBJECTID STATEFP20 COUNTYFP20 TRACTCE20      GEOID20   NAME20  \
0      0         1        49        049    000901  49049000901     9.01   
1      1         2        49        049    002500  49049002500       25   
2      2         3        49        049    003401  49049003401    34.01   
3      3         4        49        049    010210  49049010210   102.10   
4      4         5        49        049    000505  49049000505     5.05   
..   ...       ...       ...        ...       ...          ...      ...   
711  711       712        49        035    111701  49035111701  1117.01   
712  712       713        49        035    111903  49035111903  1119.03   
713  713       714        49        035    111905  49035111905  1119.05   
714  714       715        49        035    113309  49035113309  1133.09   
715  715       716        49        015    976500  49015976500     9765   

       NAMELSAD20 MTFCC20 FUNCSTAT20       ALAND20    AWATER20   INTPTLAT20  \
0    Census Tract   G5020          S  1.686016e+06         0.0  +40.3051285   
1    Census Tract   G5020          S  1.034541e+06         0.0  +40.2296149   
2    Census Tract   G5020          S  9.085765e+06     23788.0  +40.0560227   
3    Census Tract   G5020          S  1.581048e+07         0.0  +40.4005884   
4    Census Tract   G5020          S  3.919712e+06         0.0  +40.3700595   
..            ...     ...        ...           ...         ...          ...   
711  Census Tract   G5020          S  1.358256e+06         0.0  +40.6934670   
712  Census Tract   G5020          S  2.072253e+06         0.0  +40.6806830   
713  Census Tract   G5020          S  1.167718e+06         0.0  +40.6765749   
714  Census Tract   G5020          S  1.867612e+06         0.0  +40.6881369   
715  Census Tract   G5020          S  8.782568e+09  14165655.0  +38.9311083   

       INTPTLON20     SHAPE_Leng    SHAPE_Area  \
0    -111.6922978    7129.054778  2.902253e+06   
1    -111.6497278    5588.845931  1.776891e+06   
2    -111.7122570   18878.825275  1.556674e+07   
3    -111.7306856   26101.425584  2.729233e+07   
4    -111.7070846   12562.893900  6.760193e+06   
..            ...            ...           ...   
711  -111.8826082    6277.757800  2.365082e+06   
712  -111.8627470    7592.371898  3.606962e+06   
713  -111.8744366    8615.733516  2.032283e+06   
714  -111.9693980    8501.284969  3.251486e+06   
715  -110.6644589  917894.696612  1.454313e+10   

                                                 SHAPE STATEFP COUNTYFP  \
0    {'rings': [[[-12434548.4857, 4911361.749799997...      49      049   
1    {'rings': [[[-12429589.868, 4898990.177699998]...      49      049   
2    {'rings': [[[-12439397.559799999, 4872289.2984...      49      049   
3    {'rings': [[[-12442557.703499999, 4926512.4487...      49      049   
4    {'rings': [[[-12437368.7665, 4920654.352499999...      49      049   
..                                                 ...     ...      ...   
711  {'rings': [[[-12455347.0952, 4966754.840000004...      49      035   
712  {'rings': [[[-12453471.3611, 4964642.738300003...      49      035   
713  {'rings': [[[-12454528.1172, 4964343.751500003...      49      035   
714  {'rings': [[[-12465233.158599999, 4967696.3889...      49      035   
715  {'rings': [[[-12390649.8356, 4669994.337099999...      49      015   

    TRACTCE  AFK_h  ALA_h  ALP_h  BDL_h  BGM_h  BNT_h  BRT_h  CDF_h  CEN_h  \
0    000901     59      0     19     10     17      7      1      0      5   
1    002500     25      1      3      0      0      2      0      0      1   
2    003401      3      0      3      5      1      5      0      0      0   
3    010210     33      0      8      1      1      1      0      0      0   
4    000505     11      0      2      1      0      1      0      2      0   
..      ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
711  111701      3      0      0      5      2     12      0      1      7   
712  111903     33      5    

FID  OBJECTID STATEFP20 COUNTYFP20 TRACTCE20      GEOID20   NAME20  \
0      0         1        49        049    000901  49049000901     9.01   
1      1         2        49        049    002500  49049002500       25   
2      2         3        49        049    003401  49049003401    34.01   
3      3         4        49        049    010210  49049010210   102.10   
4      4         5        49        049    000505  49049000505     5.05   
..   ...       ...       ...        ...       ...          ...      ...   
711  711       712        49        035    111701  49035111701  1117.01   
712  712       713        49        035    111903  49035111903  1119.03   
713  713       714        49        035    111905  49035111905  1119.05   
714  714       715        49        035    113309  49035113309  1133.09   
715  715       716        49        015    976500  49015976500     9765   

       NAMELSAD20 MTFCC20 FUNCSTAT20       ALAND20    AWATER20   INTPTLAT20  \
0    Census Tract   G5020          S  1.686016e+06         0.0  +40.3051285   
1    Census Tract   G5020          S  1.034541e+06         0.0  +40.2296149   
2    Census Tract   G5020          S  9.085765e+06     23788.0  +40.0560227   
3    Census Tract   G5020          S  1.581048e+07         0.0  +40.4005884   
4    Census Tract   G5020          S  3.919712e+06         0.0  +40.3700595   
..            ...     ...        ...           ...         ...          ...   
711  Census Tract   G5020          S  1.358256e+06         0.0  +40.6934670   
712  Census Tract   G5020          S  2.072253e+06         0.0  +40.6806830   
713  Census Tract   G5020          S  1.167718e+06         0.0  +40.6765749   
714  Census Tract   G5020          S  1.867612e+06         0.0  +40.6881369   
715  Census Tract   G5020          S  8.782568e+09  14165655.0  +38.9311083   

       INTPTLON20     SHAPE_Leng    SHAPE_Area  \
0    -111.6922978    7129.054778  2.902253e+06   
1    -111.6497278    5588.845931  1.776891e+06   
2    -111.7122570   18878.825275  1.556674e+07   
3    -111.7306856   26101.425584  2.729233e+07   
4    -111.7070846   12562.893900  6.760193e+06   
..            ...            ...           ...   
711  -111.8826082    6277.757800  2.365082e+06   
712  -111.8627470    7592.371898  3.606962e+06   
713  -111.8744366    8615.733516  2.032283e+06   
714  -111.9693980    8501.284969  3.251486e+06   
715  -110.6644589  917894.696612  1.454313e+10   

                                                 SHAPE STATEFP COUNTYFP  \
0    {'rings': [[[-12434548.4857, 4911361.749799997...      49      049   
1    {'rings': [[[-12429589.868, 4898990.177699998]...      49      049   
2    {'rings': [[[-12439397.559799999, 4872289.2984...      49      049   
3    {'rings': [[[-12442557.703499999, 4926512.4487...      49      049   
4    {'rings': [[[-12437368.7665, 4920654.352499999...      49      049   
..                                                 ...     ...      ...   
711  {'rings': [[[-12455347.0952, 4966754.840000004...      49      035   
712  {'rings': [[[-12453471.3611, 4964642.738300003...      49      035   
713  {'rings': [[[-12454528.1172, 4964343.751500003...      49      035   
714  {'rings': [[[-12465233.158599999, 4967696.3889...      49      035   
715  {'rings': [[[-12390649.8356, 4669994.337099999...      49      015   

    TRACTCE     AFK_h     ALA_h     ALP_h     BDL_h     BGM_h     BNT_h  \
0    000901  0.444813  0.000000  0.402372  0.143184  0.170563  0.034921   
1    002500  0.188480  0.520833  0.063532  0.000000  0.000000  0.009978   
2    003401  0.022618  0.000000  0.063532  0.071592  0.010033  0.024944   
3    010210  0.248794  0.000000  0.169420  0.014318  0.010033  0.004989   
4    000505  0.082931  0.000000  0.042355  0.014318  0.000000  0.004989   
..      ...       ...       ...       ...       ...       ...       ...   
711  111701  0.022618  0.000000  0.000000  0.071592  0.020066  0.059865   
712  111903  0.248794  2.604167  0.317662  0.658648  

In [457]:
sdf_LEHDCommutePatterns_tract.sum()


FID                                                      255970
OBJECTID                                                 256686
STATEFP20     4949494949494949494949494949494949494949494949...
COUNTYFP20    0490490490490490490490510130490490490490490490...
TRACTCE20     0009010025000034010102100005050005070102099601...
                                    ...                        
z49_w                                                    240735
z51_h                                                     12428
z51_w                                                      8044
z57_h                                                    110179
z57_w                                                    101860
Length: 235, dtype: object

In [458]:
sdf_LEHDCommutePatterns_Percent_SA_tract.sum()

FID                                                      255970
OBJECTID                                                 256686
STATEFP20     4949494949494949494949494949494949494949494949...
COUNTYFP20    0490490490490490490490510130490490490490490490...
TRACTCE20     0009010025000034010102100005050005070102099601...
                                    ...                        
z49_w                                                     100.0
z51_h                                                     100.0
z51_w                                                     100.0
z57_h                                                     100.0
z57_w                                                     100.0
Length: 235, dtype: object

In [459]:
sdf_LEHDCommutePatterns_tract.spatial.to_featureclass(fname_TractsWCommutePatterns_Number, sanitize_columns=False)

'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2019\\LEHDCommutePatterns.gdb\\Tract_CommutePatterns_Number'

In [460]:
sdf_LEHDCommutePatterns_Percent_SA_tract.spatial.to_featureclass(fname_TractsWCommutePatterns_Percent_SA, sanitize_columns=False)

'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2019\\LEHDCommutePatterns.gdb\\Tract_CommutePatterns_Percent_SelectedArea'

# Group by Small District

In [461]:
#input filenames
fname_SD_shp = os.path.join(dirInput, 'Dist_Small' + r'\Dist_Small_Counties.shp')

In [462]:
sdf_SD = pd.DataFrame.spatial.from_featureclass(fname_SD_shp)
sdf_SD

FID  DISTSML                         DSML_NAME STATEFP20 COUNTYFP20  \
0      0      1.0           1.1: Brigham City North        49        003   
1      1      2.0    2.1: Brigham City West of I-15        49        003   
2      2      3.0  3.1: Brigham City West and Perry        49        003   
3      3      4.0          3.2: Brigham City Center        49        003   
4      4      5.0                      4.1: Willard        49        003   
..   ...      ...                               ...       ...        ...   
150  150    151.0  99.1: Outside WFRC Modeling Area        49        031   
151  151    152.0  99.1: Outside WFRC Modeling Area        49        021   
152  152    153.0  99.1: Outside WFRC Modeling Area        49        055   
153  153    154.0  99.1: Outside WFRC Modeling Area        49        037   
154  154    155.0  99.1: Outside WFRC Modeling Area        49        025   

                                                 SHAPE  
0    {"rings": [[[412988.500000001, 4605724.4], [41...  
1    {"rings": [[[408196.8937999996, 4599532.781500...  
2    {"rings": [[[413636.79999999964, 4598064.69999...  
3    {"rings": [[[415302.1999999995, 4598736.699999...  
4    {"rings": [[[412551.0000000001, 4588753.600000...  
..                                                 ...  
150  {"rings": [[[384022.18659999967, 4263333.3738]...  
151  {"rings": [[[292688.5865000002, 4224956.9639],...  
152  {"rings": [[[438313.3267000001, 4262656.513800...  
153  {"rings": [[[609343.4170000004, 4095382.083499...  
154  {"rings": [[[425313.8965999996, 4154648.073699...  

[155 rows x 6 columns]

In [463]:
#calculate small district stats
df_LEHDCommutePatterns_sd = sdf_LEHDCommutePatterns.groupby(['STATEFP','COUNTYFP','DISTSML'])[dColCodesWCounty].apply(lambda x : x.astype(int).sum())
df_LEHDCommutePatterns_sd = df_LEHDCommutePatterns_sd.reset_index()
display(df_LEHDCommutePatterns_sd)

#caclulate tract Percent_SA stats
df_LEHDCommutePatterns_Percent_SA_sd = sdf_LEHDCommutePatterns_Percent_SA.groupby(['STATEFP','COUNTYFP','DISTSML'])[dColCodesWCounty].apply(lambda x : x.astype(float).sum())
df_LEHDCommutePatterns_Percent_SA_sd = df_LEHDCommutePatterns_Percent_SA_sd.reset_index()
display(df_LEHDCommutePatterns_Percent_SA_sd)


#df_test = df_LEHDCommutePatterns / df_LEHDCommutePatterns_ColSum

STATEFP COUNTYFP  DISTSML  AFK_h  ALA_h  ALP_h  BDL_h  BGM_h  BNT_h  \
0        49      001    149.0      4      0      3      1      2      5   
1        49      003      1.0      0      0      0      0    167      1   
2        49      003      2.0      0      0      0      0     31      3   
3        49      003      3.0      2      0      1      3    671     11   
4        49      003      4.0      4      0      3      0   1852     18   
..      ...      ...      ...    ...    ...    ...    ...    ...    ...   
143      49      057     17.0     26      0     14     10    158    154   
144      49      057     18.0     28      1      6     11    101    184   
145      49      057     19.0      3      0      1      0     32     59   
146      49      057    124.0      1      1      0      0     26      9   
147      49      057    147.0      3      0      3      2     30     11   

     BRT_h  CDF_h  CEN_h  CHA_h  CHL_h  CLF_h  CLI_h  CMT_h  COA_h  CWH_h  \
0        0      0      1      0      1      2      3      0      0      5   
1        0      0      2      0      0      6      4      0      0      0   
2        0      0      1      0      1      2      2      0      0      0   
3        0      0      3      0      3     17      5      0      0      3   
4        0      0      4      0      1     35     30      0      2     10   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
143      0      2     63      2     14    422    416      0      6     33   
144      0      1     65      1     12    274    227      0      4     50   
145      0      0     15      1      1     44     71      0      1      3   
146      0      0      2      0      0     38     43      0      2      2   
147      0      0     14      0      1     29     33      1      2      6   

     DAN_h  DRA_h  EAG_h  ELK_h  EMT_h  FAR_h  FCS_h  FFD_h  FRR_h  FTH_h  \
0        1      7      1      0      0      3      0      0      0      1   
1        0      1      1      0      0      0      0      0      6      1   
2        0      0      0      0      0      0      0      0      4      0   
3        0      3      3      0      0      6      0      0     22      0   
4        0      9      5      1      0      9      1      0     29      4   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
143      1     42     30      5      2     86      1      0    177     43   
144      2     52     37      5      3     75      1      0    112     29   
145      0      5      2      0      1     24      0      0     20      5   
146      0      5      0      0      0      1      0      0     39      1   
147      0     10      2      1      1     21      2      0     14      8   

     GLA_h  GOS_h  GRL_h  HAR_h  HDT_h  HEB_h  HER_h  HGH_h  HNF_h  HOL_h  \
0        0      0      0      0      0      1      4      4      0      1   
1        0      0      0      7      0      1      1      1      0      0   
2        0      0      1      4      0      0      0      1      0      0   
3        0      0      4     10      0      3      2      1      1      2   
4        1      0     12     32      1     14      6      4      0      7   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
143      2      0     26    196      1     32     23     12      1     28   
144      2      2     16     89      0     33     32     21      3     41   
145      0      0      0     36      0      0      2      1      0      4   
146      0      0      2     30      0      0      1      1      3      0   
147      0      0      0     19      0      8      4      3      1      6   

     HOO_h  HVL_h  IND_h  INT_h  KAY_h  KMS_h  KMT_h  LAY_h  LEH_h  LIN_h  \
0        0      0      0      0      2      0      4      4      6      3   
1        2      0      0      0      0      1      0     13      0      0   
2        1      0      0      0      2      0      0     16      0      0   
3        9      1   

STATEFP COUNTYFP  DISTSML     AFK_h     ALA_h     ALP_h     BDL_h  \
0        49      001    149.0  0.030157  0.000000  0.063532  0.014318   
1        49      003      1.0  0.000000  0.000000  0.000000  0.000000   
2        49      003      2.0  0.000000  0.000000  0.000000  0.000000   
3        49      003      3.0  0.015078  0.000000  0.021177  0.042955   
4        49      003      4.0  0.030157  0.000000  0.063532  0.000000   
..      ...      ...      ...       ...       ...       ...       ...   
143      49      057     17.0  0.196019  0.000000  0.296485  0.143184   
144      49      057     18.0  0.211098  0.520833  0.127065  0.157503   
145      49      057     19.0  0.022618  0.000000  0.021177  0.000000   
146      49      057    124.0  0.007539  0.520833  0.000000  0.000000   
147      49      057    147.0  0.022618  0.000000  0.063532  0.028637   

         BGM_h     BNT_h  BRT_h     CDF_h     CEN_h     CHA_h     CHL_h  \
0     0.020066  0.024944    0.0  0.000000  0.013252  0.000000  0.021791   
1     1.675529  0.004989    0.0  0.000000  0.026504  0.000000  0.000000   
2     0.311026  0.014966    0.0  0.000000  0.013252  0.000000  0.021791   
3     6.732216  0.054877    0.0  0.000000  0.039756  0.000000  0.065374   
4    18.581318  0.089798    0.0  0.000000  0.053008  0.000000  0.021791   
..         ...       ...    ...       ...       ...       ...       ...   
143   1.585231  0.768271    0.0  0.609756  0.834879  0.735294  0.305077   
144   1.013344  0.917935    0.0  0.304878  0.861384  0.367647  0.261495   
145   0.321059  0.294338    0.0  0.000000  0.198781  0.367647  0.021791   
146   0.260861  0.044899    0.0  0.000000  0.026504  0.000000  0.000000   
147   0.300993  0.054877    0.0  0.000000  0.185529  0.000000  0.021791   

        CLF_h     CLI_h    CMT_h     COA_h     CWH_h     DAN_h     DRA_h  \
0    0.014467  0.028977  0.00000  0.000000  0.029894  0.149477  0.030578   
1    0.043400  0.038636  0.00000  0.000000  0.000000  0.000000  0.004368   
2    0.014467  0.019318  0.00000  0.000000  0.000000  0.000000  0.000000   
3    0.122966  0.048295  0.00000  0.000000  0.017936  0.000000  0.013105   
4    0.253165  0.289771  0.00000  0.240964  0.059787  0.000000  0.039315   
..        ...       ...      ...       ...       ...       ...       ...   
143  3.052441  4.018159  0.00000  0.722892  0.197298  0.149477  0.183470   
144  1.981917  2.192601  0.00000  0.481928  0.298936  0.298954  0.227154   
145  0.318264  0.685792  0.00000  0.120482  0.017936  0.000000  0.021842   
146  0.274864  0.415339  0.00000  0.240964  0.011957  0.000000  0.021842   
147  0.209765  0.318748  0.19084  0.240964  0.035872  0.000000  0.043683   

        EAG_h     ELK_h     EMT_h     FAR_h     FCS_h  FFD_h     FRR_h  \
0    0.006501  0.000000  0.000000  0.032545  0.000000    0.0  0.000000   
1    0.006501  0.000000  0.000000  0.000000  0.000000    0.0  0.185874   
2    0.000000  0.000000  0.000000  0.000000  0.000000    0.0  0.123916   
3    0.019503  0.000000  0.000000  0.065090  0.000000    0.0  0.681537   
4    0.032506  0.055835  0.000000  0.097635  0.190476    0.0  0.898389   
..        ...       ...       ...       ...       ...    ...       ...   
143  0.195033  0.279174  0.280505  0.932957  0.190476    0.0  5.483271   
144  0.240541  0.279174  0.420757  0.813626  0.190476    0.0  3.469641   
145  0.013002  0.000000  0.140252  0.260360  0.000000    0.0  0.619579   
146  0.000000  0.000000  0.000000  0.010848  0.000000    0.0  1.208178   
147  0.013002  0.055835  0.140252  0.227815  0.380952    0.0  0.433705   

        FTH_h     GLA_h     GOS_h     GRL_h     HAR_h     HDT_h     HEB_h  \
0    0.043668  0.000000  0.000000  0.000000  0.000000  0.000000  0.011885   
1    0.043668  0.000000  0.000000  0.000000  0.221729  0.000000  0.011885   
2    0.000000  0.000000  0.000000  0.017765  0.126703  0.000000  0.000000   
3    0.000000  0.000000  0.000000  0.071061  0.316756  0.000000  0.035655   
4    0.174672  0.114155  0.000000  0.21

In [464]:
df_LEHDCommutePatterns_Percent_SA_sd.sum()

STATEFP     4949494949494949494949494949494949494949494949...
COUNTYFP    0010030030030030030030030050070090110110110110...
DISTSML                                               11772.0
AFK_h                                                   100.0
ALA_h                                                   100.0
                                  ...                        
z49_w                                                   100.0
z51_h                                                   100.0
z51_w                                                   100.0
z57_h                                                   100.0
z57_w                                                   100.0
Length: 219, dtype: object

In [465]:
sdf_LEHDCommutePatterns_sd = pd.DataFrame.merge(sdf_SD, df_LEHDCommutePatterns_sd, left_on=['STATEFP20','COUNTYFP20','DISTSML'], right_on=['STATEFP','COUNTYFP',"DISTSML"])
display(sdf_LEHDCommutePatterns_sd)

sdf_LEHDCommutePatterns_Percent_SA_sd = pd.DataFrame.merge(sdf_SD, df_LEHDCommutePatterns_Percent_SA_sd, left_on=['STATEFP20','COUNTYFP20','DISTSML'], right_on=['STATEFP','COUNTYFP',"DISTSML"])
display(sdf_LEHDCommutePatterns_Percent_SA_sd)

FID  DISTSML                         DSML_NAME STATEFP20 COUNTYFP20  \
0      0      1.0           1.1: Brigham City North        49        003   
1      1      2.0    2.1: Brigham City West of I-15        49        003   
2      2      3.0  3.1: Brigham City West and Perry        49        003   
3      3      4.0          3.2: Brigham City Center        49        003   
4      5      6.0       5.1: Mantua and Sardine Cyn        49        003   
..   ...      ...                               ...       ...        ...   
142  150    151.0  99.1: Outside WFRC Modeling Area        49        031   
143  151    152.0  99.1: Outside WFRC Modeling Area        49        021   
144  152    153.0  99.1: Outside WFRC Modeling Area        49        055   
145  153    154.0  99.1: Outside WFRC Modeling Area        49        037   
146  154    155.0  99.1: Outside WFRC Modeling Area        49        025   

                                                 SHAPE STATEFP COUNTYFP  \
0    {'rings': [[[412988.500000001, 4605724.4], [41...      49      003   
1    {'rings': [[[408196.8937999996, 4599532.781500...      49      003   
2    {'rings': [[[413636.79999999964, 4598064.69999...      49      003   
3    {'rings': [[[415302.1999999995, 4598736.699999...      49      003   
4    {'rings': [[[416806.00000000023, 4602635.50000...      49      003   
..                                                 ...     ...      ...   
142  {'rings': [[[384022.18659999967, 4263333.3738]...      49      031   
143  {'rings': [[[292688.5865000002, 4224956.9639],...      49      021   
144  {'rings': [[[438313.3267000001, 4262656.513800...      49      055   
145  {'rings': [[[609343.4170000004, 4095382.083499...      49      037   
146  {'rings': [[[425313.8965999996, 4154648.073699...      49      025   

     AFK_h  ALA_h  ALP_h  BDL_h  BGM_h  BNT_h  BRT_h  CDF_h  CEN_h  CHA_h  \
0        0      0      0      0    167      1      0      0      2      0   
1        0      0      0      0     31      3      0      0      1      0   
2        2      0      1      3    671     11      0      0      3      0   
3        4      0      3      0   1852     18      0      0      4      0   
4        0      0      0      0     32      1      0      0      0      0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
142      0      0      0      0      0      0      0      0      0      0   
143     17      0     12      4     12     19      0      2      3      1   
144      6      0      2      0      2      1      0      0      0      0   
145      0      0      1      1      2      3      0      0      0      0   
146      3      0      0      1      1      0      0      0      0      0   

     CHL_h  CLF_h  CLI_h  CMT_h  COA_h  CWH_h  DAN_h  DRA_h  EAG_h  ELK_h  \
0        0      6      4      0      0      0      0      1      1      0   
1        1      2      2      0      0      0      0      0      0      0   
2        3     17      5      0      0      3      0      3      3      0   
3        1     35     30      0      2     10      0      9      5      1   
4        0      1      3      0      0      0      0      0      2      0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
142      0      0      0      0      1      0      0      0      0      0   
143      6      5      7      1      1     19      1     26     22      2   
144      1      1      0      0      0      2      0      4      2      1   
145      2      2      2      0      0      1      0      1      3      0   
146      1      0      0      0      0      5      1      7      3      0   

     EMT_h  FAR_h  FCS_h  FFD_h  FRR_h  FTH_h  GLA_h  GOS_h  GRL_h  HAR_h  \
0        0      0      0      0      6      1      0      0      0      7   
1        0      0      0      0      4      0      0      0      1      4   
2        0      6      0      0     22      0      0      0      4     10   
3        0      9      1      0  

FID  DISTSML                         DSML_NAME STATEFP20 COUNTYFP20  \
0      0      1.0           1.1: Brigham City North        49        003   
1      1      2.0    2.1: Brigham City West of I-15        49        003   
2      2      3.0  3.1: Brigham City West and Perry        49        003   
3      3      4.0          3.2: Brigham City Center        49        003   
4      5      6.0       5.1: Mantua and Sardine Cyn        49        003   
..   ...      ...                               ...       ...        ...   
142  150    151.0  99.1: Outside WFRC Modeling Area        49        031   
143  151    152.0  99.1: Outside WFRC Modeling Area        49        021   
144  152    153.0  99.1: Outside WFRC Modeling Area        49        055   
145  153    154.0  99.1: Outside WFRC Modeling Area        49        037   
146  154    155.0  99.1: Outside WFRC Modeling Area        49        025   

                                                 SHAPE STATEFP COUNTYFP  \
0    {'rings': [[[412988.500000001, 4605724.4], [41...      49      003   
1    {'rings': [[[408196.8937999996, 4599532.781500...      49      003   
2    {'rings': [[[413636.79999999964, 4598064.69999...      49      003   
3    {'rings': [[[415302.1999999995, 4598736.699999...      49      003   
4    {'rings': [[[416806.00000000023, 4602635.50000...      49      003   
..                                                 ...     ...      ...   
142  {'rings': [[[384022.18659999967, 4263333.3738]...      49      031   
143  {'rings': [[[292688.5865000002, 4224956.9639],...      49      021   
144  {'rings': [[[438313.3267000001, 4262656.513800...      49      055   
145  {'rings': [[[609343.4170000004, 4095382.083499...      49      037   
146  {'rings': [[[425313.8965999996, 4154648.073699...      49      025   

        AFK_h  ALA_h     ALP_h     BDL_h      BGM_h     BNT_h  BRT_h  \
0    0.000000    0.0  0.000000  0.000000   1.675529  0.004989    0.0   
1    0.000000    0.0  0.000000  0.000000   0.311026  0.014966    0.0   
2    0.015078    0.0  0.021177  0.042955   6.732216  0.054877    0.0   
3    0.030157    0.0  0.063532  0.000000  18.581318  0.089798    0.0   
4    0.000000    0.0  0.000000  0.000000   0.321059  0.004989    0.0   
..        ...    ...       ...       ...        ...       ...    ...   
142  0.000000    0.0  0.000000  0.000000   0.000000  0.000000    0.0   
143  0.128166    0.0  0.254130  0.057274   0.120397  0.094787    0.0   
144  0.045235    0.0  0.042355  0.000000   0.020066  0.004989    0.0   
145  0.000000    0.0  0.021177  0.014318   0.020066  0.014966    0.0   
146  0.022618    0.0  0.000000  0.014318   0.010033  0.000000    0.0   

        CDF_h     CEN_h     CHA_h     CHL_h     CLF_h     CLI_h    CMT_h  \
0    0.000000  0.026504  0.000000  0.000000  0.043400  0.038636  0.00000   
1    0.000000  0.013252  0.000000  0.021791  0.014467  0.019318  0.00000   
2    0.000000  0.039756  0.000000  0.065374  0.122966  0.048295  0.00000   
3    0.000000  0.053008  0.000000  0.021791  0.253165  0.289771  0.00000   
4    0.000000  0.000000  0.000000  0.000000  0.007233  0.028977  0.00000   
..        ...       ...       ...       ...       ...       ...      ...   
142  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.00000   
143  0.609756  0.039756  0.367647  0.130747  0.036166  0.067613  0.19084   
144  0.000000  0.000000  0.000000  0.021791  0.007233  0.000000  0.00000   
145  0.000000  0.000000  0.000000  0.043582  0.014467  0.019318  0.00000   
146  0.000000  0.000000  0.000000  0.021791  0.000000  0.000000  0.00000   

        COA_h     CWH_h     DAN_h     DRA_h     EAG_h     ELK_h     EMT_h  \
0    0.000000  0.000000  0.000000  0.004368  0.006501  0.000000  0.000000   
1    0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2    0.000000  0.017936  0.000000  0.013105  0.019503  0.000000  0.000000   
3    0.240964  0.059787  0.000000  0.039315  0.032506  0.055835  0.000000   
4    0.000000  0.000000  0.0

In [466]:
sdf_LEHDCommutePatterns_sd.sum()

FID                                                       11507
DISTSML                                                 11654.0
DSML_NAME     1.1: Brigham City North2.1: Brigham City West ...
STATEFP20     4949494949494949494949494949494949494949494949...
COUNTYFP20    0030030030030030570030570570570570570570570570...
                                    ...                        
z49_w                                                    240573
z51_h                                                     12428
z51_w                                                      8041
z57_h                                                    110179
z57_w                                                    101843
Length: 223, dtype: object

In [467]:
sdf_LEHDCommutePatterns_Percent_SA_sd.sum()

FID                                                       11507
DISTSML                                                 11654.0
DSML_NAME     1.1: Brigham City North2.1: Brigham City West ...
STATEFP20     4949494949494949494949494949494949494949494949...
COUNTYFP20    0030030030030030570030570570570570570570570570...
                                    ...                        
z49_w                                                 99.932706
z51_h                                                     100.0
z51_w                                                 99.962705
z57_h                                                     100.0
z57_w                                                  99.98331
Length: 223, dtype: object

In [468]:
sdf_LEHDCommutePatterns_sd.spatial.to_featureclass(fname_SDWCommutePatterns_Number, sanitize_columns=False)

'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2019\\LEHDCommutePatterns.gdb\\SD_CommutePatterns_Number'

In [469]:
sdf_LEHDCommutePatterns_Percent_SA_sd.spatial.to_featureclass(fname_SDWCommutePatterns_Percent_SA, sanitize_columns=False)

'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2019\\LEHDCommutePatterns.gdb\\SD_CommutePatterns_Percent_SelectedArea'

# Group Rows by City

In [470]:

#verify that shape exists and sdf was created correctly and get spatial reference
#print(sdf_CityTownship.iloc[0].SHAPE.spatialReference)
#print(sdf_BlockGroups.iloc[0].SHAPE.spatialReference)
#
##change projection to 26912 to match TAZ Centroids
#sdf_CityTownship.spatial.project(26912)
#sdf_BlockGroups.spatial.project(26912)
#
#print(sdf_CityTownship.iloc[0].SHAPE.spatialReference)
#print(sdf_BlockGroups.iloc[0].SHAPE.spatialReference)

print ("Calculating blockgroup acreage...")

# Execute DeleteField
arcpy.DeleteField_management(fname_BlockGroups_shp, ['BGAcres'])

arcpy.AddField_management(fname_BlockGroups_shp, "BGAcres" , "DOUBLE")
arcpy.CalculateField_management(fname_BlockGroups_shp,
                                "BGAcres",
                                "!shape.area@acres!",
                                "PYTHON_9.3")
print ("Done calculating blockgroup acreage.")


print ("Intersecting blockgroup with city/township/county...")
#intersection parcels with analysis area types
deleteIfExists(fname_CityTownshipCounty_BlockGroups_shp)
arcpy.analysis.Intersect([fname_CityTownshipCountyWCodes_shp,fname_BlockGroups_shp], fname_CityTownshipCounty_BlockGroups_shp)


print ("Calculating piece area...")
arcpy.AddField_management(fname_CityTownshipCounty_BlockGroups_shp, "PieceAcres" , "DOUBLE")
arcpy.CalculateField_management(fname_CityTownshipCounty_BlockGroups_shp,
                                "PieceAcres",
                                "!shape.area@acres!",
                                "PYTHON_9.3")
print ("Calculating Percent_SA of blockgroup...")
arcpy.AddField_management(fname_CityTownshipCounty_BlockGroups_shp, "PortionBG" , "DOUBLE")
arcpy.CalculateField_management(fname_CityTownshipCounty_BlockGroups_shp,
                                "PortionBG",
                                "!PieceAcres!/!BGAcres!",
                                "PYTHON_9.3")


print ("Done")

Calculating blockgroup acreage...
Done calculating blockgroup acreage.
Intersecting blockgroup with city/township/county...
Calculating piece area...
Calculating Percent_SA of blockgroup...
Done


In [471]:
#read newly created shapefile
sdf_CityTownshipCounty_BlockGroups = pd.DataFrame.spatial.from_featureclass(fname_CityTownshipCounty_BlockGroups_shp)


In [472]:
sdf_LEHDCommutePatterns_joinCity = pd.DataFrame.merge(sdf_CityTownshipCounty_BlockGroups,sdf_LEHDCommutePatterns,on=['GEOID','STATEFP','COUNTYFP','TRACTCE','DISTSML','BLKGRPCE','NAMELSAD','MTFCC', 'FUNCSTAT','ALAND','AWATER','INTPTLAT','INTPTLON','BGAcres'])
sdf_LEHDCommutePatterns_joinCity

FID_x  FID_Munici  Id  FID_Muni_1 CODE3  \
0         0           0   0          -1   z05   
1       238           5   0          -1   z03   
2       288           6   0          -1   z57   
3      2156          90   0          55   NOG   
4         1           0   0          -1   z05   
...     ...         ...  ..         ...   ...   
3622   3551         139   0          96   WVC   
3623   3552         139   0          96   WVC   
3624   3553         139   0          96   WVC   
3625   3554         139   0          96   WVC   
3626   3558         139   0          96   WVC   

                           FIRST_NAME  FID_tl_202 STATEFP COUNTYFP TRACTCE  \
0         Cache County Unincorporated          95      49      057  210101   
1     Box Elder County Unincorporated          95      49      057  210101   
2         Weber County Unincorporated          95      49      057  210101   
3                         North Ogden          95      49      057  210101   
4         Cache County Unincorporated         578      49      005  001101   
...                               ...         ...     ...      ...     ...   
3622                 West Valley City        1666      49      035  113537   
3623                 West Valley City        1673      49      035  113309   
3624                 West Valley City        1681      49      035  113409   
3625                 West Valley City        1885      49      035  113309   
3626                 West Valley City        1907      49      035  113414   

      DISTSML BLKGRPCE         GEOID       NAMELSAD  MTFCC FUNCSTAT  \
0       147.0        1  490572101011  Block Group 1  G5030        S   
1       147.0        1  490572101011  Block Group 1  G5030        S   
2       147.0        1  490572101011  Block Group 1  G5030        S   
3       147.0        1  490572101011  Block Group 1  G5030        S   
4       130.0        1  490050011011  Block Group 1  G5030        S   
...       ...      ...           ...            ...    ...      ...   
3622     43.0        1  490351135371  Block Group 1  G5030        S   
3623     43.0        1  490351133091  Block Group 1  G5030        S   
3624     37.0        3  490351134093  Block Group 3  G5030        S   
3625     43.0        2  490351133092  Block Group 2  G5030        S   
3626     37.0        1  490351134141  Block Group 1  G5030        S   

           ALAND   AWATER     INTPTLAT      INTPTLON  CENTROID_X_x  \
0     86898873.0  19742.0  +41.3700825  -111.9334158   -111.919266   
1     86898873.0  19742.0  +41.3700825  -111.9334158   -111.919266   
2     86898873.0  19742.0  +41.3700825  -111.9334158   -111.919266   
3     86898873.0  19742.0  +41.3700825  -111.9334158   -111.919266   
4      2552940.0      0.0  +41.7149272  -111.8231317   -111.823132   
...          ...      ...          ...           ...           ...   
3622    651043.0      0.0  +40.6784813  -111.9722719   -111.972272   
3623    650128.0      0.0  +40.6929994  -111.9723023   -111.972302   
3624    685688.0      0.0  +40.6858633  -112.0391343   -112.039134   
3625    649958.0      0.0  +40.6857436  -111.9722922   -111.972292   
3626    929713.0      0.0  +40.7012857  -112.0324271   -112.032427   

      CENTROID_Y_x       BGAcres    PieceAcres  PortionBG  \
0        41.372480  21464.006346      2.821747   0.000131   
1        41.372480  21464.006346      0.887017   0.000041   
2        41.372480  21464.006346  20832.493173   0.970578   
3        41.372480  21464.006346    641.857708   0.029904   
4        41.714927    630.412036    630.843690   1.000685   
...            ...           ...           ...        ...   
3622     40.678481    160.774214    160.876163   1.000634   
3623     40.692999    160.548274    160.650081   1.000634   
3624     40.685863    169.334283    169.437669   1.000611   
3625     40.685744    160.506512    160.608298   1.000634   
3626     40.701286    229.596643    229.737391   1.000613   

                                                SHAPE

In [473]:
my_list = list(sdf_LEHDCommutePatterns_joinCity)
my_list

['FID_x',
 'FID_Munici',
 'Id',
 'FID_Muni_1',
 'CODE3',
 'FIRST_NAME',
 'FID_tl_202',
 'STATEFP',
 'COUNTYFP',
 'TRACTCE',
 'DISTSML',
 'BLKGRPCE',
 'GEOID',
 'NAMELSAD',
 'MTFCC',
 'FUNCSTAT',
 'ALAND',
 'AWATER',
 'INTPTLAT',
 'INTPTLON',
 'CENTROID_X_x',
 'CENTROID_Y_x',
 'BGAcres',
 'PieceAcres',
 'PortionBG',
 'SHAPE_x',
 'FID_y',
 'CENTROID_X_y',
 'CENTROID_Y_y',
 'SHAPE_y',
 'fakeid',
 'AFK_h',
 'ALA_h',
 'ALP_h',
 'BDL_h',
 'BGM_h',
 'BNT_h',
 'BRT_h',
 'CDF_h',
 'CEN_h',
 'CHA_h',
 'CHL_h',
 'CLF_h',
 'CLI_h',
 'CMT_h',
 'COA_h',
 'CWH_h',
 'DAN_h',
 'DRA_h',
 'EAG_h',
 'ELK_h',
 'EMT_h',
 'FAR_h',
 'FCS_h',
 'FFD_h',
 'FRR_h',
 'FTH_h',
 'GLA_h',
 'GOS_h',
 'GRL_h',
 'HAR_h',
 'HDT_h',
 'HEB_h',
 'HER_h',
 'HGH_h',
 'HNF_h',
 'HOL_h',
 'HOO_h',
 'HVL_h',
 'IND_h',
 'INT_h',
 'KAY_h',
 'KMS_h',
 'KMT_h',
 'LAY_h',
 'LEH_h',
 'LIN_h',
 'MAP_h',
 'MID_h',
 'MLC_h',
 'MMT_h',
 'MRG_h',
 'MSL_h',
 'MUR_h',
 'MWY_h',
 'NOG_h',
 'NSL_h',
 'OGD_h',
 'OKL_h',
 'ORM_h',
 'PAY_h',
 'PG

In [474]:
#for i in dColCodes:
#    display(sdf_LEHDCommutePatterns_joinCity[[i]])

In [475]:
df_LEHDCommutePatterns_CityCalcs = sdf_LEHDCommutePatterns_joinCity.copy()

for i in dColCodesWCounty:
    display(i)
    
    df_LEHDCommutePatterns_CityCalcs[i] = df_LEHDCommutePatterns_CityCalcs[i] * df_LEHDCommutePatterns_CityCalcs['PortionBG']


'AFK_h'

'ALA_h'

'ALP_h'

'BDL_h'

'BGM_h'

...

'z49_w'

'z51_h'

'z51_w'

'z57_h'

'z57_w'

In [476]:
df_LEHDCommutePatterns_CityCalcs = df_LEHDCommutePatterns_CityCalcs.rename(columns={"first_name":"FIRST_NAME", "code3":"CODE3"})
df_LEHDCommutePatterns_CityCalcs

FID_x  FID_Munici  Id  FID_Muni_1 CODE3  \
0         0           0   0          -1   z05   
1       238           5   0          -1   z03   
2       288           6   0          -1   z57   
3      2156          90   0          55   NOG   
4         1           0   0          -1   z05   
...     ...         ...  ..         ...   ...   
3622   3551         139   0          96   WVC   
3623   3552         139   0          96   WVC   
3624   3553         139   0          96   WVC   
3625   3554         139   0          96   WVC   
3626   3558         139   0          96   WVC   

                           FIRST_NAME  FID_tl_202 STATEFP COUNTYFP TRACTCE  \
0         Cache County Unincorporated          95      49      057  210101   
1     Box Elder County Unincorporated          95      49      057  210101   
2         Weber County Unincorporated          95      49      057  210101   
3                         North Ogden          95      49      057  210101   
4         Cache County Unincorporated         578      49      005  001101   
...                               ...         ...     ...      ...     ...   
3622                 West Valley City        1666      49      035  113537   
3623                 West Valley City        1673      49      035  113309   
3624                 West Valley City        1681      49      035  113409   
3625                 West Valley City        1885      49      035  113309   
3626                 West Valley City        1907      49      035  113414   

      DISTSML BLKGRPCE         GEOID       NAMELSAD  MTFCC FUNCSTAT  \
0       147.0        1  490572101011  Block Group 1  G5030        S   
1       147.0        1  490572101011  Block Group 1  G5030        S   
2       147.0        1  490572101011  Block Group 1  G5030        S   
3       147.0        1  490572101011  Block Group 1  G5030        S   
4       130.0        1  490050011011  Block Group 1  G5030        S   
...       ...      ...           ...            ...    ...      ...   
3622     43.0        1  490351135371  Block Group 1  G5030        S   
3623     43.0        1  490351133091  Block Group 1  G5030        S   
3624     37.0        3  490351134093  Block Group 3  G5030        S   
3625     43.0        2  490351133092  Block Group 2  G5030        S   
3626     37.0        1  490351134141  Block Group 1  G5030        S   

           ALAND   AWATER     INTPTLAT      INTPTLON  CENTROID_X_x  \
0     86898873.0  19742.0  +41.3700825  -111.9334158   -111.919266   
1     86898873.0  19742.0  +41.3700825  -111.9334158   -111.919266   
2     86898873.0  19742.0  +41.3700825  -111.9334158   -111.919266   
3     86898873.0  19742.0  +41.3700825  -111.9334158   -111.919266   
4      2552940.0      0.0  +41.7149272  -111.8231317   -111.823132   
...          ...      ...          ...           ...           ...   
3622    651043.0      0.0  +40.6784813  -111.9722719   -111.972272   
3623    650128.0      0.0  +40.6929994  -111.9723023   -111.972302   
3624    685688.0      0.0  +40.6858633  -112.0391343   -112.039134   
3625    649958.0      0.0  +40.6857436  -111.9722922   -111.972292   
3626    929713.0      0.0  +40.7012857  -112.0324271   -112.032427   

      CENTROID_Y_x       BGAcres    PieceAcres  PortionBG  \
0        41.372480  21464.006346      2.821747   0.000131   
1        41.372480  21464.006346      0.887017   0.000041   
2        41.372480  21464.006346  20832.493173   0.970578   
3        41.372480  21464.006346    641.857708   0.029904   
4        41.714927    630.412036    630.843690   1.000685   
...            ...           ...           ...        ...   
3622     40.678481    160.774214    160.876163   1.000634   
3623     40.692999    160.548274    160.650081   1.000634   
3624     40.685863    169.334283    169.437669   1.000611   
3625     40.685744    160.506512    160.608298   1.000634   
3626     40.701286    229.596643    229.737391   1.000613   

                                                SHAPE

In [477]:
df_LEHDCommutePatterns_CityCalcsSum = df_LEHDCommutePatterns_CityCalcs.groupby(['CODE3','FIRST_NAME'], as_index=False)[dColCodesWCounty].apply(lambda x : x.astype(int).sum())
df_LEHDCommutePatterns_CityCalcsSum = df_LEHDCommutePatterns_CityCalcsSum.reset_index()
df_LEHDCommutePatterns_CityCalcsSum

index CODE3                        FIRST_NAME  AFK_h  ALA_h  ALP_h  \
0        0   AFK                     American Fork   1849      0    306   
1        1   ALA                              Alta      1      1      1   
2        2   ALP                            Alpine    100      0    274   
3        3   BDL                         Bluffdale     58      0     22   
4        4   BGM                      Brigham City      6      0      4   
..     ...   ...                               ...    ...    ...    ...   
121    121   z49        Utah County Unincorporated    508      0     95   
122    122   z51     Wasatch County Unincorporated     14      0      0   
123    123   z53  Washington County Unincorporated     28      0      5   
124    124   z55       Wayne County Unincorporated      6      0      2   
125    125   z57       Weber County Unincorporated      2      0      2   

     BDL_h  BGM_h  BNT_h  BRT_h  CDF_h  CEN_h  CHA_h  CHL_h  CLF_h  CLI_h  \
0      137     50     91      0     16     29      1    327     54     27   
1        1      0      1      0      0      1      0      0      0      0   
2       11      2      8      0      0      2      0     69      3      1   
3      379      2     18      0      9      5      0     13     13      4   
4        0   2308     21      0      0      6      0      4     41     34   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
121     50     18     33      0      6     10      2    143     21      8   
122      1      2      7      0      0      2     26      1      2      2   
123      3     18     24      0      0     13      0     15     16      9   
124      0      2      1      0      0      0      0      1      1      0   
125      1    121     44      0      0     25      0      3    143    170   

     CMT_h  COA_h  CWH_h  DAN_h  DRA_h  EAG_h  ELK_h  EMT_h  FAR_h  FCS_h  \
0        5      3     82      4    464    849     27      4     30      1   
1        0      0     49      0     10      1      0      0      0      0   
2        0      1     20      0     54     71      3      0      2      0   
3        1      1     44      0    156    149      5      0      9      0   
4        0      2     11      0     11      6      1      0     10      1   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
121      0      1     39      1    156    352    210      0     11      0   
122      0      6      5     50      8     19      0      0      3      7   
123      0      0     29      1     57     46      0      1     13      0   
124      0      0      2      0      4      2      1      0      0      0   
125      1      2     11      0     17      4      1      1     35      2   

     FFD_h  FRR_h  FTH_h  GLA_h  GOS_h  GRL_h  HAR_h  HDT_h  HEB_h  HER_h  \
0        6      7      6      8      7     33      6      0     99    309   
1        0      0      0      0      0      0      0      0      0      2   
2        0      1      0      1      0     54      0      0      4     27   
3        2      0      0      2      0     12      0      0      7    166   
4        0     40      4      1      0     13     42      1     15      8   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
121      1      4      3    109     52     12      0      0     38     98   
122      0      1      0      0      0      2      1     20    750      5   
123      0      1      1      0      0     10      2      0     10     21   
124      0      0      0      1      0      1      0      0      0      2   
125      0    113     10      0      0      4    102      0     11      5   

     HGH_h  HNF_h  HOL_h  HOO_h  HVL_h  IND_h  INT_h  KAY_h  KMS_h  KMT_h  \
0      613      6     77     11      0      1      0     65      3     95   
1        1      0     18      0      0      0      0      0      0      2   
2      161      1      7      0      0      0      0      2      4      9   
3       47      1    

In [478]:
df_LEHDCommutePatterns_CityCalcsSum.sum()

index                                                      7875
CODE3         AFKALAALPBDLBGMBNTBRTCDFCENCHACHLCLFCLICMTCOAC...
FIRST_NAME    American ForkAltaAlpineBluffdaleBrigham CityBo...
AFK_h                                                     12753
ALA_h                                                       141
                                    ...                        
z49_w                                                    239906
z51_h                                                     11966
z51_w                                                      7450
z57_h                                                    109465
z57_w                                                    101013
Length: 219, dtype: object

In [479]:
sdf_LEHDCommutePatterns_joinCity_Percent_SA = pd.DataFrame.merge(sdf_CityTownshipCounty_BlockGroups,sdf_LEHDCommutePatterns_Percent_SA,on=['GEOID','STATEFP','COUNTYFP','TRACTCE','DISTSML','BLKGRPCE','NAMELSAD','MTFCC', 'FUNCSTAT','ALAND','AWATER','INTPTLAT','INTPTLON','BGAcres'])
sdf_LEHDCommutePatterns_joinCity_Percent_SA = sdf_LEHDCommutePatterns_joinCity_Percent_SA.rename(columns={"first_name":"FIRST_NAME", "code3":"CODE3"})
df_LEHDCommutePatterns_CityCalcs_Percent_SA = sdf_LEHDCommutePatterns_joinCity_Percent_SA.copy()

for i in dColCodesWCounty:    
    df_LEHDCommutePatterns_CityCalcs_Percent_SA[i] = df_LEHDCommutePatterns_CityCalcs_Percent_SA[i] * df_LEHDCommutePatterns_CityCalcs_Percent_SA['PortionBG']


display(df_LEHDCommutePatterns_CityCalcs_Percent_SA.sum())
    
df_LEHDCommutePatterns_CityCalcs_Percent_SA = df_LEHDCommutePatterns_CityCalcs_Percent_SA.fillna(0)
   

df_LEHDCommutePatterns_CityCalcsSum_Percent_SA = df_LEHDCommutePatterns_CityCalcs_Percent_SA.groupby(['CODE3','FIRST_NAME'], as_index=False)[dColCodesWCounty].apply(lambda x : x.astype(float).sum())
df_LEHDCommutePatterns_CityCalcsSum_Percent_SA = df_LEHDCommutePatterns_CityCalcsSum_Percent_SA.reset_index()
df_LEHDCommutePatterns_CityCalcsSum_Percent_SA
    
display(df_LEHDCommutePatterns_CityCalcsSum_Percent_SA.sum())

FID_x                                                   6578904
FID_Munici                                               251195
Id                                                            0
FID_Muni_1                                               139499
CODE3         z05z03z57NOGz05z05z05z05z05z05z05z05z05z05z03z...
                                    ...                        
z49_w                                                 100.06754
z51_h                                                100.071169
z51_w                                                100.071353
z57_h                                                100.063355
z57_w                                                100.062624
Length: 245, dtype: object

index                                                      7875
CODE3         AFKALAALPBDLBGMBNTBRTCDFCENCHACHLCLFCLICMTCOAC...
FIRST_NAME    American ForkAltaAlpineBluffdaleBrigham CityBo...
AFK_h                                                100.067783
ALA_h                                                100.066626
                                    ...                        
z49_w                                                 100.06754
z51_h                                                100.071169
z51_w                                                100.071353
z57_h                                                100.063355
z57_w                                                100.062624
Length: 219, dtype: object

In [480]:
sdf_LEHDCommutePatterns_City_Number = pd.DataFrame.merge(sdf_CityTownshipWCodes,df_LEHDCommutePatterns_CityCalcsSum,on=['CODE3','FIRST_NAME'])
sdf_LEHDCommutePatterns_City_Percent_SA = pd.DataFrame.merge(sdf_CityTownshipWCodes,df_LEHDCommutePatterns_CityCalcsSum_Percent_SA,on=['CODE3','FIRST_NAME'])

In [481]:
sdf_LEHDCommutePatterns_City_Number.spatial.to_featureclass(fname_CitiesWCommutePatterns_Number, sanitize_columns=False)

'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2019\\LEHDCommutePatterns.gdb\\City_CommutePatterns_Number'

In [482]:
sdf_LEHDCommutePatterns_City_Percent_SA.spatial.to_featureclass(fname_CitiesWCommutePatterns_Percent_SA, sanitize_columns=False)

'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2019\\LEHDCommutePatterns.gdb\\City_CommutePatterns_Percent_SelectedArea'

In [483]:
sdf_LEHDCommutePatterns_City_Number

OBJECTID CODE3        FIRST_NAME FIRST_COUNTYNBR  \
0          1   AFK     American Fork              25   
1          2   ALA              Alta              18   
2          3   ALP            Alpine              25   
3          4   BDL         Bluffdale              18   
4          5   BGM      Brigham City              02   
..       ...   ...               ...             ...   
92        93   WIL           Willard              02   
93        94   WJC       West Jordan              18   
94        95   WPT        West Point              06   
95        96   WVC  West Valley City              18   
96        97   WXC       Woods Cross              06   

                                                SHAPE  index  AFK_h  ALA_h  \
0   {"rings": [[[-111.77435121873373, 40.353624868...      0   1849      0   
1   {"rings": [[[-111.59946851855727, 40.577431980...      1      1      1   
2   {"rings": [[[-111.75455302160464, 40.479513910...      2    100      0   
3   {"rings": [[[-111.9704071902396, 40.5008379065...      3     58      0   
4   {"rings": [[[-112.01898409573937, 41.535781784...      4      6      0   
..                                                ...    ...    ...    ...   
92  {"rings": [[[-112.02999503963935, 41.391465965...     92      0      0   
93  {"rings": [[[-112.00475852158849, 40.638664299...     93    127      4   
94  {"rings": [[[-112.10779328273378, 41.143687479...     94      0      0   
95  {"rings": [[[-111.9626132723846, 40.7260972067...     95    185      5   
96  {"rings": [[[-111.89260269236036, 40.866220107...     96      4      0   

    ALP_h  BDL_h  BGM_h  BNT_h  BRT_h  CDF_h  CEN_h  CHA_h  CHL_h  CLF_h  \
0     306    137     50     91      0     16     29      1    327     54   
1       1      1      0      1      0      0      1      0      0      0   
2     274     11      2      8      0      0      2      0     69      3   
3      22    379      2     18      0      9      5      0     13     13   
4       4      0   2308     21      0      0      6      0      4     41   
..    ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
92      0      0      6      0      0      0      0      0      0      0   
93     76    390     82    209      0     14     57      3     43    134   
94      0      1      6     22      0      0     14      0      0     67   
95    104    314    165    945      3      5    336      0     71    392   
96      0     12     10    552      0      0    186      0     10     91   

    CLI_h  CMT_h  COA_h  CWH_h  DAN_h  DRA_h  EAG_h  ELK_h  EMT_h  FAR_h  \
0      27      5      3     82      4    464    849     27      4     30   
1       0      0      0     49      0     10      1      0      0      0   
2       1      0      1     20      0     54     71      3      0      2   
3       4      1      1     44      0    156    149      5      0      9   
4      34      0      2     11      0     11      6      1      0     10   
..    ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
92      0      0      0      0      0      0      0      0      0      0   
93     72     28      7    390      5    740    472     19     10     77   
94     85      0      0      2      1      1      0      0      0     13   
95    268     35     14    819      5    881    458     27     30    378   
96     53      0      0     37      0     39     11      0      1    205   

    FCS_h  FFD_h  FRR_h  FTH_h  GLA_h  GOS_h  GRL_h  HAR_h  HDT_h  HEB_h  \
0       1      6      7      6      8      7     33      6      0     99   
1       0      0      0      0      0      0      0      0      0      0   
2       0      0      1      0      1      0     54      0      0      4   
3       0      2      0      0      2      0     12      0      0      7   
4       1      0     40      4      1      0     13     42      1     15   
..    ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
92      0      0      0      0      

# Calculate Percents by Map Units

In [484]:
# prepare column list

#display(dColCodesWCounty)
dColCodesWCounty = dColCodesWCounty.copy()

dColCodesWCounty_x = [x for x in dColCodesWCounty if "w" not in x]
dColCodesWCounty_y = [x for x in dColCodesWCounty if "h" not in x]

#remove and append to make sure at end
dColCodesWCounty_x.remove('TTL_h')
dColCodesWCounty_y.remove('TTL_w')
dColCodesWCounty_x.append('TTL_h')
dColCodesWCounty_y.append('TTL_w')

display(dColCodesWCounty_x)
display(dColCodesWCounty_y)

dColCodesNoTotal_x = [x for x in dColCodes if "w" not in x]
dColCodesNoTotal_x.remove('TTL_h')

dColCodesNoTotal_x = [x for x in dColCodes if "h" not in x]
dColCodesNoTotal_x.remove('TTL_w')

['AFK_h',
 'ALA_h',
 'ALP_h',
 'BDL_h',
 'BGM_h',
 'BNT_h',
 'BRT_h',
 'CDF_h',
 'CEN_h',
 'CHA_h',
 'CHL_h',
 'CLF_h',
 'CLI_h',
 'CMT_h',
 'COA_h',
 'CWH_h',
 'DAN_h',
 'DRA_h',
 'EAG_h',
 'ELK_h',
 'EMT_h',
 'FAR_h',
 'FCS_h',
 'FFD_h',
 'FRR_h',
 'FTH_h',
 'GLA_h',
 'GOS_h',
 'GRL_h',
 'HAR_h',
 'HDT_h',
 'HEB_h',
 'HER_h',
 'HGH_h',
 'HNF_h',
 'HOL_h',
 'HOO_h',
 'HVL_h',
 'IND_h',
 'INT_h',
 'KAY_h',
 'KMS_h',
 'KMT_h',
 'LAY_h',
 'LEH_h',
 'LIN_h',
 'MAP_h',
 'MID_h',
 'MLC_h',
 'MMT_h',
 'MRG_h',
 'MSL_h',
 'MUR_h',
 'MWY_h',
 'NOG_h',
 'NSL_h',
 'OGD_h',
 'OKL_h',
 'ORM_h',
 'PAY_h',
 'PGR_h',
 'PLN_h',
 'PRK_h',
 'PRY_h',
 'PVO_h',
 'PVW_h',
 'ROY_h',
 'RVD_h',
 'RVT_h',
 'SAN_h',
 'SAQ_h',
 'SAR_h',
 'SFK_h',
 'SJC_h',
 'SLC_h',
 'SLM_h',
 'SOG_h',
 'SPV_h',
 'SSL_h',
 'SUN_h',
 'SWE_h',
 'SYR_h',
 'TAY_h',
 'TOO_h',
 'UIN_h',
 'VIN_h',
 'WAT_h',
 'WBG_h',
 'WDL_h',
 'WEB_h',
 'WHT_h',
 'WHV_h',
 'WIL_h',
 'WJC_h',
 'WPT_h',
 'WVC_h',
 'WXC_h',
 'z03_h',
 'z11_h',
 'z23_h',


['AFK_w',
 'ALA_w',
 'ALP_w',
 'BDL_w',
 'BGM_w',
 'BNT_w',
 'BRT_w',
 'CDF_w',
 'CEN_w',
 'CHA_w',
 'CHL_w',
 'CLF_w',
 'CLI_w',
 'CMT_w',
 'COA_w',
 'CWH_w',
 'DAN_w',
 'DRA_w',
 'EAG_w',
 'ELK_w',
 'EMT_w',
 'FAR_w',
 'FCS_w',
 'FFD_w',
 'FRR_w',
 'FTH_w',
 'GLA_w',
 'GOS_w',
 'GRL_w',
 'HAR_w',
 'HDT_w',
 'HEB_w',
 'HER_w',
 'HGH_w',
 'HNF_w',
 'HOL_w',
 'HOO_w',
 'HVL_w',
 'IND_w',
 'INT_w',
 'KAY_w',
 'KMS_w',
 'KMT_w',
 'LAY_w',
 'LEH_w',
 'LIN_w',
 'MAP_w',
 'MID_w',
 'MLC_w',
 'MMT_w',
 'MRG_w',
 'MSL_w',
 'MUR_w',
 'MWY_w',
 'NOG_w',
 'NSL_w',
 'OGD_w',
 'OKL_w',
 'ORM_w',
 'PAY_w',
 'PGR_w',
 'PLN_w',
 'PRK_w',
 'PRY_w',
 'PVO_w',
 'PVW_w',
 'ROY_w',
 'RVD_w',
 'RVT_w',
 'SAN_w',
 'SAQ_w',
 'SAR_w',
 'SFK_w',
 'SJC_w',
 'SLC_w',
 'SLM_w',
 'SOG_w',
 'SPV_w',
 'SSL_w',
 'SUN_w',
 'SWE_w',
 'SYR_w',
 'TAY_w',
 'TOO_w',
 'UIN_w',
 'VIN_w',
 'WAT_w',
 'WBG_w',
 'WDL_w',
 'WEB_w',
 'WHT_w',
 'WHV_w',
 'WIL_w',
 'WJC_w',
 'WPT_w',
 'WVC_w',
 'WXC_w',
 'z03_w',
 'z11_w',
 'z23_w',


In [485]:
# block group
sdf_LEHDCommutePatterns_Percent_MU = sdf_LEHDCommutePatterns.copy()
sdf_LEHDCommutePatterns_tract_Percent_MU  = sdf_LEHDCommutePatterns_tract.copy()
sdf_LEHDCommutePatterns_sd_Percent_MU  = sdf_LEHDCommutePatterns_sd.copy()
sdf_LEHDCommutePatterns_City_Percent_MU  = sdf_LEHDCommutePatterns_City_Number.copy()

for x in dColCodesWCounty_x:   
    #display(x)
    sdf_LEHDCommutePatterns_Percent_MU      [x] = sdf_LEHDCommutePatterns_Percent_MU      [x] / sdf_LEHDCommutePatterns_Percent_MU      ['TTL_h'] * 100
    sdf_LEHDCommutePatterns_tract_Percent_MU[x] = sdf_LEHDCommutePatterns_tract_Percent_MU[x] / sdf_LEHDCommutePatterns_tract_Percent_MU['TTL_h'] * 100
    sdf_LEHDCommutePatterns_sd_Percent_MU   [x] = sdf_LEHDCommutePatterns_sd_Percent_MU   [x] / sdf_LEHDCommutePatterns_sd_Percent_MU   ['TTL_h'] * 100
    sdf_LEHDCommutePatterns_City_Percent_MU [x] = sdf_LEHDCommutePatterns_City_Percent_MU [x] / sdf_LEHDCommutePatterns_City_Percent_MU ['TTL_h'] * 100

for y in dColCodesWCounty_y:   
    #display(y)
    sdf_LEHDCommutePatterns_Percent_MU      [y] = sdf_LEHDCommutePatterns_Percent_MU      [y] / sdf_LEHDCommutePatterns_Percent_MU      ['TTL_w'] * 100
    sdf_LEHDCommutePatterns_tract_Percent_MU[y] = sdf_LEHDCommutePatterns_tract_Percent_MU[y] / sdf_LEHDCommutePatterns_tract_Percent_MU['TTL_w'] * 100
    sdf_LEHDCommutePatterns_sd_Percent_MU   [y] = sdf_LEHDCommutePatterns_sd_Percent_MU   [y] / sdf_LEHDCommutePatterns_sd_Percent_MU   ['TTL_w'] * 100    
    sdf_LEHDCommutePatterns_City_Percent_MU [y] = sdf_LEHDCommutePatterns_City_Percent_MU [y] / sdf_LEHDCommutePatterns_City_Percent_MU ['TTL_w'] * 100
    

In [486]:
#check that everything is near 100 (subtracting out non-city areas)
display(sdf_LEHDCommutePatterns_Percent_MU      .loc[:,dColCodesNoTotal_x].sum(axis=1))
display(sdf_LEHDCommutePatterns_tract_Percent_MU.loc[:,dColCodesNoTotal_x].sum(axis=1))
display(sdf_LEHDCommutePatterns_sd_Percent_MU   .loc[:,dColCodesNoTotal_x].sum(axis=1))
display(sdf_LEHDCommutePatterns_City_Percent_MU .loc[:,dColCodesNoTotal_x].sum(axis=1))

0       95.533981
1       97.297297
2       96.930533
3       96.046512
4       96.831956
          ...    
2014    89.660266
2015    93.019197
2016    94.117647
2017    93.838028
2018    92.363112
Length: 2019, dtype: float64

0      95.579030
1      95.714286
2      91.923486
3      95.407308
4      96.595461
         ...    
711    96.901203
712    97.477164
713    97.253306
714    97.843666
715    20.638086
Length: 716, dtype: float64

0      79.973298
1      83.083333
2      82.751323
3      79.714912
4      82.070707
         ...    
142    25.055432
143    14.939594
144    18.190757
145     7.089921
146    10.738714
Length: 147, dtype: float64

0     92.210803
1     77.685950
2     92.106471
3     94.305373
4     78.928974
        ...    
92    66.319444
93    95.950145
94    90.119605
95    96.407587
96    90.161224
Length: 97, dtype: float64

In [487]:
#export to GDB
deleteIfExists(fname_BlockGroupsWCommutePatterns_Percent_MU)
deleteIfExists(fname_TractsWCommutePatterns_Percent_MU     )
deleteIfExists(fname_SDWCommutePatterns_Percent_MU         )
deleteIfExists(fname_CitiesWCommutePatterns_Percent_MU     )

sdf_LEHDCommutePatterns_Percent_MU      .spatial.to_featureclass(fname_BlockGroupsWCommutePatterns_Percent_MU, sanitize_columns=False)
sdf_LEHDCommutePatterns_tract_Percent_MU.spatial.to_featureclass(fname_TractsWCommutePatterns_Percent_MU     , sanitize_columns=False)
sdf_LEHDCommutePatterns_sd_Percent_MU   .spatial.to_featureclass(fname_SDWCommutePatterns_Percent_MU         , sanitize_columns=False)
sdf_LEHDCommutePatterns_City_Percent_MU .spatial.to_featureclass(fname_CitiesWCommutePatterns_Percent_MU     , sanitize_columns=False)

'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2019\\LEHDCommutePatterns.gdb\\City_CommutePatterns_Percent_MapUnit'

# Summarize by County

In [488]:
df_CityTownship_NameCode

NAME CODE3 zCOFIPS
0           Alpine   ALP     z49
1    American Fork   AFK     z49
2       Cedar Fort   CDF     z49
3      Cedar Hills   CHL     z49
4   Eagle Mountain   EAG     z49
..             ...   ...     ...
92      West Haven   WHV     z57
93     Grantsville   GRL     z45
94          Tooele   TOO     z45
95          Morgan   MRG     z29
96       Santaquin   SAQ     z23

[97 rows x 3 columns]

In [489]:
display(df_LEHDCommutePatterns_CityCalcsSum)
display(df_LEHDCommutePatterns_CityCalcsSum_Percent_SA)

index CODE3                        FIRST_NAME  AFK_h  ALA_h  ALP_h  \
0        0   AFK                     American Fork   1849      0    306   
1        1   ALA                              Alta      1      1      1   
2        2   ALP                            Alpine    100      0    274   
3        3   BDL                         Bluffdale     58      0     22   
4        4   BGM                      Brigham City      6      0      4   
..     ...   ...                               ...    ...    ...    ...   
121    121   z49        Utah County Unincorporated    508      0     95   
122    122   z51     Wasatch County Unincorporated     14      0      0   
123    123   z53  Washington County Unincorporated     28      0      5   
124    124   z55       Wayne County Unincorporated      6      0      2   
125    125   z57       Weber County Unincorporated      2      0      2   

     BDL_h  BGM_h  BNT_h  BRT_h  CDF_h  CEN_h  CHA_h  CHL_h  CLF_h  CLI_h  \
0      137     50     91      0     16     29      1    327     54     27   
1        1      0      1      0      0      1      0      0      0      0   
2       11      2      8      0      0      2      0     69      3      1   
3      379      2     18      0      9      5      0     13     13      4   
4        0   2308     21      0      0      6      0      4     41     34   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
121     50     18     33      0      6     10      2    143     21      8   
122      1      2      7      0      0      2     26      1      2      2   
123      3     18     24      0      0     13      0     15     16      9   
124      0      2      1      0      0      0      0      1      1      0   
125      1    121     44      0      0     25      0      3    143    170   

     CMT_h  COA_h  CWH_h  DAN_h  DRA_h  EAG_h  ELK_h  EMT_h  FAR_h  FCS_h  \
0        5      3     82      4    464    849     27      4     30      1   
1        0      0     49      0     10      1      0      0      0      0   
2        0      1     20      0     54     71      3      0      2      0   
3        1      1     44      0    156    149      5      0      9      0   
4        0      2     11      0     11      6      1      0     10      1   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
121      0      1     39      1    156    352    210      0     11      0   
122      0      6      5     50      8     19      0      0      3      7   
123      0      0     29      1     57     46      0      1     13      0   
124      0      0      2      0      4      2      1      0      0      0   
125      1      2     11      0     17      4      1      1     35      2   

     FFD_h  FRR_h  FTH_h  GLA_h  GOS_h  GRL_h  HAR_h  HDT_h  HEB_h  HER_h  \
0        6      7      6      8      7     33      6      0     99    309   
1        0      0      0      0      0      0      0      0      0      2   
2        0      1      0      1      0     54      0      0      4     27   
3        2      0      0      2      0     12      0      0      7    166   
4        0     40      4      1      0     13     42      1     15      8   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
121      1      4      3    109     52     12      0      0     38     98   
122      0      1      0      0      0      2      1     20    750      5   
123      0      1      1      0      0     10      2      0     10     21   
124      0      0      0      1      0      1      0      0      0      2   
125      0    113     10      0      0      4    102      0     11      5   

     HGH_h  HNF_h  HOL_h  HOO_h  HVL_h  IND_h  INT_h  KAY_h  KMS_h  KMT_h  \
0      613      6     77     11      0      1      0     65      3     95   
1        1      0     18      0      0      0      0      0      0      2   
2      161      1      7      0      0      0      0      2      4      9   
3       47      1    

index CODE3                        FIRST_NAME      AFK_h     ALA_h  \
0        0   AFK                     American Fork  14.039185  0.000000   
1        1   ALA                              Alta   0.013040  0.998391   
2        2   ALP                            Alpine   0.786367  0.000000   
3        3   BDL                         Bluffdale   0.471076  0.000495   
4        4   BGM                      Brigham City   0.047276  0.000000   
..     ...   ...                               ...        ...       ...   
121    121   z49        Utah County Unincorporated   4.147297  0.002104   
122    122   z51     Wasatch County Unincorporated   0.158243  0.000325   
123    123   z53  Washington County Unincorporated   0.429548  0.000000   
124    124   z55       Wayne County Unincorporated   0.045259  0.000000   
125    125   z57       Weber County Unincorporated   0.069516  0.347946   

        ALP_h     BDL_h      BGM_h     BNT_h     BRT_h     CDF_h     CEN_h  \
0    6.703662  2.126556   0.593184  0.502134  0.136252  7.243608  0.483141   
1    0.032477  0.025374   0.000086  0.006715  1.307114  0.000000  0.015242   
2    5.882593  0.168902   0.022114  0.051235  0.000000  0.187428  0.026523   
3    0.565201  5.490395   0.041970  0.113565  0.000000  3.522337  0.105863   
4    0.084855  0.006107  23.205994  0.114564  0.000000  0.000000  0.087154   
..        ...       ...        ...       ...       ...       ...       ...   
121  2.575755  1.022486   0.361853  0.282961  0.335652  3.682571  0.276064   
122  0.078041  0.079132   0.054617  0.063249  0.000103  0.000002  0.077698   
123  0.550352  0.214683   0.431215  0.299186  0.000000  0.000000  0.423855   
124  0.042370  0.000002   0.020076  0.004991  0.000000  0.000000  0.000000   
125  0.134247  0.059078   1.372864  0.288990  0.000000  0.000049  0.437987   

         CHA_h     CHL_h     CLF_h     CLI_h     CMT_h     COA_h     CWH_h  \
0     0.877582  7.373471  0.456543  0.327181  1.713258  0.727924  0.557821   
1     0.000009  0.008357  0.005423  0.003785  0.000000  0.022582  0.296451   
2     0.378267  1.552696  0.032395  0.021898  0.000000  0.120566  0.134148   
3     0.000005  0.381261  0.108291  0.074178  0.943155  0.240484  0.294000   
4     0.001594  0.090223  0.307041  0.341671  0.000000  0.242159  0.068460   
..         ...       ...       ...       ...       ...       ...       ...   
121   1.528035  3.745457  0.274861  0.165176  0.545123  0.469825  0.352933   
122  11.678365  0.066161  0.054101  0.054453  0.091970  1.374528  0.062010   
123   1.102386  0.914793  0.245810  0.183433  0.000000  0.481717  0.370506   
124   0.000000  0.021807  0.007236  0.000000  0.000000  0.000015  0.011962   
125   0.004554  0.151936  1.165826  1.822976  0.196416  0.502202  0.090335   

        DAN_h     DRA_h     EAG_h      ELK_h     EMT_h     FAR_h     FCS_h  \
0    0.888455  2.068874  5.595586   1.988549  0.752306  0.402442  0.211759   
1    0.000002  0.048345  0.008807   0.000001  0.086036  0.004252  0.001624   
2    0.000000  0.253109  0.483882   0.257746  0.000000  0.026110  0.190359   
3    0.147767  0.702611  1.001059   0.436985  0.000139  0.140138  0.008178   
4    0.001296  0.050952  0.046829   0.055869  0.000000  0.119253  0.193298   
..        ...       ...       ...        ...       ...       ...       ...   
121  0.745973  0.844587  2.589802  12.901644  0.295611  0.273920  0.451190   
122  8.660065  0.069601  0.167268   0.058046  0.000517  0.096329  2.846152   
123  0.448251  0.427898  0.552321   0.334837  0.841153  0.336136  0.571226   
124  0.000000  0.017480  0.013007   0.055855  0.000000  0.000002  0.000000   
125  0.209160  0.112439  0.058397   0.094491  0.194080  0.487307  0.383484   

        FFD_h     FRR_h     FTH_h      GLA_h      GOS_h     GRL_h     HAR_h  \
0    9.715517  0.311104  0.432726   1.381803   2.259899  0.706301  0.337860   
1    0.000000  0.000000  0.008557   0.000000   0.000000  0.006962  0.000000   
2    0.208973  0.031000  0.000000   0.228320   0.039902 

In [490]:
df_CitySum_wCounty_Join            = pd.DataFrame.merge(df_LEHDCommutePatterns_CityCalcsSum           , df_CityTownship_NameCode, on="CODE3", how="left")
df_CitySum_wCounty_Join_Percent_SA = pd.DataFrame.merge(df_LEHDCommutePatterns_CityCalcsSum_Percent_SA, df_CityTownship_NameCode, on="CODE3", how="left")

df_CitySum_wCounty_Join           .loc[df_CitySum_wCounty_Join           .CODE3.str[0] == 'z', 'zCOFIPS'] = df_CitySum_wCounty_Join           .CODE3
df_CitySum_wCounty_Join_Percent_SA.loc[df_CitySum_wCounty_Join_Percent_SA.CODE3.str[0] == 'z', 'zCOFIPS'] = df_CitySum_wCounty_Join_Percent_SA.CODE3

display(df_CitySum_wCounty_Join)
display(df_CitySum_wCounty_Join_Percent_SA)

index CODE3                        FIRST_NAME  AFK_h  ALA_h  ALP_h  \
0        0   AFK                     American Fork   1849      0    306   
1        1   ALA                              Alta      1      1      1   
2        2   ALP                            Alpine    100      0    274   
3        3   BDL                         Bluffdale     58      0     22   
4        4   BGM                      Brigham City      6      0      4   
..     ...   ...                               ...    ...    ...    ...   
121    121   z49        Utah County Unincorporated    508      0     95   
122    122   z51     Wasatch County Unincorporated     14      0      0   
123    123   z53  Washington County Unincorporated     28      0      5   
124    124   z55       Wayne County Unincorporated      6      0      2   
125    125   z57       Weber County Unincorporated      2      0      2   

     BDL_h  BGM_h  BNT_h  BRT_h  CDF_h  CEN_h  CHA_h  CHL_h  CLF_h  CLI_h  \
0      137     50     91      0     16     29      1    327     54     27   
1        1      0      1      0      0      1      0      0      0      0   
2       11      2      8      0      0      2      0     69      3      1   
3      379      2     18      0      9      5      0     13     13      4   
4        0   2308     21      0      0      6      0      4     41     34   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
121     50     18     33      0      6     10      2    143     21      8   
122      1      2      7      0      0      2     26      1      2      2   
123      3     18     24      0      0     13      0     15     16      9   
124      0      2      1      0      0      0      0      1      1      0   
125      1    121     44      0      0     25      0      3    143    170   

     CMT_h  COA_h  CWH_h  DAN_h  DRA_h  EAG_h  ELK_h  EMT_h  FAR_h  FCS_h  \
0        5      3     82      4    464    849     27      4     30      1   
1        0      0     49      0     10      1      0      0      0      0   
2        0      1     20      0     54     71      3      0      2      0   
3        1      1     44      0    156    149      5      0      9      0   
4        0      2     11      0     11      6      1      0     10      1   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
121      0      1     39      1    156    352    210      0     11      0   
122      0      6      5     50      8     19      0      0      3      7   
123      0      0     29      1     57     46      0      1     13      0   
124      0      0      2      0      4      2      1      0      0      0   
125      1      2     11      0     17      4      1      1     35      2   

     FFD_h  FRR_h  FTH_h  GLA_h  GOS_h  GRL_h  HAR_h  HDT_h  HEB_h  HER_h  \
0        6      7      6      8      7     33      6      0     99    309   
1        0      0      0      0      0      0      0      0      0      2   
2        0      1      0      1      0     54      0      0      4     27   
3        2      0      0      2      0     12      0      0      7    166   
4        0     40      4      1      0     13     42      1     15      8   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
121      1      4      3    109     52     12      0      0     38     98   
122      0      1      0      0      0      2      1     20    750      5   
123      0      1      1      0      0     10      2      0     10     21   
124      0      0      0      1      0      1      0      0      0      2   
125      0    113     10      0      0      4    102      0     11      5   

     HGH_h  HNF_h  HOL_h  HOO_h  HVL_h  IND_h  INT_h  KAY_h  KMS_h  KMT_h  \
0      613      6     77     11      0      1      0     65      3     95   
1        1      0     18      0      0      0      0      0      0      2   
2      161      1      7      0      0      0      0      2      4      9   
3       47      1    

index CODE3                        FIRST_NAME      AFK_h     ALA_h  \
0        0   AFK                     American Fork  14.039185  0.000000   
1        1   ALA                              Alta   0.013040  0.998391   
2        2   ALP                            Alpine   0.786367  0.000000   
3        3   BDL                         Bluffdale   0.471076  0.000495   
4        4   BGM                      Brigham City   0.047276  0.000000   
..     ...   ...                               ...        ...       ...   
121    121   z49        Utah County Unincorporated   4.147297  0.002104   
122    122   z51     Wasatch County Unincorporated   0.158243  0.000325   
123    123   z53  Washington County Unincorporated   0.429548  0.000000   
124    124   z55       Wayne County Unincorporated   0.045259  0.000000   
125    125   z57       Weber County Unincorporated   0.069516  0.347946   

        ALP_h     BDL_h      BGM_h     BNT_h     BRT_h     CDF_h     CEN_h  \
0    6.703662  2.126556   0.593184  0.502134  0.136252  7.243608  0.483141   
1    0.032477  0.025374   0.000086  0.006715  1.307114  0.000000  0.015242   
2    5.882593  0.168902   0.022114  0.051235  0.000000  0.187428  0.026523   
3    0.565201  5.490395   0.041970  0.113565  0.000000  3.522337  0.105863   
4    0.084855  0.006107  23.205994  0.114564  0.000000  0.000000  0.087154   
..        ...       ...        ...       ...       ...       ...       ...   
121  2.575755  1.022486   0.361853  0.282961  0.335652  3.682571  0.276064   
122  0.078041  0.079132   0.054617  0.063249  0.000103  0.000002  0.077698   
123  0.550352  0.214683   0.431215  0.299186  0.000000  0.000000  0.423855   
124  0.042370  0.000002   0.020076  0.004991  0.000000  0.000000  0.000000   
125  0.134247  0.059078   1.372864  0.288990  0.000000  0.000049  0.437987   

         CHA_h     CHL_h     CLF_h     CLI_h     CMT_h     COA_h     CWH_h  \
0     0.877582  7.373471  0.456543  0.327181  1.713258  0.727924  0.557821   
1     0.000009  0.008357  0.005423  0.003785  0.000000  0.022582  0.296451   
2     0.378267  1.552696  0.032395  0.021898  0.000000  0.120566  0.134148   
3     0.000005  0.381261  0.108291  0.074178  0.943155  0.240484  0.294000   
4     0.001594  0.090223  0.307041  0.341671  0.000000  0.242159  0.068460   
..         ...       ...       ...       ...       ...       ...       ...   
121   1.528035  3.745457  0.274861  0.165176  0.545123  0.469825  0.352933   
122  11.678365  0.066161  0.054101  0.054453  0.091970  1.374528  0.062010   
123   1.102386  0.914793  0.245810  0.183433  0.000000  0.481717  0.370506   
124   0.000000  0.021807  0.007236  0.000000  0.000000  0.000015  0.011962   
125   0.004554  0.151936  1.165826  1.822976  0.196416  0.502202  0.090335   

        DAN_h     DRA_h     EAG_h      ELK_h     EMT_h     FAR_h     FCS_h  \
0    0.888455  2.068874  5.595586   1.988549  0.752306  0.402442  0.211759   
1    0.000002  0.048345  0.008807   0.000001  0.086036  0.004252  0.001624   
2    0.000000  0.253109  0.483882   0.257746  0.000000  0.026110  0.190359   
3    0.147767  0.702611  1.001059   0.436985  0.000139  0.140138  0.008178   
4    0.001296  0.050952  0.046829   0.055869  0.000000  0.119253  0.193298   
..        ...       ...       ...        ...       ...       ...       ...   
121  0.745973  0.844587  2.589802  12.901644  0.295611  0.273920  0.451190   
122  8.660065  0.069601  0.167268   0.058046  0.000517  0.096329  2.846152   
123  0.448251  0.427898  0.552321   0.334837  0.841153  0.336136  0.571226   
124  0.000000  0.017480  0.013007   0.055855  0.000000  0.000002  0.000000   
125  0.209160  0.112439  0.058397   0.094491  0.194080  0.487307  0.383484   

        FFD_h     FRR_h     FTH_h      GLA_h      GOS_h     GRL_h     HAR_h  \
0    9.715517  0.311104  0.432726   1.381803   2.259899  0.706301  0.337860   
1    0.000000  0.000000  0.008557   0.000000   0.000000  0.006962  0.000000   
2    0.208973  0.031000  0.000000   0.228320   0.039902 

In [491]:
dColCodesWCounty

['AFK_h',
 'ALA_h',
 'ALP_h',
 'BDL_h',
 'BGM_h',
 'BNT_h',
 'BRT_h',
 'CDF_h',
 'CEN_h',
 'CHA_h',
 'CHL_h',
 'CLF_h',
 'CLI_h',
 'CMT_h',
 'COA_h',
 'CWH_h',
 'DAN_h',
 'DRA_h',
 'EAG_h',
 'ELK_h',
 'EMT_h',
 'FAR_h',
 'FCS_h',
 'FFD_h',
 'FRR_h',
 'FTH_h',
 'GLA_h',
 'GOS_h',
 'GRL_h',
 'HAR_h',
 'HDT_h',
 'HEB_h',
 'HER_h',
 'HGH_h',
 'HNF_h',
 'HOL_h',
 'HOO_h',
 'HVL_h',
 'IND_h',
 'INT_h',
 'KAY_h',
 'KMS_h',
 'KMT_h',
 'LAY_h',
 'LEH_h',
 'LIN_h',
 'MAP_h',
 'MID_h',
 'MLC_h',
 'MMT_h',
 'MRG_h',
 'MSL_h',
 'MUR_h',
 'MWY_h',
 'NOG_h',
 'NSL_h',
 'OGD_h',
 'OKL_h',
 'ORM_h',
 'PAY_h',
 'PGR_h',
 'PLN_h',
 'PRK_h',
 'PRY_h',
 'PVO_h',
 'PVW_h',
 'ROY_h',
 'RVD_h',
 'RVT_h',
 'SAN_h',
 'SAQ_h',
 'SAR_h',
 'SFK_h',
 'SJC_h',
 'SLC_h',
 'SLM_h',
 'SOG_h',
 'SPV_h',
 'SSL_h',
 'SUN_h',
 'SWE_h',
 'SYR_h',
 'TAY_h',
 'TOO_h',
 'UIN_h',
 'VIN_h',
 'WAT_h',
 'WBG_h',
 'WDL_h',
 'WEB_h',
 'WHT_h',
 'WHV_h',
 'WIL_h',
 'WJC_h',
 'WPT_h',
 'WVC_h',
 'WXC_h',
 'TTL_h',
 'AFK_w',
 'ALA_w',


In [492]:
df_CountySum            = df_CitySum_wCounty_Join           .groupby(['zCOFIPS'])[dColCodesWCounty].apply(lambda x : x.astype(int  ).sum())
df_CountySum_Percent_SA = df_CitySum_wCounty_Join_Percent_SA.groupby(['zCOFIPS'])[dColCodesWCounty].apply(lambda x : x.astype(float).sum())

df_CountySum            = df_CountySum           .reset_index()
df_CountySum_Percent_SA = df_CountySum_Percent_SA.reset_index()

display(df_CountySum)
display(df_CountySum_Percent_SA)

zCOFIPS  AFK_h  ALA_h  ALP_h  BDL_h  BGM_h  BNT_h  BRT_h  CDF_h  CEN_h  \
0      z01      3      0      3      1      2      5      0      0      1   
1      z03     14      0      5      4   3899     53      0      0     13   
2      z05     77      1     35     13    715    248      2      0     92   
3      z07     25      0     10      1     14     11      0      1      8   
4      z09      0      0      0      0      0      0      0      0      0   
5      z11    171      4     72    129    639   6227      0      1   2667   
6      z13      8      0      5      1      7     12      0      1      3   
7      z15      5      0      6      1      7      3      0      0      0   
8      z17      3      0      1      2      2      2      0      0      0   
9      z19      5      0      0      1      3      2      0      1      0   
10     z21      9      0      5      0      7      7      0      0      0   
11     z23     19      0      9      2      6      4      0      0      2   
12     z25      3      0      0      1      1      0      0      0      0   
13     z27      6      0      4      2      3      3      0      0      0   
14     z29      1      0      0      0      4     29      0      0      7   
15     z31      0      0      0      0      0      0      0      0      0   
16     z33      0      0      0      0      9      4      0      0      3   
17     z35   3185    126   1662   5245   1628  10845     44    104   3655   
18     z37      0      0      1      1      2      3      0      0      0   
19     z39     29      0     13      4     19     11      0      0      2   
20     z41     16      0      4      8     11     10      0      0      5   
21     z43     70      2     37     47     55    145      1      1     49   
22     z45     61      0     11     19     50     76      0      2     14   
23     z47     14      0      2      3     11     19      0      0      6   
24     z49   8793      7   2399   1062    420    721      3    108    247   
25     z51     54      0     12      5     16     30      0      0      8   
26     z53     28      0      5      3     18     24      0      0     13   
27     z55      6      0      2      0      2      1      0      0      0   
28     z57    148      1     42     48   1989    987      0      1    339   

    CHA_h  CHL_h  CLF_h  CLI_h  CMT_h  COA_h  CWH_h  DAN_h  DRA_h  EAG_h  \
0       0      1      2      3      0      0      4      1      6      1   
1       0      6     96     80      0      4     27      2     34     15   
2       9     31    170    139      2     11     80      8    122     93   
3       0      7     12      4      0      3     12      0     18     31   
4       0      0      0      0      0      0      0      0      0      0   
5       3     82   5505   3682     12     21    432      4    677    257   
6       1      5      5      3      0      4     10      2      5     18   
7       0      5      1      0      0      0      6      0     13     13   
8       0      1      1      1      0      3      1      0      1      1   
9       1      1      2      1      0      0      4      3      5      3   
10      0      1      1      1      0      0      9      0     13      8   
11      0      7      2      0      0      2      5      1     11     27   
12      0      0      0      0      0      0      5      1      6      2   
13      0      4      0      2      0      0      2      0      5     22   
14      0      0     32     30      0     12      5      0     17      4   
15      0      0      0      0      0      1      0      0      0      0   
16      0      2      4      0      0      0      2      1      3      3   
17     44   1373   3909   2528    354    206  13973    135  17093   6971   
18      0      2      2      2      0      0      1      0      1      3   
19      1      9     10      4      0      2     11      2     15     32   
20      1      7      5      5      0      3      8      1     10     21   
21     42     38    

zCOFIPS         AFK_h      ALA_h         ALP_h         BDL_h         BGM_h  \
0      z01  3.016053e-02   0.000000  6.354153e-02  1.432260e-02  2.007216e-02   
1      z03  1.131544e-01   0.000139  1.271421e-01  7.163412e-02  3.926291e+01   
2      z05  5.809169e-01   0.521191  7.417164e-01  2.005704e-01  7.188758e+00   
3      z07  1.886226e-01   0.000000  2.119387e-01  1.432978e-02  1.405738e-01   
4      z09  7.524677e-03   0.000000  0.000000e+00  0.000000e+00  7.643768e-10   
5      z11  1.637052e+00   3.648104  2.161528e+00  2.321031e+00  7.078037e+00   
6      z13  7.541844e-02   0.000000  1.271176e-01  1.432798e-02  8.031768e-02   
7      z15  3.772927e-02   0.000000  1.271524e-01  1.432979e-02  7.029106e-02   
8      z17  2.263428e-02   0.000000  4.237323e-02  2.864722e-02  2.008127e-02   
9      z19  3.770817e-02   0.000000  1.571953e-05  1.432448e-02  3.011155e-02   
10     z21  1.281649e-01   0.000000  2.541025e-01  5.727298e-02  1.203983e-01   
11     z23  1.695749e-01   0.000000  2.523673e-01  4.512366e-02  6.219263e-02   
12     z25  2.263038e-02   0.000000  9.754153e-06  1.432748e-02  1.003470e-02   
13     z27  4.525449e-02   0.000000  8.474113e-02  2.864615e-02  3.011044e-02   
14     z29  2.264001e-02   0.000000  1.762404e-05  1.413993e-05  7.031627e-02   
15     z31  1.535480e-06   0.000000  9.053554e-07  8.042780e-07  3.915863e-08   
16     z33  1.996468e-07   0.000000  0.000000e+00  1.738707e-07  9.034500e-02   
17     z35  2.526067e+01  87.555946  3.818062e+01  7.772069e+01  1.764073e+01   
18     z37  7.632407e-06   0.000000  2.119109e-02  1.431955e-02  2.007727e-02   
19     z39  2.187957e-01   0.000000  2.755076e-01  5.731425e-02  1.907625e-01   
20     z41  1.207011e-01   0.000000  8.475926e-02  1.146202e-01  1.104303e-01   
21     z43  6.111420e-01   1.563536  9.112537e-01  7.737868e-01  6.525623e-01   
22     z45  5.279984e-01   0.521212  3.813563e-01  4.010902e-01  6.223133e-01   
23     z47  1.056362e-01   0.000000  4.240506e-02  4.297334e-02  1.104205e-01   
24     z49  6.772731e+01   4.171734  5.366673e+01  1.679800e+01  5.077301e+00   
25     z51  4.983789e-01   0.000325  3.816594e-01  1.720125e-01  2.210440e-01   
26     z53  4.295480e-01   0.000000  5.503517e-01  2.146834e-01  4.312148e-01   
27     z55  4.525934e-02   0.000000  4.236953e-02  2.455934e-06  2.007628e-02   
28     z57  1.403146e+00   2.084438  1.334969e+00  9.169549e-01  2.069088e+01   

           BNT_h      BRT_h         CDF_h         CEN_h      CHA_h  \
0   2.495119e-02   0.000000  2.921056e-07  1.325592e-02   0.000000   
1   3.094923e-01   0.000000  1.662561e-06  2.254257e-01   0.367873   
2   1.238069e+00   2.741601  0.000000e+00  1.233270e+00   3.311064   
3   5.492008e-02   0.000000  3.051126e-01  1.060981e-01   0.000000   
4   4.979090e-03   0.000000  0.000000e+00  1.322633e-02   0.000000   
5   3.158803e+01   4.112297  2.135459e+00  3.655891e+01   2.575026   
6   6.488793e-02   0.000000  3.050436e-01  3.978161e-02   0.367979   
7   1.497917e-02   0.000000  8.734448e-06  2.928417e-06   0.000000   
8   9.983969e-03   0.000000  1.244370e-04  5.408869e-06   0.000000   
9   9.981520e-03   0.000000  3.050008e-01  0.000000e+00   0.367795   
10  9.478522e-02   0.000000  6.096989e-01  3.975321e-02   0.367627   
11  3.524197e-02   0.000000  6.099030e-01  5.617531e-02   0.000000   
12  1.399956e-06   0.000000  1.550288e-06  6.738596e-08   0.000000   
13  1.995933e-02   0.000000  4.741788e-06  5.279498e-08   0.000000   
14  1.603846e-01   0.000000  0.000000e+00  1.196142e-01   0.000173   
15  9.411639e-07   0.000000  0.000000e+00  0.000000e+00   0.000000   
16  1.996583e-02   0.000000  0.000000e+00  3.977791e-02   0.000000   
17  5.507546e+01  85.124995  4.593055e+01  5.046696e+01  22.809248   
18  1.497158e-02   0.000000  0.000000e+00  0.000000e+00   0.000000   
19  5.491628e-02   0.000000  9.702778e-06  2.652433e-02   0.367896   
20  4.991757e-02   0.000000  0.000000e+00  6.630289e-02   0.367890   
21  7.787736e-01   1.370965  3.0

In [493]:
df_CountySum           ['WFCounty'] = "Outside Wasatch Front"
df_CountySum_Percent_SA['WFCounty'] = "Outside Wasatch Front"

df_CountySum           .loc[df_CountySum.zCOFIPS == 'z11', 'WFCounty'] = "Davis County"
df_CountySum           .loc[df_CountySum.zCOFIPS == 'z57', 'WFCounty'] = "Weber County"
df_CountySum           .loc[df_CountySum.zCOFIPS == 'z35', 'WFCounty'] = "Salt Lake County"
df_CountySum           .loc[df_CountySum.zCOFIPS == 'z49', 'WFCounty'] = "Utah County"

df_CountySum_Percent_SA.loc[df_CountySum.zCOFIPS == 'z11', 'WFCounty'] = "Davis County"
df_CountySum_Percent_SA.loc[df_CountySum.zCOFIPS == 'z57', 'WFCounty'] = "Weber County"
df_CountySum_Percent_SA.loc[df_CountySum.zCOFIPS == 'z35', 'WFCounty'] = "Salt Lake County"
df_CountySum_Percent_SA.loc[df_CountySum.zCOFIPS == 'z49', 'WFCounty'] = "Utah County"

display(df_CountySum)
display(df_CountySum_Percent_SA)

zCOFIPS  AFK_h  ALA_h  ALP_h  BDL_h  BGM_h  BNT_h  BRT_h  CDF_h  CEN_h  \
0      z01      3      0      3      1      2      5      0      0      1   
1      z03     14      0      5      4   3899     53      0      0     13   
2      z05     77      1     35     13    715    248      2      0     92   
3      z07     25      0     10      1     14     11      0      1      8   
4      z09      0      0      0      0      0      0      0      0      0   
5      z11    171      4     72    129    639   6227      0      1   2667   
6      z13      8      0      5      1      7     12      0      1      3   
7      z15      5      0      6      1      7      3      0      0      0   
8      z17      3      0      1      2      2      2      0      0      0   
9      z19      5      0      0      1      3      2      0      1      0   
10     z21      9      0      5      0      7      7      0      0      0   
11     z23     19      0      9      2      6      4      0      0      2   
12     z25      3      0      0      1      1      0      0      0      0   
13     z27      6      0      4      2      3      3      0      0      0   
14     z29      1      0      0      0      4     29      0      0      7   
15     z31      0      0      0      0      0      0      0      0      0   
16     z33      0      0      0      0      9      4      0      0      3   
17     z35   3185    126   1662   5245   1628  10845     44    104   3655   
18     z37      0      0      1      1      2      3      0      0      0   
19     z39     29      0     13      4     19     11      0      0      2   
20     z41     16      0      4      8     11     10      0      0      5   
21     z43     70      2     37     47     55    145      1      1     49   
22     z45     61      0     11     19     50     76      0      2     14   
23     z47     14      0      2      3     11     19      0      0      6   
24     z49   8793      7   2399   1062    420    721      3    108    247   
25     z51     54      0     12      5     16     30      0      0      8   
26     z53     28      0      5      3     18     24      0      0     13   
27     z55      6      0      2      0      2      1      0      0      0   
28     z57    148      1     42     48   1989    987      0      1    339   

    CHA_h  CHL_h  CLF_h  CLI_h  CMT_h  COA_h  CWH_h  DAN_h  DRA_h  EAG_h  \
0       0      1      2      3      0      0      4      1      6      1   
1       0      6     96     80      0      4     27      2     34     15   
2       9     31    170    139      2     11     80      8    122     93   
3       0      7     12      4      0      3     12      0     18     31   
4       0      0      0      0      0      0      0      0      0      0   
5       3     82   5505   3682     12     21    432      4    677    257   
6       1      5      5      3      0      4     10      2      5     18   
7       0      5      1      0      0      0      6      0     13     13   
8       0      1      1      1      0      3      1      0      1      1   
9       1      1      2      1      0      0      4      3      5      3   
10      0      1      1      1      0      0      9      0     13      8   
11      0      7      2      0      0      2      5      1     11     27   
12      0      0      0      0      0      0      5      1      6      2   
13      0      4      0      2      0      0      2      0      5     22   
14      0      0     32     30      0     12      5      0     17      4   
15      0      0      0      0      0      1      0      0      0      0   
16      0      2      4      0      0      0      2      1      3      3   
17     44   1373   3909   2528    354    206  13973    135  17093   6971   
18      0      2      2      2      0      0      1      0      1      3   
19      1      9     10      4      0      2     11      2     15     32   
20      1      7      5      5      0      3      8      1     10     21   
21     42     38    

zCOFIPS         AFK_h      ALA_h         ALP_h         BDL_h         BGM_h  \
0      z01  3.016053e-02   0.000000  6.354153e-02  1.432260e-02  2.007216e-02   
1      z03  1.131544e-01   0.000139  1.271421e-01  7.163412e-02  3.926291e+01   
2      z05  5.809169e-01   0.521191  7.417164e-01  2.005704e-01  7.188758e+00   
3      z07  1.886226e-01   0.000000  2.119387e-01  1.432978e-02  1.405738e-01   
4      z09  7.524677e-03   0.000000  0.000000e+00  0.000000e+00  7.643768e-10   
5      z11  1.637052e+00   3.648104  2.161528e+00  2.321031e+00  7.078037e+00   
6      z13  7.541844e-02   0.000000  1.271176e-01  1.432798e-02  8.031768e-02   
7      z15  3.772927e-02   0.000000  1.271524e-01  1.432979e-02  7.029106e-02   
8      z17  2.263428e-02   0.000000  4.237323e-02  2.864722e-02  2.008127e-02   
9      z19  3.770817e-02   0.000000  1.571953e-05  1.432448e-02  3.011155e-02   
10     z21  1.281649e-01   0.000000  2.541025e-01  5.727298e-02  1.203983e-01   
11     z23  1.695749e-01   0.000000  2.523673e-01  4.512366e-02  6.219263e-02   
12     z25  2.263038e-02   0.000000  9.754153e-06  1.432748e-02  1.003470e-02   
13     z27  4.525449e-02   0.000000  8.474113e-02  2.864615e-02  3.011044e-02   
14     z29  2.264001e-02   0.000000  1.762404e-05  1.413993e-05  7.031627e-02   
15     z31  1.535480e-06   0.000000  9.053554e-07  8.042780e-07  3.915863e-08   
16     z33  1.996468e-07   0.000000  0.000000e+00  1.738707e-07  9.034500e-02   
17     z35  2.526067e+01  87.555946  3.818062e+01  7.772069e+01  1.764073e+01   
18     z37  7.632407e-06   0.000000  2.119109e-02  1.431955e-02  2.007727e-02   
19     z39  2.187957e-01   0.000000  2.755076e-01  5.731425e-02  1.907625e-01   
20     z41  1.207011e-01   0.000000  8.475926e-02  1.146202e-01  1.104303e-01   
21     z43  6.111420e-01   1.563536  9.112537e-01  7.737868e-01  6.525623e-01   
22     z45  5.279984e-01   0.521212  3.813563e-01  4.010902e-01  6.223133e-01   
23     z47  1.056362e-01   0.000000  4.240506e-02  4.297334e-02  1.104205e-01   
24     z49  6.772731e+01   4.171734  5.366673e+01  1.679800e+01  5.077301e+00   
25     z51  4.983789e-01   0.000325  3.816594e-01  1.720125e-01  2.210440e-01   
26     z53  4.295480e-01   0.000000  5.503517e-01  2.146834e-01  4.312148e-01   
27     z55  4.525934e-02   0.000000  4.236953e-02  2.455934e-06  2.007628e-02   
28     z57  1.403146e+00   2.084438  1.334969e+00  9.169549e-01  2.069088e+01   

           BNT_h      BRT_h         CDF_h         CEN_h      CHA_h  \
0   2.495119e-02   0.000000  2.921056e-07  1.325592e-02   0.000000   
1   3.094923e-01   0.000000  1.662561e-06  2.254257e-01   0.367873   
2   1.238069e+00   2.741601  0.000000e+00  1.233270e+00   3.311064   
3   5.492008e-02   0.000000  3.051126e-01  1.060981e-01   0.000000   
4   4.979090e-03   0.000000  0.000000e+00  1.322633e-02   0.000000   
5   3.158803e+01   4.112297  2.135459e+00  3.655891e+01   2.575026   
6   6.488793e-02   0.000000  3.050436e-01  3.978161e-02   0.367979   
7   1.497917e-02   0.000000  8.734448e-06  2.928417e-06   0.000000   
8   9.983969e-03   0.000000  1.244370e-04  5.408869e-06   0.000000   
9   9.981520e-03   0.000000  3.050008e-01  0.000000e+00   0.367795   
10  9.478522e-02   0.000000  6.096989e-01  3.975321e-02   0.367627   
11  3.524197e-02   0.000000  6.099030e-01  5.617531e-02   0.000000   
12  1.399956e-06   0.000000  1.550288e-06  6.738596e-08   0.000000   
13  1.995933e-02   0.000000  4.741788e-06  5.279498e-08   0.000000   
14  1.603846e-01   0.000000  0.000000e+00  1.196142e-01   0.000173   
15  9.411639e-07   0.000000  0.000000e+00  0.000000e+00   0.000000   
16  1.996583e-02   0.000000  0.000000e+00  3.977791e-02   0.000000   
17  5.507546e+01  85.124995  4.593055e+01  5.046696e+01  22.809248   
18  1.497158e-02   0.000000  0.000000e+00  0.000000e+00   0.000000   
19  5.491628e-02   0.000000  9.702778e-06  2.652433e-02   0.367896   
20  4.991757e-02   0.000000  0.000000e+00  6.630289e-02   0.367890   
21  7.787736e-01   1.370965  3.0

In [494]:
df_CountySum_wOutWF            = df_CountySum           .groupby(['WFCounty'])[dColCodesWCounty].apply(lambda x : x.astype(int  ).sum())
df_CountySum_wOutWF_Percent_SA = df_CountySum_Percent_SA.groupby(['WFCounty'])[dColCodesWCounty].apply(lambda x : x.astype(float).sum())

df_CountySum_wOutWF            = df_CountySum_wOutWF.reset_index()
df_CountySum_wOutWF_Percent_SA = df_CountySum_wOutWF_Percent_SA.reset_index()

display(df_CountySum_wOutWF)
display(df_CountySum_wOutWF_Percent_SA)

WFCounty  AFK_h  ALA_h  ALP_h  BDL_h  BGM_h  BNT_h  BRT_h  \
0           Davis County    171      4     72    129    639   6227      0   
1  Outside Wasatch Front    456      3    170    119   4863    702      3   
2       Salt Lake County   3185    126   1662   5245   1628  10845     44   
3            Utah County   8793      7   2399   1062    420    721      3   
4           Weber County    148      1     42     48   1989    987      0   

   CDF_h  CEN_h  CHA_h  CHL_h  CLF_h  CLI_h  CMT_h  COA_h  CWH_h  DAN_h  \
0      1   2667      3     82   5505   3682     12     21    432      4   
1      6    226    133    178    518    390      5    405    692    356   
2    104   3655     44   1373   3909   2528    354    206  13973    135   
3    108    247     24   2532    454    267     37     41    926     56   
4      1    339      5     53   2947   3049      2     25    205      6   

   DRA_h  EAG_h  ELK_h  EMT_h  FAR_h  FCS_h  FFD_h  FRR_h  FTH_h  GLA_h  \
0    677    257     13     17   3558      6      0    431    884     10   
1    719    591     89     43    296    316      1    182     69     65   
2  17093   6971    318    516   4198     88     34    484    839    143   
3   3509   6838   1139     24    294     19     22     66     69    494   
4    296    171     21      8    437      8      0   1802    183      8   

   GOS_h  GRL_h  HAR_h  HDT_h  HEB_h  HER_h  HGH_h  HNF_h  HOL_h  HOO_h  \
0      2    237    410      3    206    402    145     10    418    856   
1     47   1867    178    195   5054    419    334    191    632    152   
2     93   2593    467     66   1709  15258   3020     58  12093    624   
3    247    421     63     22    862   2116   4109     25    686     87   
4      4    138   1775      4    201    144     95     27    176   1757   

   HVL_h  IND_h  INT_h  KAY_h  KMS_h  KMT_h  LAY_h  LEH_h  LIN_h  MAP_h  \
0     23      2      2   5176     13    593  13514    543     74     54   
1     16     58      9    458    640    568   1275   1233    139    210   
2     48     21      5   5213    201  15836  10002  12286    972    893   
3      6     12      2    480     54    832   1075  16042   3427   3386   
4    140      3      1    893     13    252   6047    362     40     61   

   MID_h  MLC_h  MMT_h  MRG_h  MSL_h  MUR_h  MWY_h  NOG_h  NSL_h  OGD_h  \
0    364   1094    538    299    120    745     43   1147   2285   6935   
1    442   1311    447    628     48    779   1213    595    278   2326   
2  14922  25343  12634    418    135  21533    522   1501   5139   7261   
3    990   1364    611     73     28   1160    305    214    237   1271   
4    173    396    172    359    527    327     50   5256    368  21393   

   OKL_h  ORM_h  PAY_h  PGR_h  PLN_h  PRK_h  PRY_h  PVO_h  PVW_h  ROY_h  \
0      7    779    185    254    426     84    236    693    548   4805   
1    343   1614    586    570    188   2860   1181   1443    331    903   
2    116   9384   2003   3747    451    815    440   6639    738   3723   
3     37  32774   6282  11443     62    164     99  28947     97    564   
4      9    601    119    214   1865     83    587    546   2478   8412   

   RVD_h  RVT_h  SAN_h  SAQ_h  SAR_h  SFK_h  SJC_h  SLC_h  SLM_h  SOG_h  \
0    824    640   1250     71    218    332    905   4585     51   1482   
1    202    651   1613    571    514    973    910   3786    180    332   
2    746  19229  39941   1213   6783   4219  27304  76396    783   1533   
3     87   2612   3810   3363   7233  14180   3120   3738   2679    205   
4   1899    281    674     59    121    255    358   1187     51   3864   

   SPV_h  SSL_h  SUN_h  SWE_h  SYR_h  TAY_h  TOO_h  UIN_h  VIN_h  WAT_h  \
0    318    425    907   1041   5257    948    953     94      0    835   
1    798    501     88     85    408    959   5226     25      2    178   
2   3534  10186    612    827   3432  26856   8664    107     14    863   
3  11527    463     61     83    379   1503   1482     13     86    116   
4    212    165    73

WFCounty      AFK_h      ALA_h      ALP_h      BDL_h  \
0           Davis County   1.637052   3.648104   2.161528   2.321031   
1  Outside Wasatch Front   4.039603   2.606403   4.723090   2.308675   
2       Salt Lake County  25.260672  87.555946  38.180616  77.720689   
3            Utah County  67.727310   4.171734  53.666726  16.798004   
4           Weber County   1.403146   2.084438   1.334969   0.916955   

       BGM_h      BNT_h      BRT_h      CDF_h      CEN_h      CHA_h  \
0   7.078037  31.588030   4.112297   2.135459  36.558906   2.575026   
1  49.575414   4.004185   4.112681   3.659864   3.742545  57.762867   
2  17.640730  55.075465  85.124995  45.930547  50.466965  22.809248   
3   5.077301   4.156009   6.716966  47.423842   4.191368  14.347662   
4  20.690884   5.241382   0.000000   0.915218   5.105177   2.575092   

       CHL_h      CLF_h      CLI_h      CMT_h      COA_h      CWH_h  \
0   2.398538  40.611798  36.544140   3.819146   4.701715   2.943320   
1   5.084797   4.247536   4.243522   1.728041  52.809264   4.645188   
2  32.747334  29.402869  25.734106  81.770748  30.019642  84.888338   
3  58.222707   3.871737   3.310247  12.173929   7.716847   6.165198   
4   1.613521  21.929800  30.231505   0.572892   4.822260   1.423785   

       DAN_h      DRA_h      EAG_h      ELK_h      EMT_h      FAR_h  \
0   1.645077   3.269589   1.990548   1.229137   4.070094  39.610839   
1  57.589863   3.589286   4.479564   6.120158   7.578137   3.920157   
2  26.340560  75.671873  46.656604  21.818940  81.849602  47.338583   
3  12.401500  16.053128  45.638045  69.280669   4.883506   3.908965   
4   2.093861   1.481753   1.301025   1.620211   1.684108   5.286335   

       FCS_h      FFD_h      FRR_h      FTH_h      GLA_h      GOS_h  \
0   2.096576   1.031607  15.406665  41.948552   2.056134   0.787920   
1  65.381604   3.094937   6.509785   4.107483   9.128077  12.582278   
2  23.253312  52.611113  16.955646  40.133924  21.372431  23.657492   
3   7.244178  42.297282   3.132103   4.174866  65.912340  61.857702   
4   2.096486   1.031572  58.059044   9.699596   1.599156   1.181851   

       GRL_h      HAR_h      HDT_h      HEB_h      HER_h      HGH_h  \
0   5.155130  14.580733   3.554306   3.056417   2.398604   2.250212   
1  34.326410   6.814351  60.974107  61.004748   2.627046   5.143453   
2  48.737318  16.771123  22.966154  21.867616  82.119065  38.923993   
3   8.764099   3.197795  10.389874  11.347978  11.949019  52.244971   
4   3.075213  58.699033   2.187013   2.794619   0.971085   1.504233   

       HNF_h      HOL_h      HOO_h      HVL_h      IND_h      INT_h  \
0   4.618239   3.223654  24.766159  11.872922   1.563567  14.715400   
1  55.681330   4.801939   4.735933   6.802940  57.072599  50.037242   
2  21.039407  85.125639  18.653125  21.369946  21.889440  23.545208   
3   8.980403   5.441326   3.439784   3.375432  14.854871   8.829618   
4   9.749638   1.473409  48.468031  56.643504   4.690467   2.943040   

       KAY_h      KMS_h      KMT_h      LAY_h      LEH_h      LIN_h  \
0  41.584175   2.633245   3.547357  41.925606   1.970605   2.158346   
1   4.098374  63.957048   3.507757   4.224765   4.393868   3.743975   
2  42.400251  23.605718  86.430014  31.364294  40.176885  21.640271   
3   4.472150   7.712649   5.028986   3.669161  52.223334  71.266693   
4   7.509682   2.163017   1.550247  18.880165   1.301960   1.258988   

       MAP_h      MID_h      MLC_h      MMT_h      MRG_h      MSL_h  \
0   1.713794   2.386061   3.886491   4.013558  17.827227  15.789367   
1   5.245584   3.015509   4.660840   3.443131  32.785328   6.019251   
2  20.274937  87.139458  85.044357  86.395665  23.976689  16.282883   
3  71.201920   6.339894   4.988094   4.786764   4.930369   4.046301   
4   1.633055   1.184355   1.486112   1.425130  20.546983  57.925022   

       MUR_h      MWY_h      NOG_h      NSL_h      OGD_h      OKL_h  \
0   3.234503   3.034791  13.453367  27.281188  17.703787   2.108528   
1   3.537142  53.268484  

In [495]:
# bu map unit
# block group
df_CountySum_wOutWF_Percent_MU = df_CountySum_wOutWF.copy()

for x in dColCodesWCounty_x:   
    #display(x)
    df_CountySum_wOutWF_Percent_MU[x] = df_CountySum_wOutWF_Percent_MU[x] / df_CountySum_wOutWF_Percent_MU['TTL_h'] * 100

for y in dColCodesWCounty_y:   
    #display(y)
    df_CountySum_wOutWF_Percent_MU[y] = df_CountySum_wOutWF_Percent_MU[y] / df_CountySum_wOutWF_Percent_MU['TTL_w'] * 100

df_CountySum_wOutWF_Percent_MU

WFCounty     AFK_h     ALA_h     ALP_h     BDL_h     BGM_h  \
0           Davis County  0.148697  0.003478  0.062609  0.112175  0.555657   
1  Outside Wasatch Front  0.163566  0.001076  0.060979  0.042685  1.744349   
2       Salt Lake County  0.465172  0.018402  0.242737  0.766037  0.237771   
3            Utah County  3.602832  0.002868  0.982963  0.435142  0.172090   
4           Weber County  0.136387  0.000922  0.038704  0.044234  1.832926   

      BNT_h     BRT_h     CDF_h     CEN_h     CHA_h     CHL_h     CLF_h  \
0  5.414830  0.000000  0.000870  2.319151  0.002609  0.071305  4.786998   
1  0.251806  0.001076  0.002152  0.081066  0.047707  0.063848  0.185806   
2  1.583922  0.006426  0.015189  0.533816  0.006426  0.200528  0.570913   
3  0.295422  0.001229  0.044252  0.101205  0.009834  1.037458  0.186021   
4  0.909552  0.000000  0.000922  0.312399  0.004608  0.048841  2.715754   

      CLI_h     CMT_h     COA_h     CWH_h     DAN_h     DRA_h     EAG_h  \
0  3.201767  0.010435  0.018261  0.375655  0.003478  0.588701  0.223480   
1  0.139892  0.001793  0.145273  0.248219  0.127697  0.257904  0.211991   
2  0.369217  0.051702  0.030086  2.040769  0.019717  2.496447  1.018121   
3  0.109400  0.015160  0.016799  0.379418  0.022945  1.437773  2.801793   
4  2.809750  0.001843  0.023038  0.188914  0.005529  0.272773  0.157582   

      ELK_h     EMT_h     FAR_h     FCS_h     FFD_h     FRR_h     FTH_h  \
0  0.011304  0.014783  3.093940  0.005217  0.000000  0.374786  0.768702   
1  0.031924  0.015424  0.106175  0.113349  0.000359  0.065283  0.024750   
2  0.046444  0.075362  0.613122  0.012852  0.004966  0.070689  0.122537   
3  0.466692  0.009834  0.120463  0.007785  0.009014  0.027043  0.028272   
4  0.019352  0.007372  0.402709  0.007372  0.000000  1.660600  0.168640   

      GLA_h     GOS_h     GRL_h     HAR_h     HDT_h     HEB_h     HER_h  \
0  0.008696  0.001739  0.206089  0.356525  0.002609  0.179132  0.349568   
1  0.023315  0.016859  0.669689  0.063848  0.069946  1.812860  0.150294   
2  0.020885  0.013583  0.378710  0.068206  0.009639  0.249601  2.228444   
3  0.202411  0.101205  0.172500  0.025814  0.009014  0.353195  0.867007   
4  0.007372  0.003686  0.127171  1.635719  0.003686  0.185228  0.132701   

      HGH_h     HNF_h     HOL_h     HOO_h     HVL_h     IND_h     INT_h  \
0  0.126088  0.008696  0.363481  0.744354  0.020000  0.001739  0.001739   
1  0.119805  0.068511  0.226697  0.054522  0.005739  0.020804  0.003228   
2  0.441074  0.008471  1.766193  0.091136  0.007010  0.003067  0.000730   
3  1.683616  0.010243  0.281081  0.035647  0.002458  0.004917  0.000819   
4  0.087546  0.024881  0.162190  1.619131  0.129014  0.002765  0.000922   

      KAY_h     KMS_h     KMT_h      LAY_h     LEH_h     LIN_h     MAP_h  \
0  4.500909  0.011304  0.515657  11.751407  0.472178  0.064348  0.046957   
1  0.164284  0.229567  0.203741   0.457340  0.442275  0.049859  0.075327   
2  0.761363  0.029356  2.312861   1.460801  1.794381  0.141961  0.130423   
3  0.196675  0.022126  0.340903   0.440469  6.573028  1.404174  1.387375   
4  0.822928  0.011980  0.232226   5.572501  0.333594  0.036861  0.056213   

      MID_h     MLC_h     MMT_h     MRG_h     MSL_h     MUR_h     MWY_h  \
0  0.316524  0.951313  0.467830  0.260002  0.104349  0.647832  0.037392   
1  0.158545  0.470253  0.160338  0.225262  0.017218  0.279426  0.435101   
2  2.179371  3.701367  1.845207  0.061049  0.019717  3.144913  0.076239   
3  0.405641  0.558884  0.250350  0.029911  0.011473  0.475297  0.124970   
4  0.159425  0.364927  0.158503  0.330830  0.485647  0.301341  0.046077   

      NOG_h     NSL_h      OGD_h     OKL_h      ORM_h     PAY_h     PGR_h  \
0  0.997400  1.986974   6.030487  0.006087   0.677397  0.160871  0.220871   
1  0.213425  0.099718   0.834332  0.123033   0.578939  0.210197  0.204458   
2  0.219222  0.750555   1.060475  0.016942   1.370541  0.292540  0.547253   
3  0.087684  0.097108   0.520778  0.015160  13.428775  2.573978  4.688640   

In [496]:
df_CountySum_wOutWF           .to_json(os.path.join(dirResults, "countydata_number.json"    ),orient='records')
df_CountySum_wOutWF_Percent_SA.to_json(os.path.join(dirResults, "countydata_percent_sa.json"),orient='records')
df_CountySum_wOutWF_Percent_MU.to_json(os.path.join(dirResults, "countydata_percent_mu.json"),orient='records')